# Project Five 
# Game of Thrones - Season Six

## Importing and Cleaning

In [1]:
import numpy as np
import pandas as pd
import nltk
from nltk.tag import pos_tag
from nltk.tokenize import word_tokenize
from nltk.tokenize import sent_tokenize
from textblob import TextBlob
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.decomposition import NMF, LatentDirichletAllocation
import gensim
from nltk.tag import pos_tag
import re

Using Theano backend.


In [2]:
pd.set_option('display.max_columns', 135)
pd.set_option('display.max_rows', 135)

In [3]:
df_s6 = pd.read_json('/Users/zoemarkovits/Metis/project_five_got/scrape/season_six.json')

In [4]:
df_s6[['title','script_text']]

title  \
0           [The Red Woman (Script)]   
1                    [Home (Script)]   
2             [Oathbreaker (Script)]   
3    [Book of the Stranger (Script)]   
4                [The Door (Script)]   
5       [Blood of My Blood (Script)]   
6          [The Broken Man (Script)]   
7                  [No One (Script)]   
8  [Battle of the Bastards (Script)]   
9     [The Winds of Winter (Script)]   

                                         script_text  
0  [\n, \n, CUT TO: CASTLE BLACK - DAVOS’ CHAMBER...  
1  [INT. GREAT WEIRWOOD TREE - CAVE, \n, \n, \n, ...  
2  [\n, \nDAVOS: Easy, easy,  Easy, \n, \n, \n, \...  
3  [INT. CASTLE BLACK - JON SNOW’S ROOM, \n, \n, ...  
4  [INT. CASTLE BLACK - SANSA’S ROOM, \n, \n, \n,...  
5  [\n, \nBRAN: Meera. They found us., \n, \n, \n...  
6  [\n, \nMAN: That’s it. Get it to the top., \n,...  
7  [ The Bloody Hand. , \n, \nLADY CRANE: My son....  
8  [\n, \nTYRION: Despite appearances, I think yo...  
9  [\n, \n, CUT TO: RED KEEP - TOMMEN’S CHAMBER, ...

In [5]:
df_s6['title'] = df_s6['title'].map(lambda x: str(x)[3:-11])

In [6]:
df_s6.title

0             The Red Woman
1                      Home
2               Oathbreaker
3      Book of the Stranger
4                  The Door
5         Blood of My Blood
6            The Broken Man
7                    No One
8    Battle of the Bastards
9       The Winds of Winter
Name: title, dtype: object

In [7]:
names6_01 = ['NIGHT’S WATCHMAN','DAVOS','DOLOROUS EDD','MELISANDRE','MALE VOICE #1','MALE VOICE #2','ALLISER THORNE',
             'NIGHT’S WATCHMEN #1','NIGHT’S WATCHMEN #2','RAMSAY','MAESTER WOLKAN','ROOSE','THEON','SANSA',
             'BOLTON OFFICER','BRIENNE','PODRICK','HANDMAIDEN','CERSEI','JAIME','SEPTA UNELLA','MARGAERY',
             'HIGH SPARROW','DORAN','ELLARIA','MAESTER','TRYSTANE','OBARA','NYMERIA','TYRION','VARYS','RED PRIEST',
             'DAARIO','JORAH','BLOODRIDER #1','BLOODRIDER #2','WIFE #1','WIFE #2','KHAL MORO','BLOODRIDER #3',
             'BLOODRIDER #4','DAENERYS','ARYA','WAIF','NIGHT’S WATCHMAN #1','NIGHT’S WATCHMAN #2']

names6_02 = ['YOUNG RODRICK','BRAN','YOUNG NED','THREE-EYED RAVEN','YOUNG BENJEN','YOUNG LYANNA','YOUNG HODOR','NAN',
             'HODOR','MEERA','CHILD OF THE FOREST','ALLISER THORNE','DAVOS','DOLOROUS EDD','TORMUND','STORYTELLER',
             'CERSEI','KING’S SOLDIER','TOMMEN','JAIME','HIGH SPARROW','TYRION','VARYS','GREY WORM','MISSANDEI',
             'WAIF','ARYA','JAQEN','LORD KARSTARK','ROOSE','RAMSAY','MAESTER WOLKAN','LADY WALDA','RAMSEY','BRIENNE',
             'SANSA','THEON','YARA','BALON','HOODED FIGURE','EURON','AERON','ALL','MELISANDRE']

names6_03 = ['DAVOS','JON SNOW','MELISANDRE','TORMUND','DOLOROUS EDD','GILLY','SAMWELL','BRAN','THREE-EYED RAVEN',
             'ARTHUR','NED','BLOODRIDER','DAENERYS','KHAL MORO','DOTHRAKI WOMAN','DOTHRAKI MATRON','VARYS','WOMAN',
             'VALA','TYRION','GREY WORM','MISSANDEI','QYBURN','ARTHUR','LITTLE BIRD','CERSEI','JAIME',
             'MAESTER PYCELLE','KEVAN','MACE TYRELL','LADY OLENNA','HIGH SPARROW','TOMMEN','WAIF','ARYA','JAQEN',
             'RAMSAY','LORD KARSTARK','SMALLJON','BOWEN MARSH','OTHELL YARWICK','ALLISER THRONE']

names6_04 = ['DOLOROUS EDD','JON SNOW','MAN','MAN #2','SANSA','DAVOS','MELISANDRE','BRIENNE','LITTLEFINGER','ROBIN',
             'YOHN ROYCE','TYRION','GREY WORM','MISSANDEI','YEZZAN','RAZDAL','BELICHO','MAN #1','MAN #2','DAARIO',
             'JORAH','DOTHRAKI #1','LEADER','LHAZAREEN WOMAN','DAENERYS','HIGH SPARROW','MARGAERY','LORAS',
             'MAESTER PYCELLE','CERSEI','TOMMEN','LADY OLENNA','JAIME','KEVAN','YARA','THEON','RAMSAY','OSHA','MAN',
             'TORMUND','KHAL MORO','KHAL #1','KHAL #2','KHAL #3','KHAL #4']

names6_05 = ['SANSA','MAN','LITTLEFINGER','BRIENNE','WAIF','ARYA','JAQEN','IZEMBARO','CLARENZO','LADYC RANE',
             'CAMELLO','BOBONO','LADY CRANE','BIANCA','BRAN','LEAF','AERON','YARA','MAN #1','ALL','MAN #2','THEON',
             'EURON','AERSON','DAENERYS','JORAH','VARYS','GREY WORM','TYRION','MISSANDEI','KINVARA',
             'THREE-EYED RAVEN','MEERA','HODOR','DAVOS','JON SNOW','DOLOROUS EDD','RICKARD','YOUNG NED','NAN',
             'YOUNG HODOR']

names6_06 = ['BRAN','MEERA','RIDER','GILLY','SAM','MELESSA','TALLA','TOMMEN','HIGH SPARROW','MARGAERY','DICKON',
             'RANDYLL','CLARENZO','ALL','BOBONO','LADY CRANE','IZEMBARO','CAMELLO','ARYA','BIANCA','WAIF','JAQEN',
             'MACE','JAIME','CAPTAIN','WOMAN','OLENNA','WALDER','BLACK WALDER','LOTHAR','CERSEI','BENJEN','DAARIO',
             'DAENERYS']

names6_07 = ['MAN','MAN #2','RAY','SANDOR','HIGH SPARROW','MARGAERY','OLENNA','DIM DALBA','TORMUND','JON SNOW',
             'WUN WUN','CERSEI','BRONN','JAIME','LOTHAR','BLACK WALDER','BRYNDEN','LYANNA','SANSA','DAVOS','ROBETT',
             'THEON','YARA','LEM','ARYA','WOMAN']

names6_08 = ['LADY CRANE','ARYA','MAN','GATINS','YOUNG MAN','YOUNG MAN #2','SANDOR','RED PRIESTESS','TYRION','VARYS',
             'QYBURN','CERSEI','LANCEL','PODRICK','BRIENNE','BRONN','JAIME','BRYNDEN','KEVAN','TOMMEN','CROWD',
             'MISSANDEI','GREY WORM','EDMURE','GUARD CAPTAIN','GUARD','BLACK WALDER','BERIC','THOROS','SANDOR',
             'LEM','WAIF','JAQEN']

names6_09 = ['TYRION','DAENERYS','RAZDAL','YEZZAN','GREY WORM','MISSANDEI','BELICHO','JON SNOW','SANSA','RAMSAY',
             'DAVOS','TORMUND','MELISANDRE','THEON','YARA','KARSTARK','SMALLJON','ALL','MAN','MAN #2']

names6_10 = ['ATTENDANT','MISTRESS','PYCELLE','GIRL','HIGH SPARROW','LORAS','MACE','MARGAERY','TOMMEN','LANCEL',
             'QYBURN','CERSEI','SEPTA UNELLA','WALDER','MEN','BRONN','JAIME','SAM','MAESTER','JON SNOW','MELISANDRE',
             'DAVOS','SANSA','OLENNA','ELLARIA','OBARA','NYMERIA','VARYS','DAARIO','DAENERYS','TYRION','HANDMAIDEN',
             'ARYA','PETYR','BENJEN','MEERA','BRAN','LYANNA','NED','VALE KNIGHT','TORMUND','MAN','MANDERLY','GLOVER',
             'ALL']

### Episode One

In [8]:
df_s6.script_text[0]

[u'\n',
 u'\n',
 u'CUT TO: CASTLE BLACK - DAVOS\u2019 CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\nNIGHT\u2019S WATCHMAN: It\u2019s the Lord Commander!',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAVOS: Help me get him inside',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: CASTLE BLACK - ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\nDOLOROUS EDD: Thorne did this',
 u'\n',
 u'\nDAVOS: How many of your brothers do you think you can trust?',
 u'\n',
 u'\nDOLOROUS EDD: Trust? The men in this room',
 u'\n',
 u'\nDAVOS: Does the wolf know you?',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAVOS: We need all the help we can get',
 u'\n',
 u'\n',
 u'\n',
 u'\nMELISANDRE (O.S.): Ser Davos',
 u'\n',
 u'\n',
 u'\n',
 u'\nMELISANDRE: I saw him in the flames, fighting at Winterfell',
 u'\n',
 u'\nDAVOS: I can\u2019t speak for the flames, but he\u2019s gone',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: CASTLE BLACK - MESS HALL',
 u'\n',
 u'\n',
 u'\n',
 u'\nMALE VOICE #1: He was our Lord Commander!',
 u'\n',
 u'\nMALE VOICE #2: He never should ha

In [9]:
script_text6_01 = df_s6.script_text[0]
print type(script_text6_01)

script_text6_01

<type 'list'>


[u'\n',
 u'\n',
 u'CUT TO: CASTLE BLACK - DAVOS\u2019 CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\nNIGHT\u2019S WATCHMAN: It\u2019s the Lord Commander!',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAVOS: Help me get him inside',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: CASTLE BLACK - ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\nDOLOROUS EDD: Thorne did this',
 u'\n',
 u'\nDAVOS: How many of your brothers do you think you can trust?',
 u'\n',
 u'\nDOLOROUS EDD: Trust? The men in this room',
 u'\n',
 u'\nDAVOS: Does the wolf know you?',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAVOS: We need all the help we can get',
 u'\n',
 u'\n',
 u'\n',
 u'\nMELISANDRE (O.S.): Ser Davos',
 u'\n',
 u'\n',
 u'\n',
 u'\nMELISANDRE: I saw him in the flames, fighting at Winterfell',
 u'\n',
 u'\nDAVOS: I can\u2019t speak for the flames, but he\u2019s gone',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: CASTLE BLACK - MESS HALL',
 u'\n',
 u'\n',
 u'\n',
 u'\nMALE VOICE #1: He was our Lord Commander!',
 u'\n',
 u'\nMALE VOICE #2: He never should ha

In [10]:
script_split = [i.split('\n') for i in script_text6_01]
script_split

[[u'', u''],
 [u'', u''],
 [u'CUT TO: CASTLE BLACK - DAVOS\u2019 CHAMBER'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'NIGHT\u2019S WATCHMAN: It\u2019s the Lord Commander!'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'DAVOS: Help me get him inside'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: CASTLE BLACK - ROOM'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'DOLOROUS EDD: Thorne did this'],
 [u'', u''],
 [u'', u'DAVOS: How many of your brothers do you think you can trust?'],
 [u'', u''],
 [u'', u'DOLOROUS EDD: Trust? The men in this room'],
 [u'', u''],
 [u'', u'DAVOS: Does the wolf know you?'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'DAVOS: We need all the help we can get'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'MELISANDRE (O.S.): Ser Davos'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'MELISANDRE: I saw him in the flames, fighting at Winterfell'],
 [u'', u''],
 [u'', u'DAVOS: I can\u2019t speak for the flames, but he\u2019s gon

In [11]:
string_script_text = ' '

for i in script_split:
    for e in i:
        string_script_text = string_script_text + ' ' + e

In [12]:
string_script_text

u'      CUT TO: CASTLE BLACK - DAVOS\u2019 CHAMBER        NIGHT\u2019S WATCHMAN: It\u2019s the Lord Commander!        DAVOS: Help me get him inside         CUT TO: CASTLE BLACK - ROOM        DOLOROUS EDD: Thorne did this    DAVOS: How many of your brothers do you think you can trust?    DOLOROUS EDD: Trust? The men in this room    DAVOS: Does the wolf know you?        DAVOS: We need all the help we can get        MELISANDRE (O.S.): Ser Davos        MELISANDRE: I saw him in the flames, fighting at Winterfell    DAVOS: I can\u2019t speak for the flames, but he\u2019s gone         CUT TO: CASTLE BLACK - MESS HALL        MALE VOICE #1: He was our Lord Commander!    MALE VOICE #2: He never should have been!        ALLISER THORNE: You all know why you\u2019re here  Jon Snow is dead    NIGHT\u2019S WATCHMAN #1: Who killed him?    ALLISER THORNE: I did        ALLISER THORNE: And Bowen Marsh and Othell Yarwyck and the other officers in this castle    NIGHT\u2019S WATCHMEN #1: Murderers!    NIGH

In [13]:
words = word_tokenize(string_script_text)
words

[u'CUT',
 u'TO',
 u':',
 u'CASTLE',
 u'BLACK',
 u'-',
 u'DAVOS\u2019',
 u'CHAMBER',
 u'NIGHT\u2019S',
 u'WATCHMAN',
 u':',
 u'It\u2019s',
 u'the',
 u'Lord',
 u'Commander',
 u'!',
 u'DAVOS',
 u':',
 u'Help',
 u'me',
 u'get',
 u'him',
 u'inside',
 u'CUT',
 u'TO',
 u':',
 u'CASTLE',
 u'BLACK',
 u'-',
 u'ROOM',
 u'DOLOROUS',
 u'EDD',
 u':',
 u'Thorne',
 u'did',
 u'this',
 u'DAVOS',
 u':',
 u'How',
 u'many',
 u'of',
 u'your',
 u'brothers',
 u'do',
 u'you',
 u'think',
 u'you',
 u'can',
 u'trust',
 u'?',
 u'DOLOROUS',
 u'EDD',
 u':',
 u'Trust',
 u'?',
 u'The',
 u'men',
 u'in',
 u'this',
 u'room',
 u'DAVOS',
 u':',
 u'Does',
 u'the',
 u'wolf',
 u'know',
 u'you',
 u'?',
 u'DAVOS',
 u':',
 u'We',
 u'need',
 u'all',
 u'the',
 u'help',
 u'we',
 u'can',
 u'get',
 u'MELISANDRE',
 u'(',
 u'O.S',
 u'.',
 u')',
 u':',
 u'Ser',
 u'Davos',
 u'MELISANDRE',
 u':',
 u'I',
 u'saw',
 u'him',
 u'in',
 u'the',
 u'flames',
 u',',
 u'fighting',
 u'at',
 u'Winterfell',
 u'DAVOS',
 u':',
 u'I',
 u'can\u2019t',
 u's

In [14]:
sentences = sent_tokenize(string_script_text)
sentences

[u'      CUT TO: CASTLE BLACK - DAVOS\u2019 CHAMBER        NIGHT\u2019S WATCHMAN: It\u2019s the Lord Commander!',
 u'DAVOS: Help me get him inside         CUT TO: CASTLE BLACK - ROOM        DOLOROUS EDD: Thorne did this    DAVOS: How many of your brothers do you think you can trust?',
 u'DOLOROUS EDD: Trust?',
 u'The men in this room    DAVOS: Does the wolf know you?',
 u'DAVOS: We need all the help we can get        MELISANDRE (O.S.',
 u'): Ser Davos        MELISANDRE: I saw him in the flames, fighting at Winterfell    DAVOS: I can\u2019t speak for the flames, but he\u2019s gone         CUT TO: CASTLE BLACK - MESS HALL        MALE VOICE #1: He was our Lord Commander!',
 u'MALE VOICE #2: He never should have been!',
 u'ALLISER THORNE: You all know why you\u2019re here  Jon Snow is dead    NIGHT\u2019S WATCHMAN #1: Who killed him?',
 u'ALLISER THORNE: I did        ALLISER THORNE: And Bowen Marsh and Othell Yarwyck and the other officers in this castle    NIGHT\u2019S WATCHMEN #1: Murder

In [15]:
dialogue = []

for sentence in sentences:
    if sentence.split(':')[0] in (names6_01):
        dialogue.append(sentence)

/Users/zoemarkovits/anaconda/lib/python2.7/site-packages/ipykernel_launcher.py:4: UnicodeWarning: Unicode equal comparison failed to convert both arguments to Unicode - interpreting them as being unequal
  after removing the cwd from sys.path.


In [16]:
dialogue

[u'DAVOS: Help me get him inside         CUT TO: CASTLE BLACK - ROOM        DOLOROUS EDD: Thorne did this    DAVOS: How many of your brothers do you think you can trust?',
 u'DOLOROUS EDD: Trust?',
 u'DAVOS: We need all the help we can get        MELISANDRE (O.S.',
 u'MALE VOICE #2: He never should have been!',
 u'ALLISER THORNE: You all know why you\u2019re here  Jon Snow is dead    NIGHT\u2019S WATCHMAN #1: Who killed him?',
 u'ALLISER THORNE: I did        ALLISER THORNE: And Bowen Marsh and Othell Yarwyck and the other officers in this castle    NIGHT\u2019S WATCHMEN #1: Murderers!',
 u'ALLISER THORNE: You\u2019re right!',
 u'ALLISER THORNE: We\u2019ve committed treason, all of us  Jon Snow was my Lord Commander  I had no love for him  That was no secret  But I never once disobeyed an order  Loyalty is the foundation on which the Night\u2019s Watch is built, and the Watch means everything to me  I have given my life, we have all given our lives to the Night\u2019s Watch  Jon Snow wa

In [17]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s601.pkl', 'wb') as f:
    pickle.dump(dialogue, f)

In [18]:
from collections import defaultdict

speakers = defaultdict(list)
for sentence in dialogue:
    speakers[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers

defaultdict(list,
            {u'ALLISER THORNE': [u' You all know why you\u2019re here  Jon Snow is dead    NIGHT\u2019S WATCHMAN #1',
              u' I did        ALLISER THORNE',
              u' You\u2019re right!',
              u' We\u2019ve committed treason, all of us  Jon Snow was my Lord Commander  I had no love for him  That was no secret  But I never once disobeyed an order  Loyalty is the foundation on which the Night\u2019s Watch is built, and the Watch means everything to me  I have given my life, we have all given our lives to the Night\u2019s Watch  Jon Snow was going to destroy the Night\u2019s Watch  He let the wildlings through our gates, as no Lord Commander has ever done before  He gave them the very land on which they reaved and raped and murdered  Lord Commander Snow did what he thought was right, I\u2019ve no doubt about that  And what he thought was right would have been the end of us  He thrust a terrible choice upon us, and we made it         CUT TO',
     

In [19]:
speakers['DAVOS']

[u' Help me get him inside         CUT TO',
 u' We need all the help we can get        MELISANDRE (O.S.',
 u' You\u2019re not the only ones who owe your lives to Jon Snow        DOLOROUS EDD',
 u' I\u2019m not much of a hunter  I\u2019ll need some food if I\u2019m gonna make it south without starving    ALLISER THORNE',
 u' You haven\u2019t seen her do what I\u2019ve seen her do     CUT TO']

In [20]:
episode_one = pd.DataFrame.from_dict(speakers, orient="index")
print episode_one.shape

(24, 6)


In [21]:
#from numpy import nan
#episode_one.fillna(value=str(0), inplace=True)

In [22]:
episode_one.info()

<class 'pandas.core.frame.DataFrame'>
Index: 24 entries, DAVOS to BLOODRIDER #2
Data columns (total 6 columns):
0    24 non-null object
1    8 non-null object
2    5 non-null object
3    5 non-null object
4    4 non-null object
5    1 non-null object
dtypes: object(6)
memory usage: 1.3+ KB


In [23]:
episode_one.head()

0  \
DAVOS                      Help me get him inside         CUT TO   
MALE VOICE #2                         He never should have been!   
JAIME                                           Mother    CERSEI   
TYRION          We’re never going to fix what’s wrong with th...   
WIFE #1         I told you she was a witch  Cut off her head ...   

                                                               1  \
DAVOS           We need all the help we can get        MELISA...   
MALE VOICE #2                                               None   
JAIME                                                       None   
TYRION          Hard to know  Our queen is not as popular in ...   
WIFE #1                                                     None   

                                                               2  \
DAVOS           You’re not the only ones who owe your lives t...   
MALE VOICE #2                                               None   
JAIME                                                       None   
TYRION          Very possibly  Daenerys Targaryen took away t...   
WIFE #1                                                     None   

                                                               3  \
DAVOS           I’m not much of a hunter  I’ll need some food...   
MALE VOICE #2                                               None   
JAIME                                                       None   
TYRION                              It’s a problem        TYRION   
WIFE #1                                                     None   

                                                               4     5  
DAVOS           You haven’t seen her do what I’ve seen her do...  None  
MALE VOICE #2                                               None  None  
JAIME                                                       None  None  
TYRION                                                      None  None  
WIFE #1                                                     None  None

In [24]:
def remove_stops(sentence):
    characters = ['?','!','.',',',':',';']
    stoplist = stopwords.words('english') + characters
    try: 
        new_sentence = re.sub(r'[^a-zA-Z ]','', sentence)
        new_sentence = new_sentence.lower()
        new_sentence = new_sentence.split()
        new_sentence = [word for word in new_sentence if word not in stoplist]
        new_sentence = ' '.join(new_sentence)
        return new_sentence
    except:
        return sentence   

In [25]:
test = episode_one[0].apply(remove_stops)
test

DAVOS                                           help get inside cut
MALE VOICE #2                                                 never
JAIME                                                 mother cersei
TYRION            never going fix whats wrong city top foot pyra...
WIFE #1                               told witch cut head khal moro
DOLOROUS EDD                                                  trust
RED PRIEST        lord light sent mother dragons love darkness c...
MAESTER WOLKAN                                 shall grave dug lord
DAENERYS          lie bear children anyone else sun rises west s...
DORAN             always envied oberyn lived truly lived sailed ...
ROOSE             rebelled crown arrange marriage sansa stark th...
MAESTER                                                prince doran
THEON                                           dead bolton officer
CERSEI                          think locking myrcella crypt cersei
VARYS             walk though paving stones pers

In [26]:
for column in episode_one.columns:
    for x in range(len(episode_one[column])):
        episode_one[column][x] = remove_stops(episode_one[column][x])

In [27]:
episode_one.info()

<class 'pandas.core.frame.DataFrame'>
Index: 24 entries, DAVOS to BLOODRIDER #2
Data columns (total 6 columns):
0    24 non-null object
1    8 non-null object
2    5 non-null object
3    5 non-null object
4    4 non-null object
5    1 non-null object
dtypes: object(6)
memory usage: 1.3+ KB


In [28]:
episode_one.index = episode_one.index.str.title()

In [29]:
episode_one.head()

0  \
Davos                                        help get inside cut   
Male Voice #2                                              never   
Jaime                                              mother cersei   
Tyrion         never going fix whats wrong city top foot pyra...   
Wife #1                            told witch cut head khal moro   

                                                        1  \
Davos                         need help get melisandre os   
Male Voice #2                                        None   
Jaime                                                None   
Tyrion         hard know queen popular meereen used varys   
Wife #1                                              None   

                                                               2  \
Davos                 youre ones owe lives jon snow dolorous edd   
Male Voice #2                                               None   
Jaime                                                       None   
Tyrion         possibly daenerys targaryen took away valuable...   
Wife #1                                                     None   

                                                               3  \
Davos          im much hunter ill need food im gonna make sou...   
Male Voice #2                                               None   
Jaime                                                       None   
Tyrion                                            problem tyrion   
Wife #1                                                     None   

                                      4     5  
Davos          havent seen ive seen cut  None  
Male Voice #2                      None  None  
Jaime                              None  None  
Tyrion                             None  None  
Wife #1                            None  None

### Episode Two

In [30]:
df_s6.script_text[1]

[u'INT. GREAT WEIRWOOD TREE - CAVE',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nBRAN (to THREE-EYED RAVEN): That\u2019s my father. And my Uncle Benjen',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nBRAN: They were all so happy',
 u'\n',
 u'\nTHREE-EYED RAVEN: So were you once',
 u'\n',
 u'\n',
 u'\n',
 u'\nYOUNG NED: Stop showing off',
 u'\n',
 u'\nYOUNG BENJEN: Lyanna!',
 u'\n',
 u'\nBRAN: My Aunt Lyanna',
 u' I\u2019ve seen her statue in the crypt',
 u' My father never talked about her',
 u'\n',
 u'\n',
 u'\n',
 u'\nYOUNG BENJEN: Would you get out of here? We\u2019re sparring',
 u'\n',
 u'\nYOUNG LYANNA: Who are you gonna spar with when Ned goes off to the Eyrie?',
 u'\n',
 u'\nYOUNG BENJEN: I don\u2019t know',
 u'\n',
 u'\n',
 u'\n',
 u'\nYOUNG LYANNA: What about him?',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nBRAN: Hodor?',
 u'\n',
 u'\n',
 u'\n',
 u'\nYOUNG BENJEN: But he\u2019s got giant\u2019s blood',
 u'\n',
 u'\nYOUNG NED: 

In [31]:
script_text6_02 = df_s6.script_text[1]
print type(script_text6_02)

script_text6_02

<type 'list'>


[u'INT. GREAT WEIRWOOD TREE - CAVE',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nBRAN (to THREE-EYED RAVEN): That\u2019s my father. And my Uncle Benjen',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nBRAN: They were all so happy',
 u'\n',
 u'\nTHREE-EYED RAVEN: So were you once',
 u'\n',
 u'\n',
 u'\n',
 u'\nYOUNG NED: Stop showing off',
 u'\n',
 u'\nYOUNG BENJEN: Lyanna!',
 u'\n',
 u'\nBRAN: My Aunt Lyanna',
 u' I\u2019ve seen her statue in the crypt',
 u' My father never talked about her',
 u'\n',
 u'\n',
 u'\n',
 u'\nYOUNG BENJEN: Would you get out of here? We\u2019re sparring',
 u'\n',
 u'\nYOUNG LYANNA: Who are you gonna spar with when Ned goes off to the Eyrie?',
 u'\n',
 u'\nYOUNG BENJEN: I don\u2019t know',
 u'\n',
 u'\n',
 u'\n',
 u'\nYOUNG LYANNA: What about him?',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nBRAN: Hodor?',
 u'\n',
 u'\n',
 u'\n',
 u'\nYOUNG BENJEN: But he\u2019s got giant\u2019s blood',
 u'\n',
 u'\nYOUNG NED: 

In [32]:
script_split2 = [i.split('\n') for i in script_text6_02]
script_split2

[[u'INT. GREAT WEIRWOOD TREE - CAVE'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'',
  u'BRAN (to THREE-EYED RAVEN): That\u2019s my father. And my Uncle Benjen'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'BRAN: They were all so happy'],
 [u'', u''],
 [u'', u'THREE-EYED RAVEN: So were you once'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'YOUNG NED: Stop showing off'],
 [u'', u''],
 [u'', u'YOUNG BENJEN: Lyanna!'],
 [u'', u''],
 [u'', u'BRAN: My Aunt Lyanna'],
 [u' I\u2019ve seen her statue in the crypt'],
 [u' My father never talked about her'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'YOUNG BENJEN: Would you get out of here? We\u2019re sparring'],
 [u'', u''],
 [u'',
  u'YOUNG LYANNA: Who are you gonna spar with when Ned goes off to the Eyrie?'],
 [u'', u''],
 [u'', u'YOUNG BENJEN: I don\u2019t know'],
 [u'', u''],
 [u'', u''],
 [u'', u'']

In [33]:
string_script_text2 = ' '

for i in script_split2:
    for e in i:
        string_script_text2 = string_script_text2 + ' ' + e

In [34]:
string_script_text2

u"  INT. GREAT WEIRWOOD TREE - CAVE                        BRAN (to THREE-EYED RAVEN): That\u2019s my father. And my Uncle Benjen            BRAN: They were all so happy    THREE-EYED RAVEN: So were you once        YOUNG NED: Stop showing off    YOUNG BENJEN: Lyanna!    BRAN: My Aunt Lyanna  I\u2019ve seen her statue in the crypt  My father never talked about her        YOUNG BENJEN: Would you get out of here? We\u2019re sparring    YOUNG LYANNA: Who are you gonna spar with when Ned goes off to the Eyrie?    YOUNG BENJEN: I don\u2019t know        YOUNG LYANNA: What about him?            BRAN: Hodor?        YOUNG BENJEN: But he\u2019s got giant\u2019s blood    YOUNG NED: And you\u2019ve got training  Sounds like a fair match to me    YOUNG LYANNA: Benjen always lifts his chin when he\u2019s about to charge        YOUNG HODOR: And lowers it when he\u2019s going to dodge, my lady    BRAN: Hodor talks?        NAN: You leave the fighting to the little lords, Wylis  Come along, now  It\u2019

In [35]:
words2 = word_tokenize(string_script_text2)
words2

[u'INT',
 u'.',
 u'GREAT',
 u'WEIRWOOD',
 u'TREE',
 u'-',
 u'CAVE',
 u'BRAN',
 u'(',
 u'to',
 u'THREE-EYED',
 u'RAVEN',
 u')',
 u':',
 u'That\u2019s',
 u'my',
 u'father',
 u'.',
 u'And',
 u'my',
 u'Uncle',
 u'Benjen',
 u'BRAN',
 u':',
 u'They',
 u'were',
 u'all',
 u'so',
 u'happy',
 u'THREE-EYED',
 u'RAVEN',
 u':',
 u'So',
 u'were',
 u'you',
 u'once',
 u'YOUNG',
 u'NED',
 u':',
 u'Stop',
 u'showing',
 u'off',
 u'YOUNG',
 u'BENJEN',
 u':',
 u'Lyanna',
 u'!',
 u'BRAN',
 u':',
 u'My',
 u'Aunt',
 u'Lyanna',
 u'I\u2019ve',
 u'seen',
 u'her',
 u'statue',
 u'in',
 u'the',
 u'crypt',
 u'My',
 u'father',
 u'never',
 u'talked',
 u'about',
 u'her',
 u'YOUNG',
 u'BENJEN',
 u':',
 u'Would',
 u'you',
 u'get',
 u'out',
 u'of',
 u'here',
 u'?',
 u'We\u2019re',
 u'sparring',
 u'YOUNG',
 u'LYANNA',
 u':',
 u'Who',
 u'are',
 u'you',
 u'gon',
 u'na',
 u'spar',
 u'with',
 u'when',
 u'Ned',
 u'goes',
 u'off',
 u'to',
 u'the',
 u'Eyrie',
 u'?',
 u'YOUNG',
 u'BENJEN',
 u':',
 u'I',
 u'don\u2019t',
 u'know',
 

In [36]:
sentences2 = sent_tokenize(string_script_text2)
sentences2

[u'  INT.',
 u'GREAT WEIRWOOD TREE - CAVE                        BRAN (to THREE-EYED RAVEN): That\u2019s my father.',
 u'And my Uncle Benjen            BRAN: They were all so happy    THREE-EYED RAVEN: So were you once        YOUNG NED: Stop showing off    YOUNG BENJEN: Lyanna!',
 u'BRAN: My Aunt Lyanna  I\u2019ve seen her statue in the crypt  My father never talked about her        YOUNG BENJEN: Would you get out of here?',
 u'We\u2019re sparring    YOUNG LYANNA: Who are you gonna spar with when Ned goes off to the Eyrie?',
 u'YOUNG BENJEN: I don\u2019t know        YOUNG LYANNA: What about him?',
 u'BRAN: Hodor?',
 u'YOUNG BENJEN: But he\u2019s got giant\u2019s blood    YOUNG NED: And you\u2019ve got training  Sounds like a fair match to me    YOUNG LYANNA: Benjen always lifts his chin when he\u2019s about to charge        YOUNG HODOR: And lowers it when he\u2019s going to dodge, my lady    BRAN: Hodor talks?',
 u'NAN: You leave the fighting to the little lords, Wylis  Come along, now

In [37]:
dialogue2 = []

for sentence in sentences2:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names6_02):
            dialogue2.append(sentence)

/Users/zoemarkovits/anaconda/lib/python2.7/site-packages/ipykernel_launcher.py:6: UnicodeWarning: Unicode equal comparison failed to convert both arguments to Unicode - interpreting them as being unequal
  


In [38]:
dialogue2

[u'BRAN: My Aunt Lyanna  I\u2019ve seen her statue in the crypt  My father never talked about her        YOUNG BENJEN: Would you get out of here?',
 u'YOUNG BENJEN: I don\u2019t know        YOUNG LYANNA: What about him?',
 u'BRAN: Hodor?',
 u'YOUNG BENJEN: But he\u2019s got giant\u2019s blood    YOUNG NED: And you\u2019ve got training  Sounds like a fair match to me    YOUNG LYANNA: Benjen always lifts his chin when he\u2019s about to charge        YOUNG HODOR: And lowers it when he\u2019s going to dodge, my lady    BRAN: Hodor talks?',
 u'NAN: You leave the fighting to the little lords, Wylis  Come along, now  It\u2019s no place for you        YOUNG NED: Oh, Nan, look at the size of him  If he ever learned to fight, he\u2019d be unstoppable    NAN: Well, he\u2019s never going to learn to fight because he\u2019s a stable boy.',
 u'HODOR: Hodor    BRAN: Where\u2019s Meera?',
 u'HODOR: Hodor        BRAN: You shouldn\u2019t be here  It\u2019s not safe outside the cave    MEERA: It\u2019s 

In [39]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s602.pkl', 'wb') as f:
    pickle.dump(dialogue2, f)

In [40]:
from collections import defaultdict

speakers2 = defaultdict(list)
for sentence in dialogue2:
    speakers2[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers2

defaultdict(list,
            {u'ALLISER THORNE': [u' Fight, you cowards!'],
             u'ARYA': [u' No one    WAIF', u' No one    JAQEN'],
             u'BALON': [u' I thought you\u2019d be rotting under some foreign sea by now    EURON',
              u' You can mock our god without my help    EURON'],
             u'BRAN': [u' My Aunt Lyanna  I\u2019ve seen her statue in the crypt  My father never talked about her        YOUNG BENJEN',
              u' Hodor?',
              u' The Three-Eyed Raven says there\u2019s a war coming    MEERA'],
             u'HIGH SPARROW': [u' You would spill blood in this holy place?'],
             u'HODOR': [u' Hodor    BRAN', u' Hodor        BRAN'],
             u'HOODED FIGURE': [u' Haven\u2019t I always, brother?'],
             u'JAIME': [u' We all fail sometimes    TOMMEN',
              u' Go and see your mother and ask her to forgive you        HIGH SPARROW',
              u' I broke a sacred oath and stabbed my king in the back  I killed m

In [41]:
speakers2['TYRION']

[u' Dragons do not do well in captivity    MISSANDEI',
 u' That\u2019s what I do  I drink and I know things        TYRION',
 u' They will  It\u2019s time they had their supper     CUT TO']

In [42]:
episode_two = pd.DataFrame.from_dict(speakers2, orient="index")
print episode_two.shape

(19, 4)


In [43]:
#from numpy import nan
#episode_two.fillna(value=str(0), inplace=True)

In [44]:
episode_two.info()

<class 'pandas.core.frame.DataFrame'>
Index: 19 entries, YOUNG BENJEN to RAMSAY
Data columns (total 4 columns):
0    19 non-null object
1    12 non-null object
2    5 non-null object
3    1 non-null object
dtypes: object(4)
memory usage: 760.0+ bytes


In [45]:
episode_two.head()

0  \
YOUNG BENJEN                   I don’t know        YOUNG LYANNA   
THEON          I would have taken you all the way to the Wal...   
JAIME                           We all fail sometimes    TOMMEN   
ROOSE              Jon Snow is a bastard, not a Stark    RAMSAY   
TOMMEN                                   Of course not    JAIME   

                                                              1  \
YOUNG BENJEN            But he’s got giant’s blood    YOUNG NED   
THEON                                             Home     EXT.   
JAIME          Go and see your mother and ask her to forgive...   
ROOSE                                                      None   
TOMMEN         When the Faith Militant seized her and Margae...   

                                                              2  \
YOUNG BENJEN                                               None   
THEON                                                      None   
JAIME          I broke a sacred oath and stabbed my king in ...   
ROOSE                                                      None   
TOMMEN                                           Gold    CERSEI   

                                                              3  
YOUNG BENJEN                                               None  
THEON                                                      None  
JAIME          Oh, the gods won’t mind  They’ve spilled more...  
ROOSE                                                      None  
TOMMEN                                                     None

In [46]:
test2 = episode_two[0].apply(remove_stops)
test2

YOUNG BENJEN                                 dont know young lyanna
THEON                     would taken way wall would died get theon
JAIME                                         fail sometimes tommen
ROOSE                                 jon snow bastard stark ramsay
TOMMEN                                                 course jaime
SANSA                                                            go
NAN               leave fighting little lords wylis come along p...
WAIF                                                     whats name
BRAN              aunt lyanna ive seen statue crypt father never...
HODOR                                                    hodor bran
MELISANDRE                                             asking davos
HOODED FIGURE                                 havent always brother
TYRION                             dragons well captivity missandei
HIGH SPARROW                           would spill blood holy place
BALON                        thought youd rottin

In [47]:
for column in episode_two.columns:
    for x in range(len(episode_two[column])):
        episode_two[column][x] = remove_stops(episode_two[column][x])

In [48]:
episode_two.info()

<class 'pandas.core.frame.DataFrame'>
Index: 19 entries, YOUNG BENJEN to RAMSAY
Data columns (total 4 columns):
0    19 non-null object
1    12 non-null object
2    5 non-null object
3    1 non-null object
dtypes: object(4)
memory usage: 760.0+ bytes


In [49]:
episode_two.index = episode_two.index.str.title()

In [50]:
episode_two.head()

0  \
Young Benjen                     dont know young lyanna   
Theon         would taken way wall would died get theon   
Jaime                             fail sometimes tommen   
Roose                     jon snow bastard stark ramsay   
Tommen                                     course jaime   

                                                   1  \
Young Benjen          hes got giants blood young ned   
Theon                                       home ext   
Jaime         go see mother ask forgive high sparrow   
Roose                                           None   
Tommen                faith militant seized margaery   

                                                              2  \
Young Benjen                                               None   
Theon                                                      None   
Jaime         broke sacred oath stabbed king back killed cou...   
Roose                                                      None   
Tommen                                              gold cersei   

                                                              3  
Young Benjen                                               None  
Theon                                                      None  
Jaime         oh gods wont mind theyve spilled blood rest us...  
Roose                                                      None  
Tommen                                                     None

### Episode Three

In [51]:
df_s6.script_text[2]

[u'\n',
 u'\nDAVOS: Easy, easy',
 u' Easy',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAVOS: What do you remember?',
 u'\n',
 u'\nJON SNOW: They stabbed me',
 u' Olly...he put a knife in my heart',
 u' I shouldn\u2019t be here',
 u'\n',
 u'\nDAVOS: The lady brought you back.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nMELISANDRE: The Lord let you come back for a reason',
 u' Stannis was not the prince who was promised, but someone has to be',
 u'\n',
 u'\nDAVOS (to MELISANDRE): Could you give us a moment?',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAVOS: You were dead',
 u' And now you\u2019re not',
 u' That\u2019s completely fucking mad, seems to me',
 u' I can only imagine how it seems to you',
 u'\n',
 u'\nJON SNOW: I did what I thought was right',
 u' And I got murdered for it',
 u' And now I\u2019m back',
 u' Why?',
 u'\n',
 u'\nDAVOS: I don\u2019t know',
 u' Maybe we\u2019ll never know',
 u' What does it matter? You go on',
 u' You fight for as long as you can',
 u' You clean up as much of the shit as

In [52]:
script_text6_03 = df_s6.script_text[2]
print type(script_text6_03)

script_text6_03

<type 'list'>


[u'\n',
 u'\nDAVOS: Easy, easy',
 u' Easy',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAVOS: What do you remember?',
 u'\n',
 u'\nJON SNOW: They stabbed me',
 u' Olly...he put a knife in my heart',
 u' I shouldn\u2019t be here',
 u'\n',
 u'\nDAVOS: The lady brought you back.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nMELISANDRE: The Lord let you come back for a reason',
 u' Stannis was not the prince who was promised, but someone has to be',
 u'\n',
 u'\nDAVOS (to MELISANDRE): Could you give us a moment?',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAVOS: You were dead',
 u' And now you\u2019re not',
 u' That\u2019s completely fucking mad, seems to me',
 u' I can only imagine how it seems to you',
 u'\n',
 u'\nJON SNOW: I did what I thought was right',
 u' And I got murdered for it',
 u' And now I\u2019m back',
 u' Why?',
 u'\n',
 u'\nDAVOS: I don\u2019t know',
 u' Maybe we\u2019ll never know',
 u' What does it matter? You go on',
 u' You fight for as long as you can',
 u' You clean up as much of the shit as

In [53]:
script_split3 = [i.split('\n') for i in script_text6_03]
script_split3

[[u'', u''],
 [u'', u'DAVOS: Easy, easy'],
 [u' Easy'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'DAVOS: What do you remember?'],
 [u'', u''],
 [u'', u'JON SNOW: They stabbed me'],
 [u' Olly...he put a knife in my heart'],
 [u' I shouldn\u2019t be here'],
 [u'', u''],
 [u'', u'DAVOS: The lady brought you back.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'MELISANDRE: The Lord let you come back for a reason'],
 [u' Stannis was not the prince who was promised, but someone has to be'],
 [u'', u''],
 [u'', u'DAVOS (to MELISANDRE): Could you give us a moment?'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'DAVOS: You were dead'],
 [u' And now you\u2019re not'],
 [u' That\u2019s completely fucking mad, seems to me'],
 [u' I can only imagine how it seems to you'],
 [u'', u''],
 [u'', u'JON SNOW: I did what I thought was right'],
 [u' And I got murdered for it'],
 [u' And now I\u2019m back'],
 [u' Why?'],
 [u'', u''],
 [u'', u'DAVOS: I don\u2019t know'],

In [54]:
string_script_text3 = ' '

for i in script_split3:
    for e in i:
        string_script_text3 = string_script_text3 + ' ' + e

In [55]:
string_script_text3

u"     DAVOS: Easy, easy  Easy        DAVOS: What do you remember?    JON SNOW: They stabbed me  Olly...he put a knife in my heart  I shouldn\u2019t be here    DAVOS: The lady brought you back.            MELISANDRE: The Lord let you come back for a reason  Stannis was not the prince who was promised, but someone has to be    DAVOS (to MELISANDRE): Could you give us a moment?        DAVOS: You were dead  And now you\u2019re not  That\u2019s completely fucking mad, seems to me  I can only imagine how it seems to you    JON SNOW: I did what I thought was right  And I got murdered for it  And now I\u2019m back  Why?    DAVOS: I don\u2019t know  Maybe we\u2019ll never know  What does it matter? You go on  You fight for as long as you can  You clean up as much of the shit as you can    JON SNOW: I don\u2019t know how to do that  I thought I did, but...I failed    DAVOS: Good  Now go fail again     CUT TO: CASTLE BLACK - COURTYARD        TORMUND: They think you\u2019re some kind of god  The 

In [56]:
words3 = word_tokenize(string_script_text3)
words3

[u'DAVOS',
 u':',
 u'Easy',
 u',',
 u'easy',
 u'Easy',
 u'DAVOS',
 u':',
 u'What',
 u'do',
 u'you',
 u'remember',
 u'?',
 u'JON',
 u'SNOW',
 u':',
 u'They',
 u'stabbed',
 u'me',
 u'Olly',
 u'...',
 u'he',
 u'put',
 u'a',
 u'knife',
 u'in',
 u'my',
 u'heart',
 u'I',
 u'shouldn\u2019t',
 u'be',
 u'here',
 u'DAVOS',
 u':',
 u'The',
 u'lady',
 u'brought',
 u'you',
 u'back',
 u'.',
 u'MELISANDRE',
 u':',
 u'The',
 u'Lord',
 u'let',
 u'you',
 u'come',
 u'back',
 u'for',
 u'a',
 u'reason',
 u'Stannis',
 u'was',
 u'not',
 u'the',
 u'prince',
 u'who',
 u'was',
 u'promised',
 u',',
 u'but',
 u'someone',
 u'has',
 u'to',
 u'be',
 u'DAVOS',
 u'(',
 u'to',
 u'MELISANDRE',
 u')',
 u':',
 u'Could',
 u'you',
 u'give',
 u'us',
 u'a',
 u'moment',
 u'?',
 u'DAVOS',
 u':',
 u'You',
 u'were',
 u'dead',
 u'And',
 u'now',
 u'you\u2019re',
 u'not',
 u'That\u2019s',
 u'completely',
 u'fucking',
 u'mad',
 u',',
 u'seems',
 u'to',
 u'me',
 u'I',
 u'can',
 u'only',
 u'imagine',
 u'how',
 u'it',
 u'seems',
 u'to',

In [57]:
sentences3 = sent_tokenize(string_script_text3)
sentences3

[u'     DAVOS: Easy, easy  Easy        DAVOS: What do you remember?',
 u'JON SNOW: They stabbed me  Olly...he put a knife in my heart  I shouldn\u2019t be here    DAVOS: The lady brought you back.',
 u'MELISANDRE: The Lord let you come back for a reason  Stannis was not the prince who was promised, but someone has to be    DAVOS (to MELISANDRE): Could you give us a moment?',
 u'DAVOS: You were dead  And now you\u2019re not  That\u2019s completely fucking mad, seems to me  I can only imagine how it seems to you    JON SNOW: I did what I thought was right  And I got murdered for it  And now I\u2019m back  Why?',
 u'DAVOS: I don\u2019t know  Maybe we\u2019ll never know  What does it matter?',
 u'You go on  You fight for as long as you can  You clean up as much of the shit as you can    JON SNOW: I don\u2019t know how to do that  I thought I did, but...I failed    DAVOS: Good  Now go fail again     CUT TO: CASTLE BLACK - COURTYARD        TORMUND: They think you\u2019re some kind of god  Th

In [58]:
dialogue3 = []

for sentence in sentences3:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names6_03):
            dialogue3.append(sentence)

In [59]:
dialogue3

[u'JON SNOW: They stabbed me  Olly...he put a knife in my heart  I shouldn\u2019t be here    DAVOS: The lady brought you back.',
 u'MELISANDRE: The Lord let you come back for a reason  Stannis was not the prince who was promised, but someone has to be    DAVOS (to MELISANDRE): Could you give us a moment?',
 u'DAVOS: You were dead  And now you\u2019re not  That\u2019s completely fucking mad, seems to me  I can only imagine how it seems to you    JON SNOW: I did what I thought was right  And I got murdered for it  And now I\u2019m back  Why?',
 u'DAVOS: I don\u2019t know  Maybe we\u2019ll never know  What does it matter?',
 u'DOLOROUS EDD: Your eyes are still brown  Is that still you in there?',
 u'JON SNOW: I think so  Hold off on burning my body for now        DOLOROUS EDD: That\u2019s funny  You sure that\u2019s still you in there?',
 u'SAMWELL: Yes  Yes, I\u2019m fine    GILLY: Did I ever tell you I used to think the sea was called the see because it was nothing but water as far as t

In [60]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s603.pkl', 'wb') as f:
    pickle.dump(dialogue3, f)

In [61]:
from collections import defaultdict

speakers3 = defaultdict(list)
for sentence in dialogue3:
    speakers3[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers3

defaultdict(list,
            {u'ARTHUR': [u' Our prince wanted us here    NED',
              u' I wish you good fortune in the wars to come        ARTHUR',
              u' Better    QYBURN',
              u' No one\u2019s seen him    QYBURN'],
             u'ARYA': [u' No one     EXT.'],
             u'BRAN': [u' Ser Arthur Dayne    THREE-EYED RAVEN',
              u' I know he did  Heard the story a thousand times        BRAN',
              u' So why did you?'],
             u'CERSEI': [u' Not yet    JAIME'],
             u'DAVOS': [u' You were dead  And now you\u2019re not  That\u2019s completely fucking mad, seems to me  I can only imagine how it seems to you    JON SNOW',
              u' I don\u2019t know  Maybe we\u2019ll never know  What does it matter?'],
             u'DOLOROUS EDD': [u' Your eyes are still brown  Is that still you in there?'],
             u'GILLY': [u' Won\u2019t be long  We\u2019ll be in the south soon  I\u2019m excited to see Oldtown  Captain says it\u

In [62]:
speakers3['JON SNOW']

[u' They stabbed me  Olly...he put a knife in my heart  I shouldn\u2019t be here    DAVOS',
 u' I think so  Hold off on burning my body for now        DOLOROUS EDD',
 u' Wear it  Burn it  Whatever you want  You have Castle Black                 CREDITS']

In [63]:
episode_three = pd.DataFrame.from_dict(speakers3, orient="index")
print episode_three.shape

(22, 4)


In [64]:
#from numpy import nan
#episode_three.fillna(value=str(0), inplace=True)

In [65]:
episode_three.info()

<class 'pandas.core.frame.DataFrame'>
Index: 22 entries, DAVOS to MAESTER PYCELLE
Data columns (total 4 columns):
0    22 non-null object
1    13 non-null object
2    9 non-null object
3    4 non-null object
dtypes: object(4)
memory usage: 880.0+ bytes


In [66]:
episode_three.head()

0  \
DAVOS        You were dead  And now you’re not  That’s com...   
MELISANDRE   The Lord let you come back for a reason  Stan...   
SMALLJON     The bastard Jon Snow led an army of wildlings...   
GILLY        Won’t be long  We’ll be in the south soon  I’...   
JAIME        The same women who murdered Myrcella have ove...   

                                                            1  \
DAVOS        I don’t know  Maybe we’ll never know  What do...   
MELISANDRE                                               None   
SMALLJON     We need to help each other   The colder it ge...   
GILLY        So if we’re not going to Oldtown, where are y...   
JAIME                                                    None   

                                                            2  \
DAVOS                                                    None   
MELISANDRE                                               None   
SMALLJON     Your father honored tradition  Knelt for Robb...   
GILLY                                                    None   
JAIME                                                    None   

                                  3  
DAVOS                          None  
MELISANDRE                     None  
SMALLJON     Rickon Stark    RAMSAY  
GILLY                          None  
JAIME                          None

In [67]:
test3 = episode_three[0].apply(remove_stops)
test3

DAVOS               dead youre thats completely fucking mad seems ...
MELISANDRE          lord let come back reason stannis prince promi...
SMALLJON            bastard jon snow led army wildlings past wall ...
GILLY               wont long well south soon im excited see oldto...
JAIME               women murdered myrcella overthrown house marte...
THREE-EYED RAVEN    thats enough one day well visit another time bran
TYRION                      right conversations lets play game tyrion
MISSANDEI           cannot masters speak one language spoke many y...
DOLOROUS EDD                                   eyes still brown still
SAMWELL                                         yes yes im fine gilly
ARTHUR                                           prince wanted us ned
GREY WORM           patrol going patrol unsullied see patrol captu...
CERSEI                                                      yet jaime
VARYS               thats right know youve done youve done lot you...
QYBURN              

In [68]:
for column in episode_three.columns:
    for x in range(len(episode_three[column])):
        episode_three[column][x] = remove_stops(episode_three[column][x])

In [69]:
episode_three.info()

<class 'pandas.core.frame.DataFrame'>
Index: 22 entries, DAVOS to MAESTER PYCELLE
Data columns (total 4 columns):
0    22 non-null object
1    13 non-null object
2    9 non-null object
3    4 non-null object
dtypes: object(4)
memory usage: 880.0+ bytes


In [70]:
episode_three.index = episode_three.index.str.title()

In [71]:
episode_three.head()

0  \
Davos       dead youre thats completely fucking mad seems ...   
Melisandre  lord let come back reason stannis prince promi...   
Smalljon    bastard jon snow led army wildlings past wall ...   
Gilly       wont long well south soon im excited see oldto...   
Jaime       women murdered myrcella overthrown house marte...   

                                                            1  \
Davos                  dont know maybe well never know matter   
Melisandre                                               None   
Smalljon    need help colder gets farther south goat fucke...   
Gilly                                    going oldtown taking   
Jaime                                                    None   

                                                            2  \
Davos                                                    None   
Melisandre                                               None   
Smalljon    father honored tradition knelt robb stark call...   
Gilly                                                    None   
Jaime                                                    None   

                              3  
Davos                      None  
Melisandre                 None  
Smalljon    rickon stark ramsay  
Gilly                      None  
Jaime                      None

### Episode Four

In [72]:
df_s6.script_text[3]

[u'INT. CASTLE BLACK - JON SNOW\u2019S ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\nDOLOROUS EDD: Where you gonna go?',
 u'\n',
 u'\nJON SNOW: South',
 u'\n',
 u'\nDOLOROUS EDD: What are you gonna do?',
 u'\n',
 u'\nJON SNOW: Get warm',
 u'\n',
 u'\n',
 u'\n',
 u'\nDOLOROUS EDD: I was with you at Hardhome',
 u' We saw what\u2019s out there',
 u' We know it\u2019s coming here',
 u' How can you leave us now?',
 u'\n',
 u'\nJON SNOW: I did everything I could',
 u' You know that',
 u'\n',
 u'\nDOLOROUS EDD: You swore a vow',
 u'\n',
 u'\nJON SNOW: Aye, I pledged my life to the Night\u2019s Watch',
 u' I gave my life',
 u'\n',
 u'\nDOLOROUS EDD: For all nights to come',
 u'\n',
 u'\nJON SNOW: They killed me, Edd! My own brothers',
 u' You want me to stay here after that?',
 u'\n',
 u'\n',
 u'\n',
 u'\nMAN (O.S.): Riders approaching!',
 u'\n',
 u'\nMAN #2 (O.S.): Open the gate!',
 u'\n',
 u'\n',
 u'CUT TO: CASTLE BLACK - COURTYARD',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: CASTLE BLACK - JON SNOW\u

In [73]:
script_text6_04 = df_s6.script_text[3]
print type(script_text6_04)

script_text6_04

<type 'list'>


[u'INT. CASTLE BLACK - JON SNOW\u2019S ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\nDOLOROUS EDD: Where you gonna go?',
 u'\n',
 u'\nJON SNOW: South',
 u'\n',
 u'\nDOLOROUS EDD: What are you gonna do?',
 u'\n',
 u'\nJON SNOW: Get warm',
 u'\n',
 u'\n',
 u'\n',
 u'\nDOLOROUS EDD: I was with you at Hardhome',
 u' We saw what\u2019s out there',
 u' We know it\u2019s coming here',
 u' How can you leave us now?',
 u'\n',
 u'\nJON SNOW: I did everything I could',
 u' You know that',
 u'\n',
 u'\nDOLOROUS EDD: You swore a vow',
 u'\n',
 u'\nJON SNOW: Aye, I pledged my life to the Night\u2019s Watch',
 u' I gave my life',
 u'\n',
 u'\nDOLOROUS EDD: For all nights to come',
 u'\n',
 u'\nJON SNOW: They killed me, Edd! My own brothers',
 u' You want me to stay here after that?',
 u'\n',
 u'\n',
 u'\n',
 u'\nMAN (O.S.): Riders approaching!',
 u'\n',
 u'\nMAN #2 (O.S.): Open the gate!',
 u'\n',
 u'\n',
 u'CUT TO: CASTLE BLACK - COURTYARD',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: CASTLE BLACK - JON SNOW\u

In [74]:
script_split4 = [i.split('\n') for i in script_text6_04]
script_split4

[[u'INT. CASTLE BLACK - JON SNOW\u2019S ROOM'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'DOLOROUS EDD: Where you gonna go?'],
 [u'', u''],
 [u'', u'JON SNOW: South'],
 [u'', u''],
 [u'', u'DOLOROUS EDD: What are you gonna do?'],
 [u'', u''],
 [u'', u'JON SNOW: Get warm'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'DOLOROUS EDD: I was with you at Hardhome'],
 [u' We saw what\u2019s out there'],
 [u' We know it\u2019s coming here'],
 [u' How can you leave us now?'],
 [u'', u''],
 [u'', u'JON SNOW: I did everything I could'],
 [u' You know that'],
 [u'', u''],
 [u'', u'DOLOROUS EDD: You swore a vow'],
 [u'', u''],
 [u'', u'JON SNOW: Aye, I pledged my life to the Night\u2019s Watch'],
 [u' I gave my life'],
 [u'', u''],
 [u'', u'DOLOROUS EDD: For all nights to come'],
 [u'', u''],
 [u'', u'JON SNOW: They killed me, Edd! My own brothers'],
 [u' You want me to stay here after that?'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'MAN (O.S.): Riders approaching!'],
 [u'', u''],


In [75]:
string_script_text4 = ' '

for i in script_split4:
    for e in i:
        string_script_text4 = string_script_text4 + ' ' + e

In [76]:
string_script_text4

u'  INT. CASTLE BLACK - JON SNOW\u2019S ROOM        DOLOROUS EDD: Where you gonna go?    JON SNOW: South    DOLOROUS EDD: What are you gonna do?    JON SNOW: Get warm        DOLOROUS EDD: I was with you at Hardhome  We saw what\u2019s out there  We know it\u2019s coming here  How can you leave us now?    JON SNOW: I did everything I could  You know that    DOLOROUS EDD: You swore a vow    JON SNOW: Aye, I pledged my life to the Night\u2019s Watch  I gave my life    DOLOROUS EDD: For all nights to come    JON SNOW: They killed me, Edd! My own brothers  You want me to stay here after that?        MAN (O.S.): Riders approaching!    MAN #2 (O.S.): Open the gate!     CUT TO: CASTLE BLACK - COURTYARD         CUT TO: CASTLE BLACK - JON SNOW\u2019S ROOM        SANSA: This is good soup  Do you remember those kidney pies Old Nan used to make?    JON SNOW: With the peas and onions?    SANSA: Mmm    JON SNOW: We never should have left Winterfell    SANSA: Don\u2019t you wish we could go back to th

In [77]:
words4 = word_tokenize(string_script_text4)
words4

[u'INT',
 u'.',
 u'CASTLE',
 u'BLACK',
 u'-',
 u'JON',
 u'SNOW\u2019S',
 u'ROOM',
 u'DOLOROUS',
 u'EDD',
 u':',
 u'Where',
 u'you',
 u'gon',
 u'na',
 u'go',
 u'?',
 u'JON',
 u'SNOW',
 u':',
 u'South',
 u'DOLOROUS',
 u'EDD',
 u':',
 u'What',
 u'are',
 u'you',
 u'gon',
 u'na',
 u'do',
 u'?',
 u'JON',
 u'SNOW',
 u':',
 u'Get',
 u'warm',
 u'DOLOROUS',
 u'EDD',
 u':',
 u'I',
 u'was',
 u'with',
 u'you',
 u'at',
 u'Hardhome',
 u'We',
 u'saw',
 u'what\u2019s',
 u'out',
 u'there',
 u'We',
 u'know',
 u'it\u2019s',
 u'coming',
 u'here',
 u'How',
 u'can',
 u'you',
 u'leave',
 u'us',
 u'now',
 u'?',
 u'JON',
 u'SNOW',
 u':',
 u'I',
 u'did',
 u'everything',
 u'I',
 u'could',
 u'You',
 u'know',
 u'that',
 u'DOLOROUS',
 u'EDD',
 u':',
 u'You',
 u'swore',
 u'a',
 u'vow',
 u'JON',
 u'SNOW',
 u':',
 u'Aye',
 u',',
 u'I',
 u'pledged',
 u'my',
 u'life',
 u'to',
 u'the',
 u'Night\u2019s',
 u'Watch',
 u'I',
 u'gave',
 u'my',
 u'life',
 u'DOLOROUS',
 u'EDD',
 u':',
 u'For',
 u'all',
 u'nights',
 u'to',
 u'com

In [78]:
sentences4 = sent_tokenize(string_script_text4)
sentences4

[u'  INT.',
 u'CASTLE BLACK - JON SNOW\u2019S ROOM        DOLOROUS EDD: Where you gonna go?',
 u'JON SNOW: South    DOLOROUS EDD: What are you gonna do?',
 u'JON SNOW: Get warm        DOLOROUS EDD: I was with you at Hardhome  We saw what\u2019s out there  We know it\u2019s coming here  How can you leave us now?',
 u'JON SNOW: I did everything I could  You know that    DOLOROUS EDD: You swore a vow    JON SNOW: Aye, I pledged my life to the Night\u2019s Watch  I gave my life    DOLOROUS EDD: For all nights to come    JON SNOW: They killed me, Edd!',
 u'My own brothers  You want me to stay here after that?',
 u'MAN (O.S.',
 u'): Riders approaching!',
 u'MAN #2 (O.S.',
 u'): Open the gate!',
 u'CUT TO: CASTLE BLACK - COURTYARD         CUT TO: CASTLE BLACK - JON SNOW\u2019S ROOM        SANSA: This is good soup  Do you remember those kidney pies Old Nan used to make?',
 u'JON SNOW: With the peas and onions?',
 u'SANSA: Mmm    JON SNOW: We never should have left Winterfell    SANSA: Don\u201

In [79]:
dialogue4 = []

for sentence in sentences4:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names6_04):
            dialogue4.append(sentence)

In [80]:
dialogue4

[u'JON SNOW: South    DOLOROUS EDD: What are you gonna do?',
 u'JON SNOW: Get warm        DOLOROUS EDD: I was with you at Hardhome  We saw what\u2019s out there  We know it\u2019s coming here  How can you leave us now?',
 u'JON SNOW: I did everything I could  You know that    DOLOROUS EDD: You swore a vow    JON SNOW: Aye, I pledged my life to the Night\u2019s Watch  I gave my life    DOLOROUS EDD: For all nights to come    JON SNOW: They killed me, Edd!',
 u'JON SNOW: With the peas and onions?',
 u'SANSA: Mmm    JON SNOW: We never should have left Winterfell    SANSA: Don\u2019t you wish we could go back to the day we left?',
 u'SANSA: I spent a lot of time thinking about what as ass I was to you  I wish I could change everything    JON SNOW: We were children    SANSA: I was awful, just admit it        JON SNOW: You were occasionally awful  I\u2019m sure I can\u2019t have been great fun  Always sulking in the corner while the rest of you played    SANSA: Can you forgive me?',
 u'JON S

In [81]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s604.pkl', 'wb') as f:
    pickle.dump(dialogue4, f)

In [82]:
from collections import defaultdict

speakers4 = defaultdict(list)
for sentence in dialogue4:
    speakers4[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers4

defaultdict(list,
            {u'BRIENNE': [u'  I saw what happened  I saw Stannis\u2019 forces defeated in the field    DAVOS',
              u' Stannis  Just before I executed him        LITTLEFINGER (to ROBIN)'],
             u'CERSEI': [u' What are you doing here?',
              u' Since I\u2019ve missed the past several Small Coucil meetings, I wanted to speak to you about a few things.',
              u' As have we all, unfortunately.',
              u' Look at me.',
              u' It\u2019s all right.',
              u' Whether I like her or not is completely unimportant.',
              u' You\u2019ve spoken with him?',
              u' You once spoke of your respect for our father because he understood the necessity of working with one\u2019s rivals.',
              u" The High Sparrow seized power knowing full well we'd bicker amongst ourselves instead of seizing it back.",
              u' You hate these fanatics as much as we do.',
              u' Then stand aside and l

In [83]:
speakers4['JON SNOW']

[u' South    DOLOROUS EDD',
 u' Get warm        DOLOROUS EDD',
 u' I did everything I could  You know that    DOLOROUS EDD',
 u' With the peas and onions?',
 u' There\u2019s nothing to forgive    SANSA',
 u' Where will we go?',
 u' I can\u2019t stay here, not after what happened    SANSA',
 u' They didn\u2019t come here to serve me    SANSA',
 u' Sansa    SANSA',
 u' I\u2019m not Lord Commander anymore.',
 u" It's just more of the same.",
 u' Lord of Winterfell and Warden of the North.',
 u' We don\u2019t know that.']

In [84]:
episode_four = pd.DataFrame.from_dict(speakers4, orient="index")
print episode_four.shape

(33, 13)


In [85]:
#from numpy import nan
#episode_four.fillna(value=str(0), inplace=True)

In [86]:
episode_four.info()

<class 'pandas.core.frame.DataFrame'>
Index: 33 entries, KEVAN to MAN
Data columns (total 13 columns):
0     33 non-null object
1     28 non-null object
2     21 non-null object
3     18 non-null object
4     13 non-null object
5     12 non-null object
6     9 non-null object
7     9 non-null object
8     8 non-null object
9     7 non-null object
10    6 non-null object
11    3 non-null object
12    1 non-null object
dtypes: object(13)
memory usage: 3.6+ KB


In [87]:
episode_four.head()

0   \
KEVAN           The king has ordered me to take no action ag...   
MELISANDRE              I will do as Jon Snow commands    DAVOS   
JAIME                         Cersei is the mother of the king.   
TYRION                                 I did          GREY WORM   
LITTLEFINGER          My lord  Come and see        LITTLEFINGER   

                                                             1   \
KEVAN          No, but if the king should call on me --    J...   
MELISANDRE           He’s the prince that was promised    DAVOS   
JAIME                             You’ll take no action at all.   
TYRION                         Long enough to know    MISSANDEI   
LITTLEFINGER                         Indeed I was    YOHN ROYCE   

                                                             2   \
KEVAN                                Of course I want him back.   
MELISANDRE     There was a battle  Stannis was defeated     ...   
JAIME                                                      None   
TYRION         Instead of abolishing slavery overnight, we w...   
LITTLEFINGER   Tell me, Lord Royce, how many people knew of ...   

                                                             3   \
KEVAN          If it doesn’t go as planned, the Sparrows hav...   
MELISANDRE                                                 None   
JAIME                                                      None   
TYRION         Because our queen chose me as her advisor  Un...   
LITTLEFINGER   Lord Royce has served the Vale well  He;s enj...   

                                             4   \
KEVAN                                      None   
MELISANDRE                                 None   
JAIME                                      None   
TYRION         Soon  You have my word    MAN #1   
LITTLEFINGER                               None   

                                                           5     6     7   \
KEVAN                                                    None  None  None   
MELISANDRE                                               None  None  None   
JAIME                                                    None  None  None   
TYRION         We offered terms    MAN #1 (speaking Valyrian)  None  None   
LITTLEFINGER                                             None  None  None   

                8     9     10    11    12  
KEVAN         None  None  None  None  None  
MELISANDRE    None  None  None  None  None  
JAIME         None  None  None  None  None  
TYRION        None  None  None  None  None  
LITTLEFINGER  None  None  None  None  None

In [88]:
test4 = episode_four[0].apply(remove_stops)
test4

KEVAN              king ordered take action high sparrow faith mi...
MELISANDRE                                   jon snow commands davos
JAIME                                             cersei mother king
TYRION                                                     grey worm
LITTLEFINGER                              lord come see littlefinger
ROBIN                                                    uncle petyr
YARA                                                       cant hear
MAESTER PYCELLE                    advising king current predicament
YOHN ROYCE         last time saw baelish told taking sansa stark ...
KHAL #3                            id like know khaleesi tastes like
DAENERYS                                       mmhmm lhazareen woman
LADY OLENNA                 would thought perfectly clear first time
THEON                                                        escaped
TOMMEN                                   thank counsel grand maester
CERSEI                            

In [89]:
for column in episode_four.columns:
    for x in range(len(episode_four[column])):
        episode_four[column][x] = remove_stops(episode_four[column][x])

In [90]:
episode_four.index = episode_four.index.str.title()

In [91]:
episode_four.head()

0   \
Kevan         king ordered take action high sparrow faith mi...   
Melisandre                              jon snow commands davos   
Jaime                                        cersei mother king   
Tyrion                                                grey worm   
Littlefinger                         lord come see littlefinger   

                                      1   \
Kevan                    king call jaime   
Melisandre     hes prince promised davos   
Jaime                  youll take action   
Tyrion        long enough know missandei   
Littlefinger           indeed yohn royce   

                                                             2   \
Kevan                                          course want back   
Melisandre                        battle stannis defeated davos   
Jaime                                                      None   
Tyrion        instead abolishing slavery overnight give seve...   
Littlefinger  tell lord royce many people knew travel plans ...   

                                                             3   \
Kevan              doesnt go planned sparrows many friends city   
Melisandre                                                 None   
Jaime                                                      None   
Tyrion                  queen chose advisor returns travels man   
Littlefinger  lord royce served vale well hes enjoyed distin...   

                         4                                    5     6     7   \
Kevan                  None                                 None  None  None   
Melisandre             None                                 None  None  None   
Jaime                  None                                 None  None  None   
Tyrion        soon word man  offered terms man speaking valyrian  None  None   
Littlefinger           None                                 None  None  None   

                8     9     10    11    12  
Kevan         None  None  None  None  None  
Melisandre    None  None  None  None  None  
Jaime         None  None  None  None  None  
Tyrion        None  None  None  None  None  
Littlefinger  None  None  None  None  None

### Episode Five

In [92]:
df_s6.script_text[4]

[u'INT. CASTLE BLACK - SANSA\u2019S ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\nSANSA: Yes?',
 u'\n',
 u'\n',
 u'\n',
 u'\nMAN: For you, my lady.',
 u'\n',
 u'\n',
 u'\n',
 u'\nSANSA: How far is Mole\u2019s Town?',
 u'\n',
 u'\n',
 u'CUT TO: MOLE\u2019S TOWN - SHACK',
 u'\n',
 u'\n',
 u'\n',
 u'\nLITTLEFINGER: Sansa. Lady Brienne. When I heard you had escaped WInterfell, I feared the worst. You have no idea how happy I am to see you unharmed.',
 u'\n',
 u'\nSANSA: Unharmed? What are you doing here?',
 u'\n',
 u'\nLITTLEFINGER: I rode north with the Knights of the Vale to come to your aid. They\u2019re encamped at Moat Cailin as we speak.',
 u'\n',
 u'\nSANSA: To come to my aid? Did you know about Ramsay? If you didn\u2019t know, you\u2019re an idiot. If you did know, you\u2019re my enemy.',
 u'\n',
 u'\n',
 u'\n',
 u'\nSANSA: Would you like to hear about our wedding night? He never hurt my face. He needed my face, the face of Ned Stark\u2019s daughter. But the rest of me, he did what he liked 

In [93]:
script_text6_05 = df_s6.script_text[4]
print type(script_text6_05)

script_text6_05

<type 'list'>


[u'INT. CASTLE BLACK - SANSA\u2019S ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\nSANSA: Yes?',
 u'\n',
 u'\n',
 u'\n',
 u'\nMAN: For you, my lady.',
 u'\n',
 u'\n',
 u'\n',
 u'\nSANSA: How far is Mole\u2019s Town?',
 u'\n',
 u'\n',
 u'CUT TO: MOLE\u2019S TOWN - SHACK',
 u'\n',
 u'\n',
 u'\n',
 u'\nLITTLEFINGER: Sansa. Lady Brienne. When I heard you had escaped WInterfell, I feared the worst. You have no idea how happy I am to see you unharmed.',
 u'\n',
 u'\nSANSA: Unharmed? What are you doing here?',
 u'\n',
 u'\nLITTLEFINGER: I rode north with the Knights of the Vale to come to your aid. They\u2019re encamped at Moat Cailin as we speak.',
 u'\n',
 u'\nSANSA: To come to my aid? Did you know about Ramsay? If you didn\u2019t know, you\u2019re an idiot. If you did know, you\u2019re my enemy.',
 u'\n',
 u'\n',
 u'\n',
 u'\nSANSA: Would you like to hear about our wedding night? He never hurt my face. He needed my face, the face of Ned Stark\u2019s daughter. But the rest of me, he did what he liked 

In [94]:
script_split5 = [i.split('\n') for i in script_text6_05]
script_split5

[[u'INT. CASTLE BLACK - SANSA\u2019S ROOM'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'SANSA: Yes?'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'MAN: For you, my lady.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'SANSA: How far is Mole\u2019s Town?'],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: MOLE\u2019S TOWN - SHACK'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'',
  u'LITTLEFINGER: Sansa. Lady Brienne. When I heard you had escaped WInterfell, I feared the worst. You have no idea how happy I am to see you unharmed.'],
 [u'', u''],
 [u'', u'SANSA: Unharmed? What are you doing here?'],
 [u'', u''],
 [u'',
  u'LITTLEFINGER: I rode north with the Knights of the Vale to come to your aid. They\u2019re encamped at Moat Cailin as we speak.'],
 [u'', u''],
 [u'',
  u'SANSA: To come to my aid? Did you know about Ramsay? If you didn\u2019t know, you\u2019re an idiot. If you did know, you\u2019re my enemy.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'',
  u'SANSA: Would you like to h

In [95]:
string_script_text5 = ' '

for i in script_split5:
    for e in i:
        string_script_text5 = string_script_text5 + ' ' + e

In [96]:
string_script_text5

u'  INT. CASTLE BLACK - SANSA\u2019S ROOM        SANSA: Yes?        MAN: For you, my lady.        SANSA: How far is Mole\u2019s Town?     CUT TO: MOLE\u2019S TOWN - SHACK        LITTLEFINGER: Sansa. Lady Brienne. When I heard you had escaped WInterfell, I feared the worst. You have no idea how happy I am to see you unharmed.    SANSA: Unharmed? What are you doing here?    LITTLEFINGER: I rode north with the Knights of the Vale to come to your aid. They\u2019re encamped at Moat Cailin as we speak.    SANSA: To come to my aid? Did you know about Ramsay? If you didn\u2019t know, you\u2019re an idiot. If you did know, you\u2019re my enemy.        SANSA: Would you like to hear about our wedding night? He never hurt my face. He needed my face, the face of Ned Stark\u2019s daughter. But the rest of me, he did what he liked with the rest of me as long as I could still give him an heir. What do you think he did?    LITTLEFINGER: I can\u2019t begin to contemplate --    SANSA: What do you think h

In [97]:
words5 = word_tokenize(string_script_text5)
words5

[u'INT',
 u'.',
 u'CASTLE',
 u'BLACK',
 u'-',
 u'SANSA\u2019S',
 u'ROOM',
 u'SANSA',
 u':',
 u'Yes',
 u'?',
 u'MAN',
 u':',
 u'For',
 u'you',
 u',',
 u'my',
 u'lady',
 u'.',
 u'SANSA',
 u':',
 u'How',
 u'far',
 u'is',
 u'Mole\u2019s',
 u'Town',
 u'?',
 u'CUT',
 u'TO',
 u':',
 u'MOLE\u2019S',
 u'TOWN',
 u'-',
 u'SHACK',
 u'LITTLEFINGER',
 u':',
 u'Sansa',
 u'.',
 u'Lady',
 u'Brienne',
 u'.',
 u'When',
 u'I',
 u'heard',
 u'you',
 u'had',
 u'escaped',
 u'WInterfell',
 u',',
 u'I',
 u'feared',
 u'the',
 u'worst',
 u'.',
 u'You',
 u'have',
 u'no',
 u'idea',
 u'how',
 u'happy',
 u'I',
 u'am',
 u'to',
 u'see',
 u'you',
 u'unharmed',
 u'.',
 u'SANSA',
 u':',
 u'Unharmed',
 u'?',
 u'What',
 u'are',
 u'you',
 u'doing',
 u'here',
 u'?',
 u'LITTLEFINGER',
 u':',
 u'I',
 u'rode',
 u'north',
 u'with',
 u'the',
 u'Knights',
 u'of',
 u'the',
 u'Vale',
 u'to',
 u'come',
 u'to',
 u'your',
 u'aid',
 u'.',
 u'They\u2019re',
 u'encamped',
 u'at',
 u'Moat',
 u'Cailin',
 u'as',
 u'we',
 u'speak',
 u'.',
 u'S

In [98]:
sentences5 = sent_tokenize(string_script_text5)
sentences5

[u'  INT.',
 u'CASTLE BLACK - SANSA\u2019S ROOM        SANSA: Yes?',
 u'MAN: For you, my lady.',
 u'SANSA: How far is Mole\u2019s Town?',
 u'CUT TO: MOLE\u2019S TOWN - SHACK        LITTLEFINGER: Sansa.',
 u'Lady Brienne.',
 u'When I heard you had escaped WInterfell, I feared the worst.',
 u'You have no idea how happy I am to see you unharmed.',
 u'SANSA: Unharmed?',
 u'What are you doing here?',
 u'LITTLEFINGER: I rode north with the Knights of the Vale to come to your aid.',
 u'They\u2019re encamped at Moat Cailin as we speak.',
 u'SANSA: To come to my aid?',
 u'Did you know about Ramsay?',
 u'If you didn\u2019t know, you\u2019re an idiot.',
 u'If you did know, you\u2019re my enemy.',
 u'SANSA: Would you like to hear about our wedding night?',
 u'He never hurt my face.',
 u'He needed my face, the face of Ned Stark\u2019s daughter.',
 u'But the rest of me, he did what he liked with the rest of me as long as I could still give him an heir.',
 u'What do you think he did?',
 u'LITTLEFINGE

In [99]:
dialogue5 = []

for sentence in sentences5:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names6_05):
            dialogue5.append(sentence)

In [100]:
dialogue5

[u'MAN: For you, my lady.',
 u'SANSA: How far is Mole\u2019s Town?',
 u'SANSA: Unharmed?',
 u'LITTLEFINGER: I rode north with the Knights of the Vale to come to your aid.',
 u'SANSA: To come to my aid?',
 u'SANSA: Would you like to hear about our wedding night?',
 u'LITTLEFINGER: I can\u2019t begin to contemplate --    SANSA: What do you think he did to me?',
 u'BRIENNE: Lady Sansa asked you a question.',
 u'LITTLEFINGER: He beat you.',
 u'SANSA: Yes, he enjoyed that.',
 u'LITTLEFINGER: Sansa, I --    SANSA: What else?',
 u'LITTLEFINGER: Did he cut you?',
 u'SANSA: Maybe you did know about Ramsay all along.',
 u'LITTLEFINGER: I didn\u2019t know.',
 u'SANSA: I thought you knew everyone\u2019s secrets.',
 u'LITTLEFINGER: I made a mistake, a horrible mistake.',
 u'SANSA: The other things he did, ladies aren\u2019t supposed to talk about those things, but I imagine brothel keepers talk about them all the time.',
 u'LITTLEFINGER: I\u2019m so sorry.',
 u'SANSA: You said you would protect me.

In [101]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s605.pkl', 'wb') as f:
    pickle.dump(dialogue5, f)

In [102]:
from collections import defaultdict

speakers5 = defaultdict(list)
for sentence in dialogue5:
    speakers5[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers5

defaultdict(list,
            {u'AERON': [u' We speak in the presence of the Drowned God.',
              u' Let the fish eat the scales off his eyes.',
              u' What is dead may never die, but rises again harder and stronger.',
              u' What is dead may never die.',
              u' They stole our best ships.'],
             u'AERSON': [u' Listen to the waves.'],
             u'ALL': [u' Aye!',
              u' Aye!',
              u' Aye!',
              u' Aye!',
              u' Aye!',
              u' Aye!',
              u' Aye!',
              u' What is dead may never die.'],
             u'ARYA': [u' Who was the first?',
              u' Where did they go?',
              u' A girl has no desires.',
              u' Who?',
              u' If a girl could use one of the faces from the hall\u2026    JAQEN',
              u' She\u2019s a good actress.',
              u' Seems like a decent woman.',
              u' No.',
              u' The younger actress.',
  

In [103]:
speakers5['AERON']

[u' We speak in the presence of the Drowned God.',
 u' Let the fish eat the scales off his eyes.',
 u' What is dead may never die, but rises again harder and stronger.',
 u' What is dead may never die.',
 u' They stole our best ships.']

In [104]:
episode_five = pd.DataFrame.from_dict(speakers5, orient="index")
print episode_five.shape

(41, 30)


In [105]:
#from numpy import nan
#episode_five.fillna(value=str(0), inplace=True)

In [106]:
episode_five.info()

<class 'pandas.core.frame.DataFrame'>
Index: 41 entries, DAVOS to MAN
Data columns (total 30 columns):
0     41 non-null object
1     33 non-null object
2     29 non-null object
3     27 non-null object
4     25 non-null object
5     21 non-null object
6     18 non-null object
7     16 non-null object
8     12 non-null object
9     11 non-null object
10    7 non-null object
11    7 non-null object
12    7 non-null object
13    5 non-null object
14    3 non-null object
15    2 non-null object
16    1 non-null object
17    1 non-null object
18    1 non-null object
19    1 non-null object
20    1 non-null object
21    1 non-null object
22    1 non-null object
23    1 non-null object
24    1 non-null object
25    1 non-null object
26    1 non-null object
27    1 non-null object
28    1 non-null object
29    1 non-null object
dtypes: object(30)
memory usage: 9.9+ KB


In [107]:
episode_five.head()

0   \
DAVOS              Aside from the Starks and the Boltons, the mo...   
KINVARA             Daenerys Stormborn is the one who was promised.   
NAN                                                          Wylis!   
THREE-EYED RAVEN                                    He touched you.   
TYRION                                             It’s not enough.   

                                                                 1   \
DAVOS              The Umbers and the Karstarks have already dec...   
KINVARA            She has freed the slaves from their chains an...   
NAN                                                            None   
THREE-EYED RAVEN                             He knows you are here.   
TYRION                   It’s not enough for Meereen to have peace.   

                                                                 2   \
DAVOS              I beg your pardon, my lady, but they know tha...   
KINVARA            Her dragons are fire made flesh, a gift from ...   
NAN                                                            None   
THREE-EYED RAVEN                                        He can now.   
TYRION             Yes, but do they know who brought them security?   

                                                                 3   \
DAVOS                                     Precious little, my lady.   
KINVARA            You want your queen to be worshipped and obeyed.   
NAN                                                            None   
THREE-EYED RAVEN                                 The time has come.   
TYRION                               Who said anything about “him”?   

                                                                 4   \
DAVOS              They may well be loyal, but how many rose up ...   
KINVARA                     I will summon my most eloquent priests.   
NAN                                                            None   
THREE-EYED RAVEN                              For you to become me.   
TYRION                      That’s about the extent of my Valyrian.   

                                                       5   \
DAVOS                                   I don’t doubt it.   
KINVARA                    Everything is the Lord’s will.   
NAN                                                  None   
THREE-EYED RAVEN                                      No.   
TYRION             Thank you for travelling all this way.   

                                                                 6   \
DAVOS                   I didn’t know the Tullys still had an army.   
KINVARA            Everyone is what they are and where they are ...   
NAN                                                            None   
THREE-EYED RAVEN                    Listen to your friend, Brandon.   
TYRION                              The truth is we need your help.   

                                                                 7   \
DAVOS                                                  That’s good.   
KINVARA            Should I tell you the name of the one who spoke?   
NAN                                                            None   
THREE-EYED RAVEN                                               None   
TYRION                                                         Yes.   

                                         8   \
DAVOS                                  None   
KINVARA            We serve the same queen.   
NAN                                    None   
THREE-EYED RAVEN                       None   
TYRION                      She did indeed.   

                                                                 9   \
DAVOS                                                          None   
KINVARA                                                        None   
NAN                                                            None   
THREE-EYED RAVEN                                               None   
TYRION             Ideally we’d avoid purifying too many nonbeli...   


In [108]:
test5 = episode_five[0].apply(remove_stops)
test5

DAVOS               aside starks boltons powerful houses north umb...
KINVARA                               daenerys stormborn one promised
NAN                                                             wylis
THREE-EYED RAVEN                                              touched
TYRION                                                         enough
EURON                                                im euron greyjoy
LITTLEFINGER                         rode north knights vale come aid
MISSANDEI                                 people know brought freedom
DOLOROUS EDD                                                 ill best
YARA                yara greyjoy daughter balon greyjoy king iron ...
YOUNG HODOR                                                 hold door
AERSON                                                   listen waves
THEON                      theon greyjoylast living son balon greyjoy
LADY CRANE                                         stay joffreys hand
RICKARD             

In [109]:
for column in episode_five.columns:
    for x in range(len(episode_five[column])):
        episode_five[column][x] = remove_stops(episode_five[column][x])

In [110]:
episode_five.index = episode_five.index.str.title()

In [111]:
episode_five.head()

0   \
Davos             aside starks boltons powerful houses north umb...   
Kinvara                             daenerys stormborn one promised   
Nan                                                           wylis   
Three-Eyed Raven                                            touched   
Tyrion                                                       enough   

                                                              1   \
Davos             umbers karstarks already declared boltons well   
Kinvara               freed slaves chains crucified masters sins   
Nan                                                         None   
Three-Eyed Raven                                           knows   
Tyrion                                      enough meereen peace   

                                                          2   \
Davos             beg pardon lady know stark beheaded father   
Kinvara              dragons fire made flesh gift lord light   
Nan                                                     None   
Three-Eyed Raven                                               
Tyrion                             yes know brought security   

                                            3   \
Davos                     precious little lady   
Kinvara           want queen worshipped obeyed   
Nan                                       None   
Three-Eyed Raven                     time come   
Tyrion                           said anything   

                                                                4   \
Davos             may well loyal many rose boltons betrayed family   
Kinvara                                    summon eloquent priests   
Nan                                                           None   
Three-Eyed Raven                                            become   
Tyrion                                       thats extent valyrian   

                                    5                             6   \
Davos                       dont doubt  didnt know tullys still army   
Kinvara               everything lords               everyone reason   
Nan                               None                          None   
Three-Eyed Raven                               listen friend brandon   
Tyrion            thank travelling way               truth need help   

                                   7            8   \
Davos                      thats good         None   
Kinvara           tell name one spoke  serve queen   
Nan                              None         None   
Three-Eyed Raven                 None         None   
Tyrion                            yes       indeed   

                                                             9   \
Davos                                                      None   
Kinvara                                                    None   
Nan                                                        None   
Three-Eyed Raven                                           None   
Tyrion            ideally wed avoid purifying many nonbelievers   

                                10                      11  \
Davos                         None                    None   
Kinvara                       None                    None   
Nan                           None                    None   
Three-Eyed Raven              None                    None   
Tyrion            id settle obeyed  sounds excellent varys   

                                                        12  \
Davos                                                 None   
Kinvara                                               None   
Nan                                                   None   
Three-Eyed Raven                                      None   
Tyrion            wed grateful support could provide queen   

                                                                 13    14  \
Davos                                                          None  None   
Kinvara                                                      

### Episode Six

In [112]:
df_s6.script_text[5]

[u'\n',
 u'\nBRAN: Meera. They found us.',
 u'\n',
 u'\n',
 u'\n',
 u'\nMEERA: I\u2019m so sorry.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRIDER: Come with me, now.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRIDER: The dead don\u2019t rest.',
 u'\n',
 u'\n',
 u'\n',
 u'\nGILLY: It\u2019s so green.',
 u'\n',
 u'\nSAM: Oh, yes. Once you get south of the Riverlands, very different sorts of trees start to take over. Maple, elm, beech, poplar. The odd willow. And of course now that summer\u2019s over, you\u2019ll start seeing the autumn colors coming in. Still, you\u2019ll find more green here than anywhere else.',
 u'\n',
 u'\nGILLY: You\u2019re nervous. You\u2019re a nervous talker.',
 u'\n',
 u'\n',
 u'\n',
 u'\nGILLY: That\u2019s not any better being a nervous mute.',
 u'\n',
 u'\nSAM: I didn\u2019t think I\u2019d ever come back here after my father made me renounce my title and inheritance and, well, threaten to kill me if I didn\u2019t. A person just doesn\u2019t feel welcome at that point.',
 u'\n',
 u'\n

In [113]:
script_text6_06 = df_s6.script_text[5]
print type(script_text6_06)

script_text6_06

<type 'list'>


[u'\n',
 u'\nBRAN: Meera. They found us.',
 u'\n',
 u'\n',
 u'\n',
 u'\nMEERA: I\u2019m so sorry.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRIDER: Come with me, now.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRIDER: The dead don\u2019t rest.',
 u'\n',
 u'\n',
 u'\n',
 u'\nGILLY: It\u2019s so green.',
 u'\n',
 u'\nSAM: Oh, yes. Once you get south of the Riverlands, very different sorts of trees start to take over. Maple, elm, beech, poplar. The odd willow. And of course now that summer\u2019s over, you\u2019ll start seeing the autumn colors coming in. Still, you\u2019ll find more green here than anywhere else.',
 u'\n',
 u'\nGILLY: You\u2019re nervous. You\u2019re a nervous talker.',
 u'\n',
 u'\n',
 u'\n',
 u'\nGILLY: That\u2019s not any better being a nervous mute.',
 u'\n',
 u'\nSAM: I didn\u2019t think I\u2019d ever come back here after my father made me renounce my title and inheritance and, well, threaten to kill me if I didn\u2019t. A person just doesn\u2019t feel welcome at that point.',
 u'\n',
 u'\n

In [114]:
script_split6 = [i.split('\n') for i in script_text6_06]
script_split6

[[u'', u''],
 [u'', u'BRAN: Meera. They found us.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'MEERA: I\u2019m so sorry.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'RIDER: Come with me, now.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'RIDER: The dead don\u2019t rest.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'GILLY: It\u2019s so green.'],
 [u'', u''],
 [u'',
  u'SAM: Oh, yes. Once you get south of the Riverlands, very different sorts of trees start to take over. Maple, elm, beech, poplar. The odd willow. And of course now that summer\u2019s over, you\u2019ll start seeing the autumn colors coming in. Still, you\u2019ll find more green here than anywhere else.'],
 [u'', u''],
 [u'', u'GILLY: You\u2019re nervous. You\u2019re a nervous talker.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'GILLY: That\u2019s not any better being a nervous mute.'],
 [u'', u''],
 [u'',
  u'SAM: I didn\u2019t think I\u2019d ever come back here after my father made me renounce m

In [115]:
string_script_text6 = ' '

for i in script_split6:
    for e in i:
        string_script_text6 = string_script_text6 + ' ' + e

In [116]:
string_script_text6

u'     BRAN: Meera. They found us.        MEERA: I\u2019m so sorry.        RIDER: Come with me, now.        RIDER: The dead don\u2019t rest.        GILLY: It\u2019s so green.    SAM: Oh, yes. Once you get south of the Riverlands, very different sorts of trees start to take over. Maple, elm, beech, poplar. The odd willow. And of course now that summer\u2019s over, you\u2019ll start seeing the autumn colors coming in. Still, you\u2019ll find more green here than anywhere else.    GILLY: You\u2019re nervous. You\u2019re a nervous talker.        GILLY: That\u2019s not any better being a nervous mute.    SAM: I didn\u2019t think I\u2019d ever come back here after my father made me renounce my title and inheritance and, well, threaten to kill me if I didn\u2019t. A person just doesn\u2019t feel welcome at that point.        SAM: And I certainly didn\u2019t expect to be introducing him to my family. So you know what to tell them.    GILLY: That Little Sam is your baby.    SAM: Yes, now that\u

In [117]:
words6 = word_tokenize(string_script_text6)
words6

[u'BRAN',
 u':',
 u'Meera',
 u'.',
 u'They',
 u'found',
 u'us',
 u'.',
 u'MEERA',
 u':',
 u'I\u2019m',
 u'so',
 u'sorry',
 u'.',
 u'RIDER',
 u':',
 u'Come',
 u'with',
 u'me',
 u',',
 u'now',
 u'.',
 u'RIDER',
 u':',
 u'The',
 u'dead',
 u'don\u2019t',
 u'rest',
 u'.',
 u'GILLY',
 u':',
 u'It\u2019s',
 u'so',
 u'green',
 u'.',
 u'SAM',
 u':',
 u'Oh',
 u',',
 u'yes',
 u'.',
 u'Once',
 u'you',
 u'get',
 u'south',
 u'of',
 u'the',
 u'Riverlands',
 u',',
 u'very',
 u'different',
 u'sorts',
 u'of',
 u'trees',
 u'start',
 u'to',
 u'take',
 u'over',
 u'.',
 u'Maple',
 u',',
 u'elm',
 u',',
 u'beech',
 u',',
 u'poplar',
 u'.',
 u'The',
 u'odd',
 u'willow',
 u'.',
 u'And',
 u'of',
 u'course',
 u'now',
 u'that',
 u'summer\u2019s',
 u'over',
 u',',
 u'you\u2019ll',
 u'start',
 u'seeing',
 u'the',
 u'autumn',
 u'colors',
 u'coming',
 u'in',
 u'.',
 u'Still',
 u',',
 u'you\u2019ll',
 u'find',
 u'more',
 u'green',
 u'here',
 u'than',
 u'anywhere',
 u'else',
 u'.',
 u'GILLY',
 u':',
 u'You\u2019re',
 u

In [118]:
sentences6 = sent_tokenize(string_script_text6)
sentences6

[u'     BRAN: Meera.',
 u'They found us.',
 u'MEERA: I\u2019m so sorry.',
 u'RIDER: Come with me, now.',
 u'RIDER: The dead don\u2019t rest.',
 u'GILLY: It\u2019s so green.',
 u'SAM: Oh, yes.',
 u'Once you get south of the Riverlands, very different sorts of trees start to take over.',
 u'Maple, elm, beech, poplar.',
 u'The odd willow.',
 u'And of course now that summer\u2019s over, you\u2019ll start seeing the autumn colors coming in.',
 u'Still, you\u2019ll find more green here than anywhere else.',
 u'GILLY: You\u2019re nervous.',
 u'You\u2019re a nervous talker.',
 u'GILLY: That\u2019s not any better being a nervous mute.',
 u'SAM: I didn\u2019t think I\u2019d ever come back here after my father made me renounce my title and inheritance and, well, threaten to kill me if I didn\u2019t.',
 u'A person just doesn\u2019t feel welcome at that point.',
 u'SAM: And I certainly didn\u2019t expect to be introducing him to my family.',
 u'So you know what to tell them.',
 u'GILLY: That Little

In [119]:
dialogue6 = []

for sentence in sentences6:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names6_06):
            dialogue6.append(sentence)

In [120]:
dialogue6

[u'MEERA: I\u2019m so sorry.',
 u'RIDER: Come with me, now.',
 u'RIDER: The dead don\u2019t rest.',
 u'GILLY: It\u2019s so green.',
 u'SAM: Oh, yes.',
 u'GILLY: You\u2019re nervous.',
 u'GILLY: That\u2019s not any better being a nervous mute.',
 u'SAM: I didn\u2019t think I\u2019d ever come back here after my father made me renounce my title and inheritance and, well, threaten to kill me if I didn\u2019t.',
 u'SAM: And I certainly didn\u2019t expect to be introducing him to my family.',
 u'GILLY: That Little Sam is your baby.',
 u'SAM: Yes, now that\u2019s very important.',
 u'GILLY: What did you tell your family about me?',
 u'SAM: I told them I met you in the North.',
 u'GILLY: Did you tell them how far north?',
 u'SAM: Well, it wasn\u2019t a very large piece of parchment.',
 u'GILLY: You didn\u2019t tell them where I\u2019m really from?',
 u'SAM: The thing is...my father doesn\u2019t like wildlings.',
 u'GILLY: I think we\u2019re here.',
 u'SAM: Oh, hello, Mother.',
 u'MELESSA: I ne

In [121]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s606.pkl', 'wb') as f:
    pickle.dump(dialogue6, f)

In [122]:
from collections import defaultdict

speakers6 = defaultdict(list)
for sentence in dialogue6:
    speakers6[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers6

defaultdict(list,
            {u'ALL': [u' Hail King Joffrey.'],
             u'ARYA': [u' Nothing.',
              u' Three times.',
              u' No.',
              u' You\u2019re very good.',
              u' So change it.',
              u' The queen loves her son more than anything.',
              u' Mercy.',
              u' I have to go.',
              u' Careful of that one.'],
             u'BENJEN': [u' I led a ranging party deep into the North to find White Walkers.',
              u' The same way they made the Walkers in the first place.',
              u' You are the Three-Eyed Raven now.',
              u' You must learn to control it before the Night King comes.',
              u' Drink.',
              u' One way or another, he will find his way to the world of men.'],
             u'BIANCA': [u' Lady Crane, they loved you.'],
             u'BLACK WALDER': [u' Yes, father.',
              u' I don\u2019t think it\u2019s fair to blame us- -    WALDER',
            

In [123]:
speakers6['ARYA']

[u' Nothing.',
 u' Three times.',
 u' No.',
 u' You\u2019re very good.',
 u' So change it.',
 u' The queen loves her son more than anything.',
 u' Mercy.',
 u' I have to go.',
 u' Careful of that one.']

In [124]:
episode_six = pd.DataFrame.from_dict(speakers6, orient="index")
print episode_six.shape

(34, 32)


In [125]:
#from numpy import nan
#episode_six.fillna(value=str(0), inplace=True)

In [126]:
episode_six.info()

<class 'pandas.core.frame.DataFrame'>
Index: 34 entries, DICKON to BRAN
Data columns (total 32 columns):
0     34 non-null object
1     29 non-null object
2     26 non-null object
3     23 non-null object
4     20 non-null object
5     16 non-null object
6     15 non-null object
7     12 non-null object
8     11 non-null object
9     8 non-null object
10    6 non-null object
11    5 non-null object
12    4 non-null object
13    4 non-null object
14    4 non-null object
15    3 non-null object
16    3 non-null object
17    3 non-null object
18    2 non-null object
19    2 non-null object
20    2 non-null object
21    2 non-null object
22    2 non-null object
23    2 non-null object
24    1 non-null object
25    1 non-null object
26    1 non-null object
27    1 non-null object
28    1 non-null object
29    1 non-null object
30    1 non-null object
31    1 non-null object
dtypes: object(32)
memory usage: 8.8+ KB


In [127]:
episode_six.head()

0   \
DICKON                                          Well, no.   
GILLY                                      It’s so green.   
JAIME                                            My lord.   
WOMAN    Long live King Tommen and bless you, Queen Ma...   
SAM                                              Oh, yes.   

                                                       1   \
DICKON                     Brought it down from 70 yards.   
GILLY                                     You’re nervous.   
JAIME                                 Sorry to interrupt.   
WOMAN                                                None   
SAM      I didn’t think I’d ever come back here after ...   

                                                       2   \
DICKON          So do you do much hunting up at the wall?   
GILLY         That’s not any better being a nervous mute.   
JAIME    I speak for King Tommen of House Baratheon, F...   
WOMAN                                                None   
SAM      And I certainly didn’t expect to be introduci...   

                                            3   \
DICKON                                Mm-hmmm.   
GILLY            That Little Sam is your baby.   
JAIME    You already insulted one great house.   
WOMAN                                     None   
SAM            Yes, now that’s very important.   

                                                       4   \
DICKON                             There’s no such thing.   
GILLY             What did you tell your family about me?   
JAIME    I’ve been a member of the Kingsguard since be...   
WOMAN                                                None   
SAM                   I told them I met you in the North.   

                                                       5   \
DICKON                                               None   
GILLY                    Did you tell them how far north?   
JAIME              Not when you’re sitting in that chair.   
WOMAN                                                None   
SAM      Well, it wasn’t a very large piece of parchment.   

                                                       6   \
DICKON                                               None   
GILLY         You didn’t tell them where I’m really from?   
JAIME             Will I be walking naked in the streets?   
WOMAN                                                None   
SAM      The thing is...my father doesn’t like wildlings.   

                                                 7   \
DICKON                                         None   
GILLY                           I think we’re here.   
JAIME    I’m being sent to deal with the Blackfish.   
WOMAN                                          None   
SAM                              Oh, hello, Mother.   

                                          8   \
DICKON                                  None   
GILLY    I am happy to know you, Lady Tarly.   
JAIME       I’m not going to the Riverlands.   
WOMAN                                   None   
SAM                                      Oh.   

                                                       9   \
DICKON                                               None   
GILLY                                     Yes, of course.   
JAIME    I’m going to give Bronn the largest bag of go...   
WOMAN                                                None   
SAM                                                Talla?   

                                     10  \
DICKON                             None   
GILLY        It’s hard to walk in this.   
JAIME                   He has our son!   
WOMAN                              None   
SAM      Oh, um, Mother, this is Gilly.   

                                             11  \
DICKON                                     None   
GILLY                     He can wield a sword.   
JAIME                  You’ll stand trial soon.   
WOMAN                                      None   
SAM      Oh, and this, this is our son Samwell.   


In [128]:
test6 = episode_six[0].apply(remove_stops)
test6

DICKON                                                     well
GILLY                                                     green
JAIME                                                      lord
WOMAN                long live king tommen bless queen margaery
SAM                                                      oh yes
OLENNA                                            hes beaten us
LADY CRANE                                        firstborn son
TALLA                          father says marry symun fossoway
MEERA                                                  im sorry
LOTHAR                                             surprised us
DAENERYS                                 many days ride meereen
BENJEN          led ranging party deep north find white walkers
CERSEI           better youre elsewhere head army sept dungeons
CLARENZO                   beauteous bridge pledge undying love
TOMMEN                                                      way
WAIF                                    

In [129]:
for column in episode_six.columns:
    for x in range(len(episode_six[column])):
        episode_six[column][x] = remove_stops(episode_six[column][x])

In [130]:
episode_six.index = episode_six.index.str.title()

In [131]:
episode_six.head()

0   \
Dickon                                        well   
Gilly                                        green   
Jaime                                         lord   
Woman   long live king tommen bless queen margaery   
Sam                                         oh yes   

                                                       1   \
Dickon                                      brought yards   
Gilly                                       youre nervous   
Jaime                                     sorry interrupt   
Woman                                                None   
Sam     didnt think id ever come back father made reno...   

                                                  2   \
Dickon                             much hunting wall   
Gilly                      thats better nervous mute   
Jaime   speak king tommen house baratheon first name   
Woman                                           None   
Sam        certainly didnt expect introducing family   

                                      3                                 4   \
Dickon                            mmhmmm                      theres thing   
Gilly                    little sam baby                       tell family   
Jaime   already insulted one great house  ive member kingsguard since born   
Woman                               None                              None   
Sam                  yes thats important                    told met north   

                                      5   \
Dickon                              None   
Gilly                     tell far north   
Jaime                youre sitting chair   
Woman                               None   
Sam     well wasnt large piece parchment   

                                             6                       7   \
Dickon                                     None                    None   
Gilly                      didnt tell im really                   think   
Jaime                     walking naked streets  im sent deal blackfish   
Woman                                      None                    None   
Sam     thing ismy father doesnt like wildlings         oh hello mother   

                           8   \
Dickon                   None   
Gilly   happy know lady tarly   
Jaime     im going riverlands   
Woman                    None   
Sam                        oh   

                                                       9                   10  \
Dickon                                               None                None   
Gilly                                          yes course           hard walk   
Jaime   im going give bronn largest bag gold anyones e...                 son   
Woman                                                None                None   
Sam                                                 talla  oh um mother gilly   

                            11                         12  \
Dickon                    None                       None   
Gilly              wield sword  saw eyes way castle black   
Jaime   youll stand trial soon                       None   
Woman                     None                       None   
Sam             oh son samwell                     father   

                            13          14                      15  \
Dickon                    None        None                    None   
Gilly   nights watch came keep  north wall                im angry   
Jaime                     None        None                    None   
Woman                     None        None                    None   
Sam                  beautiful   oh course  oh thats fair distance   

                      16       17      18  \
Dickon              None     None    None   
Gilly   youre thinks sam      sam           
Jaime               None     None    None   
Woman               None     None    None   
Sam               oh yes  rabbits  oh yes   

                                           19    20             21  \
Dickon             

### Episode Seven

In [132]:
df_s6.script_text[6]

[u'\n',
 u'\nMAN: That\u2019s it. Get it to the top.',
 u'\n',
 u'\nMAN #2: Steady. Steady.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: Up she goes.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: Hey, come on. Put your back into it, huh?',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: Here you are, son.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: Oh, gentlemen, please.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY. And you lot, come on. Come on, get it moving. Come on, come on.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: In all my days I\u2019ve never seen a man swing an ax like that. How many men did it take to cut you down?',
 u'\n',
 u'\nSANDOR: Just one.',
 u'\n',
 u'\nRAY: Ooh. he must have been some kind of monster.',
 u'\n',
 u'\n',
 u'\n',
 u'\nSANDOR: ',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: BROTHER RAY\u2019S ENCAMPMENT',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: I think some of the men are a bit afraid of you.',
 u'\n',
 u'\nSANDOR: I\u2019m used to it.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: When I found you, I thought you\u2019d been de

In [133]:
script_text6_07 = df_s6.script_text[6]
print type(script_text6_07)

script_text6_07

<type 'list'>


[u'\n',
 u'\nMAN: That\u2019s it. Get it to the top.',
 u'\n',
 u'\nMAN #2: Steady. Steady.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: Up she goes.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: Hey, come on. Put your back into it, huh?',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: Here you are, son.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: Oh, gentlemen, please.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY. And you lot, come on. Come on, get it moving. Come on, come on.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: In all my days I\u2019ve never seen a man swing an ax like that. How many men did it take to cut you down?',
 u'\n',
 u'\nSANDOR: Just one.',
 u'\n',
 u'\nRAY: Ooh. he must have been some kind of monster.',
 u'\n',
 u'\n',
 u'\n',
 u'\nSANDOR: ',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: BROTHER RAY\u2019S ENCAMPMENT',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: I think some of the men are a bit afraid of you.',
 u'\n',
 u'\nSANDOR: I\u2019m used to it.',
 u'\n',
 u'\n',
 u'\n',
 u'\nRAY: When I found you, I thought you\u2019d been de

In [134]:
script_split7 = [i.split('\n') for i in script_text6_07]
script_split7

[[u'', u''],
 [u'', u'MAN: That\u2019s it. Get it to the top.'],
 [u'', u''],
 [u'', u'MAN #2: Steady. Steady.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'RAY: Up she goes.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'RAY: Hey, come on. Put your back into it, huh?'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'RAY: Here you are, son.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'RAY: Oh, gentlemen, please.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'',
  u'RAY. And you lot, come on. Come on, get it moving. Come on, come on.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'',
  u'RAY: In all my days I\u2019ve never seen a man swing an ax like that. How many men did it take to cut you down?'],
 [u'', u''],
 [u'', u'SANDOR: Just one.'],
 [u'', u''],
 [u'', u'RAY: Ooh. he must have been some kind of monster.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'SANDOR: '],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: BROTHER RAY\u2019S ENCAMPMENT'],
 [u

In [135]:
string_script_text7 = ' '

for i in script_split7:
    for e in i:
        string_script_text7 = string_script_text7 + ' ' + e

In [136]:
string_script_text7

u'     MAN: That\u2019s it. Get it to the top.    MAN #2: Steady. Steady.        RAY: Up she goes.        RAY: Hey, come on. Put your back into it, huh?        RAY: Here you are, son.        RAY: Oh, gentlemen, please.        RAY. And you lot, come on. Come on, get it moving. Come on, come on.        RAY: In all my days I\u2019ve never seen a man swing an ax like that. How many men did it take to cut you down?    SANDOR: Just one.    RAY: Ooh. he must have been some kind of monster.        SANDOR:          CUT TO: BROTHER RAY\u2019S ENCAMPMENT        RAY: I think some of the men are a bit afraid of you.    SANDOR: I\u2019m used to it.        RAY: When I found you, I thought you\u2019d been dead for days. The way you were stinking already and you had bugs all over you and bone was coming through right there.        RAY: I was gonna give you a proper burial and then you coughed. Oh, nearly shit myself. I reckoned you were gonna die by the time I loaded you on the wagon, but you didn\u201

In [137]:
words7 = word_tokenize(string_script_text7)
words7

[u'MAN',
 u':',
 u'That\u2019s',
 u'it',
 u'.',
 u'Get',
 u'it',
 u'to',
 u'the',
 u'top',
 u'.',
 u'MAN',
 u'#',
 u'2',
 u':',
 u'Steady',
 u'.',
 u'Steady',
 u'.',
 u'RAY',
 u':',
 u'Up',
 u'she',
 u'goes',
 u'.',
 u'RAY',
 u':',
 u'Hey',
 u',',
 u'come',
 u'on',
 u'.',
 u'Put',
 u'your',
 u'back',
 u'into',
 u'it',
 u',',
 u'huh',
 u'?',
 u'RAY',
 u':',
 u'Here',
 u'you',
 u'are',
 u',',
 u'son',
 u'.',
 u'RAY',
 u':',
 u'Oh',
 u',',
 u'gentlemen',
 u',',
 u'please',
 u'.',
 u'RAY',
 u'.',
 u'And',
 u'you',
 u'lot',
 u',',
 u'come',
 u'on',
 u'.',
 u'Come',
 u'on',
 u',',
 u'get',
 u'it',
 u'moving',
 u'.',
 u'Come',
 u'on',
 u',',
 u'come',
 u'on',
 u'.',
 u'RAY',
 u':',
 u'In',
 u'all',
 u'my',
 u'days',
 u'I\u2019ve',
 u'never',
 u'seen',
 u'a',
 u'man',
 u'swing',
 u'an',
 u'ax',
 u'like',
 u'that',
 u'.',
 u'How',
 u'many',
 u'men',
 u'did',
 u'it',
 u'take',
 u'to',
 u'cut',
 u'you',
 u'down',
 u'?',
 u'SANDOR',
 u':',
 u'Just',
 u'one',
 u'.',
 u'RAY',
 u':',
 u'Ooh',
 u'.',


In [138]:
sentences7 = sent_tokenize(string_script_text7)
sentences7

[u'     MAN: That\u2019s it.',
 u'Get it to the top.',
 u'MAN #2: Steady.',
 u'Steady.',
 u'RAY: Up she goes.',
 u'RAY: Hey, come on.',
 u'Put your back into it, huh?',
 u'RAY: Here you are, son.',
 u'RAY: Oh, gentlemen, please.',
 u'RAY.',
 u'And you lot, come on.',
 u'Come on, get it moving.',
 u'Come on, come on.',
 u'RAY: In all my days I\u2019ve never seen a man swing an ax like that.',
 u'How many men did it take to cut you down?',
 u'SANDOR: Just one.',
 u'RAY: Ooh.',
 u'he must have been some kind of monster.',
 u'SANDOR:          CUT TO: BROTHER RAY\u2019S ENCAMPMENT        RAY: I think some of the men are a bit afraid of you.',
 u'SANDOR: I\u2019m used to it.',
 u'RAY: When I found you, I thought you\u2019d been dead for days.',
 u'The way you were stinking already and you had bugs all over you and bone was coming through right there.',
 u'RAY: I was gonna give you a proper burial and then you coughed.',
 u'Oh, nearly shit myself.',
 u'I reckoned you were gonna die by the tim

In [139]:
dialogue7 = []

for sentence in sentences7:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names6_07):
            dialogue7.append(sentence)

In [140]:
dialogue7

[u'MAN #2: Steady.',
 u'RAY: Up she goes.',
 u'RAY: Hey, come on.',
 u'RAY: Here you are, son.',
 u'RAY: Oh, gentlemen, please.',
 u'RAY: In all my days I\u2019ve never seen a man swing an ax like that.',
 u'SANDOR: Just one.',
 u'RAY: Ooh.',
 u'SANDOR:          CUT TO: BROTHER RAY\u2019S ENCAMPMENT        RAY: I think some of the men are a bit afraid of you.',
 u'SANDOR: I\u2019m used to it.',
 u'RAY: When I found you, I thought you\u2019d been dead for days.',
 u'RAY: I was gonna give you a proper burial and then you coughed.',
 u'SANDOR: Hate.',
 u'RAY: No, there\u2019s a reason you\u2019re still here.',
 u'SANDOR: Aye, there\u2019s a reason.',
 u'RAY: No, a reason.',
 u'SANDOR: I\u2019ve heard that before.',
 u'RAY: Well, maybe he was right.',
 u'SANDOR: You\u2019re in the wrong line of work.',
 u'RAY: Oh, there\u2019s plenty of pious sons of bitches who think they know the word of god or gods.',
 u'SANDOR: You didn\u2019t know me back in my time.',
 u'RAY: I\u2019ve heard stories.

In [141]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s607.pkl', 'wb') as f:
    pickle.dump(dialogue7, f)

In [142]:
from collections import defaultdict

speakers7 = defaultdict(list)
for sentence in dialogue7:
    speakers7[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers7

defaultdict(list,
            {u'ARYA': [u' You\u2019re Westerosi.',
              u' I want to book passage home.',
              u' Why do you care?',
              u' I want a cabin.',
              u' See you at sunrise.'],
             u'BLACK WALDER': [u' You think I won\u2019t do it, old man?',
              u' I sliced your niece\u2019s throat from ear to ear.',
              u' Whoa, whoa.',
              u' Edmure is a prisoner of House Frey.',
              u' I don\u2019t give a rat\u2019s- -        JAIME',
              u' Those are our siege towers- -    JAIME'],
             u'BRONN': [u' Now, that is a sorry attempt at a siege.',
              u' Oh, no.',
              u' Aye, knights don\u2019t get paid.',
              u' That\u2019s like saying I have a bigger cock than anyone in the Unsullied army.',
              u' You promised me a lordship and a castle and a highborn beauty for a wife.',
              u' Good thing we\u2019re friends or we\u2019d be fucking you

In [143]:
speakers7['BRONN']

[u' Now, that is a sorry attempt at a siege.',
 u' Oh, no.',
 u' Aye, knights don\u2019t get paid.',
 u' That\u2019s like saying I have a bigger cock than anyone in the Unsullied army.',
 u' You promised me a lordship and a castle and a highborn beauty for a wife.',
 u' Good thing we\u2019re friends or we\u2019d be fucking you in the ass right now.',
 u' Have your lads start digging perimeter trenches.',
 u' A parley or a fight?',
 u' You\u2019ve got one hand.']

In [144]:
episode_seven = pd.DataFrame.from_dict(speakers7, orient="index")
print episode_seven.shape

(26, 31)


In [145]:
#from numpy import nan
#episode_seven.fillna(value=str(0), inplace=True)

In [146]:
episode_seven.info()

<class 'pandas.core.frame.DataFrame'>
Index: 26 entries, DAVOS to MAN
Data columns (total 31 columns):
0     26 non-null object
1     23 non-null object
2     23 non-null object
3     21 non-null object
4     21 non-null object
5     18 non-null object
6     15 non-null object
7     14 non-null object
8     12 non-null object
9     11 non-null object
10    10 non-null object
11    8 non-null object
12    8 non-null object
13    8 non-null object
14    7 non-null object
15    6 non-null object
16    5 non-null object
17    3 non-null object
18    3 non-null object
19    3 non-null object
20    2 non-null object
21    2 non-null object
22    1 non-null object
23    1 non-null object
24    1 non-null object
25    1 non-null object
26    1 non-null object
27    1 non-null object
28    1 non-null object
29    1 non-null object
30    1 non-null object
dtypes: object(31)
memory usage: 6.5+ KB


In [147]:
episode_seven.head()

0   \
DAVOS     If it please, my lady, I understand how you f...   
BRONN             Now, that is a sorry attempt at a siege.   
JAIME                              Someone certainly does.   
BRYNDEN                                       Go on, then.   
YARA                             Some of us still like it.   

                                          1   \
DAVOS     Davos, my lady, of House Seaworth.   
BRONN                                Oh, no.   
JAIME             You’re an anointed knight.   
BRYNDEN                          Kingslayer.   
YARA                     Don’t go far, love.   

                                                        2   \
DAVOS     You never thought you’d find yourself in your...   
BRONN                         Aye, knights don’t get paid.   
JAIME     You have better instincts than any officer in...   
BRYNDEN   I assume you’re here to fulfill the vow you g...   
YARA                               I’ll find you in a bit.   

                                                        3   \
DAVOS     Your uncle, Lord Commander Mormont, made that...   
BRONN     That’s like saying I have a bigger cock than ...   
JAIME     I expect to command all the Lannister forces ...   
BRYNDEN                                              Pity.   
YARA      Nothing on the Iron Islands has an ass like t...   

                                                        4   \
DAVOS     As long as the Boltons hold Winterfell, the N...   
BRONN     You promised me a lordship and a castle and a...   
JAIME                            And you’ll get all three.   
BRYNDEN                             Then why are you here?   
YARA                                            I’m sorry.   

                                                        5   \
DAVOS     If they’re half as ferocious as their lady, t...   
BRONN     Good thing we’re friends or we’d be fucking y...   
JAIME                                       Lothar, is it?   
BRYNDEN       My nephew’s marked for death no matter what.   
YARA                                      Of course he is.   

                                                        6   \
DAVOS        Stannis camped here on his way to Winterfell.   
BRONN     Have your lads start digging perimeter trenches.   
JAIME         ‘Cause you didn’t set up a proper perimeter.   
BRYNDEN                                  Hundreds of mine.   
YARA        It’s a great big world and we have fast ships.   

                                                        7   \
DAVOS     He was the most experienced commander in West...   
BRONN                                 A parley or a fight?   
JAIME                     Have Lord Edmure bathed and fed.   
BRYNDEN                                        Your honor?   
YARA                           I don’t care what you want.   

                                                        8   \
DAVOS                                     2,000 Wildlings.   
BRONN                                 You’ve got one hand.   
JAIME     Only a fool makes threats he’s not prepared t...   
BRYNDEN      As long as I’m standing, the war is not over.   
YARA                                         Drink it all.   

                                          9   \
DAVOS          It’s not what we’d hoped for.   
BRONN                                   None   
JAIME     The siege is now under my command.   
BRYNDEN                     Sieges are dull.   
YARA                 You’re Ironborn, Theon.   

                                                        10  \
DAVOS                                     For fuck’s sake.   
BRONN                                                 None   
JAIME                           Get word to the Blackfish.   
BRYNDEN                                   Aye, now I have.   
YARA      But I’m tired of watching you cower like a be...   

                                                 11  \
DAVOS     Friends, this is not worth fighting over!   
BRONN      

In [148]:
test7 = episode_seven[0].apply(remove_stops)
test7

DAVOS           please lady understand feel
BRONN                   sorry attempt siege
JAIME                     someone certainly
BRYNDEN                                  go
YARA                          us still like
WOMAN                            sweet girl
OLENNA                           oh madness
LOTHAR                         last warning
RAY                                    goes
THEON                         dont want one
CERSEI          heard leaving kings landing
DIM DALBA              remember mances camp
SANDOR                                  one
ROBETT                               answer
LYANNA                  welcome bear island
MARGAERY               book mother holiness
JON SNOW           thats whatll happen lose
SANSA                    remember born lady
MAN #2                               steady
LEM                                        
WUN WUN                                snow
TORMUND                werent none us would
HIGH SPARROW                    

In [149]:
for column in episode_seven.columns:
    for x in range(len(episode_seven[column])):
        episode_seven[column][x] = remove_stops(episode_seven[column][x])

In [150]:
episode_seven.index = episode_seven.index.str.title()

In [151]:
episode_seven.head()

0                          1   \
Davos    please lady understand feel  davos lady house seaworth   
Bronn            sorry attempt siege                         oh   
Jaime              someone certainly      youre anointed knight   
Brynden                           go                 kingslayer   
Yara                   us still like           dont go far love   

                                              2   \
Davos           never thought youd find position   
Bronn                  aye knights dont get paid   
Jaime    better instincts officer lannister army   
Brynden      assume youre fulfill vow gave niece   
Yara                                ill find bit   

                                                        3   \
Davos        uncle lord commander mormont made man steward   
Bronn    thats like saying bigger cock anyone unsullied...   
Jaime                 expect command lannister forces long   
Brynden                                               pity   
Yara                         nothing iron islands ass like   

                                                    4   \
Davos       long boltons hold winterfell north divided   
Bronn    promised lordship castle highborn beauty wife   
Jaime                                  youll get three   
Brynden                                                  
Yara                                          im sorry   

                                                5   \
Davos    theyre half ferocious lady boltons doomed   
Bronn     good thing friends wed fucking ass right   
Jaime                                       lothar   
Brynden                nephews marked death matter   
Yara                                        course   

                                            6   \
Davos            stannis camped way winterfell   
Bronn    lads start digging perimeter trenches   
Jaime         cause didnt set proper perimeter   
Brynden                          hundreds mine   
Yara                great big world fast ships   

                                     7   \
Davos    experienced commander westeros   
Bronn                      parley fight   
Jaime            lord edmure bathed fed   
Brynden                           honor   
Yara                     dont care want   

                                            8                     9   \
Davos                                wildlings             wed hoped   
Bronn                       youve got one hand                  None   
Jaime    fool makes threats hes prepared carry         siege command   
Brynden                   long im standing war           sieges dull   
Yara                                     drink  youre ironborn theon   

                                            10                      11  \
Davos                               fucks sake  friends worth fighting   
Bronn                                     None                    None   
Jaime                       get word blackfish             hes old man   
Brynden                                    aye                    None   
Yara     im tired watching cower like beat dog                  listen   

                   12            13       14                15  \
Davos          thisll          hold     None              None   
Bronn            None          None     None              None   
Jaime       blackfish          dont  know im  wont stop edmure   
Brynden          None          None     None              None   
Yara     escaped hear  fuck justice   listen                     

                                                        16       17  \
Davos                                                 None     None   
Bronn                                                 None     None   
Jaime                      well breach kill every last one  war ser   
Brynden                                               None     None   
Yara     since last night ashore long im gonna go fuck ...     None   

         

### Episode Eight

In [152]:
df_s6.script_text[7]

[u' The Bloody Hand. ',
 u'\n',
 u'\nLADY CRANE: My son. My firstborn son. My child king, hush. Listen to the gods, for you they sing. Fight no more, sweet child. Your wars are won. The wolves are buried and the false stag done. Shut your blue eyes, my love. Let the crown fall. The Father above beckons you into his hall. In Seventh Heaven I\u2019ll see you once more. But now I seek vengeance on Sansa the whore and my brother the Imp who killed his own king. Born amongst lions, our curse from within. I will slay him, I swear. With noose or with knife, though it take me a fortnight, a moon, or my life.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: BRAAVOS - LADY CRANE\u2019S APARTMENT',
 u'\n',
 u'\n',
 u'\n',
 u'\nARYA: You\u2019re good at that. Where did you learn?',
 u'\n',
 u'\nLADY CRANE: I\u2019m a jealous woman. I\u2019ve always liked bad men and they\u2019ve always liked me. They\u2019d come home wherever home was that night stinking of some whore\u2019s perfume.',
 u'\n',
 u'\n',

In [153]:
script_text6_08 = df_s6.script_text[7]
print type(script_text6_08)

script_text6_08

<type 'list'>


[u' The Bloody Hand. ',
 u'\n',
 u'\nLADY CRANE: My son. My firstborn son. My child king, hush. Listen to the gods, for you they sing. Fight no more, sweet child. Your wars are won. The wolves are buried and the false stag done. Shut your blue eyes, my love. Let the crown fall. The Father above beckons you into his hall. In Seventh Heaven I\u2019ll see you once more. But now I seek vengeance on Sansa the whore and my brother the Imp who killed his own king. Born amongst lions, our curse from within. I will slay him, I swear. With noose or with knife, though it take me a fortnight, a moon, or my life.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: BRAAVOS - LADY CRANE\u2019S APARTMENT',
 u'\n',
 u'\n',
 u'\n',
 u'\nARYA: You\u2019re good at that. Where did you learn?',
 u'\n',
 u'\nLADY CRANE: I\u2019m a jealous woman. I\u2019ve always liked bad men and they\u2019ve always liked me. They\u2019d come home wherever home was that night stinking of some whore\u2019s perfume.',
 u'\n',
 u'\n',

In [154]:
script_split8 = [i.split('\n') for i in script_text6_08]
script_split8

[[u' The Bloody Hand. '],
 [u'', u''],
 [u'',
  u'LADY CRANE: My son. My firstborn son. My child king, hush. Listen to the gods, for you they sing. Fight no more, sweet child. Your wars are won. The wolves are buried and the false stag done. Shut your blue eyes, my love. Let the crown fall. The Father above beckons you into his hall. In Seventh Heaven I\u2019ll see you once more. But now I seek vengeance on Sansa the whore and my brother the Imp who killed his own king. Born amongst lions, our curse from within. I will slay him, I swear. With noose or with knife, though it take me a fortnight, a moon, or my life.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: BRAAVOS - LADY CRANE\u2019S APARTMENT'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'ARYA: You\u2019re good at that. Where did you learn?'],
 [u'', u''],
 [u'',
  u'LADY CRANE: I\u2019m a jealous woman. I\u2019ve always liked bad men and they\u2019ve always liked me. They\u2019d come home wherever home was 

In [155]:
string_script_text8 = ' '

for i in script_split8:
    for e in i:
        string_script_text8 = string_script_text8 + ' ' + e

In [156]:
string_script_text8

u'   The Bloody Hand.     LADY CRANE: My son. My firstborn son. My child king, hush. Listen to the gods, for you they sing. Fight no more, sweet child. Your wars are won. The wolves are buried and the false stag done. Shut your blue eyes, my love. Let the crown fall. The Father above beckons you into his hall. In Seventh Heaven I\u2019ll see you once more. But now I seek vengeance on Sansa the whore and my brother the Imp who killed his own king. Born amongst lions, our curse from within. I will slay him, I swear. With noose or with knife, though it take me a fortnight, a moon, or my life.         CUT TO: BRAAVOS - LADY CRANE\u2019S APARTMENT        ARYA: You\u2019re good at that. Where did you learn?    LADY CRANE: I\u2019m a jealous woman. I\u2019ve always liked bad men and they\u2019ve always liked me. They\u2019d come home wherever home was that night stinking of some whore\u2019s perfume.        LADY CRANE: So we\u2019d fight and I\u2019d put a hole in them. And then I\u2019d feel

In [157]:
words8 = word_tokenize(string_script_text8)
words8

[u'The',
 u'Bloody',
 u'Hand',
 u'.',
 u'LADY',
 u'CRANE',
 u':',
 u'My',
 u'son',
 u'.',
 u'My',
 u'firstborn',
 u'son',
 u'.',
 u'My',
 u'child',
 u'king',
 u',',
 u'hush',
 u'.',
 u'Listen',
 u'to',
 u'the',
 u'gods',
 u',',
 u'for',
 u'you',
 u'they',
 u'sing',
 u'.',
 u'Fight',
 u'no',
 u'more',
 u',',
 u'sweet',
 u'child',
 u'.',
 u'Your',
 u'wars',
 u'are',
 u'won',
 u'.',
 u'The',
 u'wolves',
 u'are',
 u'buried',
 u'and',
 u'the',
 u'false',
 u'stag',
 u'done',
 u'.',
 u'Shut',
 u'your',
 u'blue',
 u'eyes',
 u',',
 u'my',
 u'love',
 u'.',
 u'Let',
 u'the',
 u'crown',
 u'fall',
 u'.',
 u'The',
 u'Father',
 u'above',
 u'beckons',
 u'you',
 u'into',
 u'his',
 u'hall',
 u'.',
 u'In',
 u'Seventh',
 u'Heaven',
 u'I\u2019ll',
 u'see',
 u'you',
 u'once',
 u'more',
 u'.',
 u'But',
 u'now',
 u'I',
 u'seek',
 u'vengeance',
 u'on',
 u'Sansa',
 u'the',
 u'whore',
 u'and',
 u'my',
 u'brother',
 u'the',
 u'Imp',
 u'who',
 u'killed',
 u'his',
 u'own',
 u'king',
 u'.',
 u'Born',
 u'amongst',
 u

In [158]:
sentences8 = sent_tokenize(string_script_text8)
sentences8

[u'   The Bloody Hand.',
 u'LADY CRANE: My son.',
 u'My firstborn son.',
 u'My child king, hush.',
 u'Listen to the gods, for you they sing.',
 u'Fight no more, sweet child.',
 u'Your wars are won.',
 u'The wolves are buried and the false stag done.',
 u'Shut your blue eyes, my love.',
 u'Let the crown fall.',
 u'The Father above beckons you into his hall.',
 u'In Seventh Heaven I\u2019ll see you once more.',
 u'But now I seek vengeance on Sansa the whore and my brother the Imp who killed his own king.',
 u'Born amongst lions, our curse from within.',
 u'I will slay him, I swear.',
 u'With noose or with knife, though it take me a fortnight, a moon, or my life.',
 u'CUT TO: BRAAVOS - LADY CRANE\u2019S APARTMENT        ARYA: You\u2019re good at that.',
 u'Where did you learn?',
 u'LADY CRANE: I\u2019m a jealous woman.',
 u'I\u2019ve always liked bad men and they\u2019ve always liked me.',
 u'They\u2019d come home wherever home was that night stinking of some whore\u2019s perfume.',
 u'LA

In [159]:
dialogue8 = []

for sentence in sentences8:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names6_08):
            dialogue8.append(sentence)

In [160]:
dialogue8

[u'LADY CRANE: My son.',
 u'LADY CRANE: I\u2019m a jealous woman.',
 u'LADY CRANE: So we\u2019d fight and I\u2019d put a hole in them.',
 u'ARYA: And good at putting holes in them.',
 u'LADY CRANE: And that.',
 u'ARYA: What happened to the actress?',
 u'LADY CRANE: Bianca.',
 u'LADY CRANE: She\u2019ll have a hard time finding work as an actress after what I did to her face.',
 u'ARYA: Mmm.',
 u'LADY CRANE: I never did learn to cook.',
 u'ARYA: I can\u2019t.',
 u'LADY CRANE: Why not?',
 u'ARYA: I don\u2019t think I could remember all of the lines.',
 u'LADY CRANE: Come with us.',
 u'ARYA: You wouldn\u2019t be safe.',
 u'LADY CRANE: Who?',
 u'ARYA: She doesn\u2019t have a name.',
 u'LADY CRANE: Where will you go?',
 u'ARYA: What\u2019s that?',
 u'LADY CRANE: Milk of the poppy.',
 u'ARYA: I don\u2019t want any.',
 u'LADY CRANE: Sleep is the only way you\u2019ll heal.',
 u'MAN: Thing about Gatins, right, is he used to be pretty.',
 u'GATINS: I was a famous kisser.',
 u'YOUNG MAN: Course we

In [161]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s608.pkl', 'wb') as f:
    pickle.dump(dialogue8, f)

In [162]:
from collections import defaultdict

speakers8 = defaultdict(list)
for sentence in dialogue8:
    speakers8[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers8

defaultdict(list,
            {u'ARYA': [u' And good at putting holes in them.',
              u' What happened to the actress?',
              u' Mmm.',
              u' I can\u2019t.',
              u' I don\u2019t think I could remember all of the lines.',
              u' You wouldn\u2019t be safe.',
              u' She doesn\u2019t have a name.',
              u' What\u2019s that?',
              u' I don\u2019t want any.',
              u' Lady Crane?',
              u' Lady Crane?',
              u' A girl is Arya Stark of Winterfell and I\u2019m going home.'],
             u'BERIC': [u' Clegane.',
              u' They\u2019re our men.',
              u' It\u2019s the Brotherhood\u2019s good name they\u2019ve dragged through the dirt.',
              u' You can have one of them.',
              u' No.',
              u' We gave you two of the three out of respect for your loss.',
              u' You ought to join us.',
              u' Cold winds are rising in the North.',
  

In [163]:
speakers8['ARYA']

[u' And good at putting holes in them.',
 u' What happened to the actress?',
 u' Mmm.',
 u' I can\u2019t.',
 u' I don\u2019t think I could remember all of the lines.',
 u' You wouldn\u2019t be safe.',
 u' She doesn\u2019t have a name.',
 u' What\u2019s that?',
 u' I don\u2019t want any.',
 u' Lady Crane?',
 u' Lady Crane?',
 u' A girl is Arya Stark of Winterfell and I\u2019m going home.']

In [164]:
episode_eight = pd.DataFrame.from_dict(speakers8, orient="index")
print episode_eight.shape

(29, 36)


In [165]:
#from numpy import nan
#episode_eight.fillna(value=str(0), inplace=True)

In [166]:
episode_eight.info()

<class 'pandas.core.frame.DataFrame'>
Index: 29 entries, KEVAN to MAN
Data columns (total 36 columns):
0     29 non-null object
1     26 non-null object
2     23 non-null object
3     22 non-null object
4     19 non-null object
5     18 non-null object
6     18 non-null object
7     18 non-null object
8     15 non-null object
9     13 non-null object
10    12 non-null object
11    9 non-null object
12    8 non-null object
13    6 non-null object
14    6 non-null object
15    5 non-null object
16    5 non-null object
17    5 non-null object
18    4 non-null object
19    4 non-null object
20    4 non-null object
21    4 non-null object
22    4 non-null object
23    4 non-null object
24    3 non-null object
25    3 non-null object
26    3 non-null object
27    3 non-null object
28    3 non-null object
29    2 non-null object
30    2 non-null object
31    2 non-null object
32    2 non-null object
33    1 non-null object
34    1 non-null object
35    1 non-null object
dtypes: object(36)
mem

In [167]:
episode_eight.head()

0   \
KEVAN                                              There is.   
BRONN                                 Podrick fucking Payne.   
JAIME       In my experience, girls like her don’t live v...   
TYRION                    I’d call that a successful gambit.   
MISSANDEI                                    You seem happy.   

                                                          1   \
KEVAN       There is to be a royal announcement in the th...   
BRONN                                     Are they in there?   
JAIME                                Well, I’m proud of you.   
TYRION                                          Look around.   
MISSANDEI            I will be happy when our queen returns.   

                                     2   \
KEVAN              Where are you going?   
BRONN        You think they’re fucking?   
JAIME       You’re welcome to have him.   
TYRION             I did and it worked.   
MISSANDEI     I have tried wine before.   

                                                          3   \
KEVAN       Your place is in the gallery with the other l...   
BRONN                                               Why not?   
JAIME       With what army does she plan on taking Winter...   
TYRION         Spoken like a man who has never had to shave.   
MISSANDEI                           I do not know any jokes.   

                                               4   \
KEVAN                                        None   
BRONN                                         Oh.   
JAIME       They’re a bit occupied at the moment.   
TYRION                     I’m going to miss you.   
MISSANDEI    A joke is like a story, Torgo Nudho.   

                                                          5   \
KEVAN                                                   None   
BRONN                  You must have shown it to her by now.   
JAIME       Riverrun was granted to the Freys by royal de...   
TYRION      I hope you’re right about this expedition of ...   
MISSANDEI                                              I do.   

                                                6   \
KEVAN                                         None   
BRONN                                      Is she?   
JAIME                                     Exactly.   
TYRION             Most of all, we need our queen.   
MISSANDEI   Two translators are on a sinking ship.   

                                                          7   \
KEVAN                                                   None   
BRONN       Then how come an old cunt like me can still s...   
JAIME                     We shouldn’t argue about politics.   
TYRION                                                Varys.   
MISSANDEI   The first says, “Do you know how to swim?” Th...   

                                             8   \
KEVAN                                      None   
BRONN          Now, that’s the truth, isn’t it?   
JAIME                          I’m a Lannister.   
TYRION      The most famous dwarf in the world.   
MISSANDEI   You don’t even know what a joke is.   

                                                    9   \
KEVAN                                             None   
BRONN       All right, let’s start with your footwork.   
JAIME                             What do you propose?   
TYRION                                     I am happy.   
MISSANDEI                                  More jokes.   

                                                  10  \
KEVAN                                           None   
BRONN                           Show me your stance.   
JAIME       Why would he abandon his ancestral home?   
TYRION                   Now it’s like a man reborn.   
MISSANDEI                      That changes nothing.   

                                          11  \
KEVAN                                   None   
BRONN                Now, listen to me, Pod.   
JAIME       Have you ever met the Blackfish?   
TYRION                  Why don’t you drink? 

In [168]:
test8 = episode_eight[0].apply(remove_stops)
test8

KEVAN                                                             
BRONN                                        podrick fucking payne
JAIME                         experience girls like dont live long
TYRION                                   id call successful gambit
MISSANDEI                                               seem happy
CROWD                                              seven blessings
LADY CRANE                                                     son
GUARD                                                      aye ser
GUARD CAPTAIN                                    hes lord riverrun
THOROS                                                        fuck
GATINS                                               famous kisser
TOMMEN             lords ladies faith crown two pillars hold world
GREY WORM                                    unsullied never drink
YOUNG MAN                                                   course
VARYS                                                        w

In [169]:
for column in episode_eight.columns:
    for x in range(len(episode_eight[column])):
        episode_eight[column][x] = remove_stops(episode_eight[column][x])

In [170]:
episode_eight.index = episode_eight.index.str.title()

In [171]:
episode_eight.head()

0   \
Kevan                                             
Bronn                     podrick fucking payne   
Jaime      experience girls like dont live long   
Tyrion                id call successful gambit   
Missandei                            seem happy   

                                              1                     2   \
Kevan      royal announcement throne room moment                 going   
Bronn                                             think theyre fucking   
Jaime                              well im proud         youre welcome   
Tyrion                               look around                worked   
Missandei                    happy queen returns            tried wine   

                                    3                            4   \
Kevan       place gallery ladies court                         None   
Bronn                                                            oh   
Jaime      army plan taking winterfell   theyre bit occupied moment   
Tyrion     spoken like man never shave                im going miss   
Missandei                   know jokes  joke like story torgo nudho   

                                            5                             6   \
Kevan                                     None                          None   
Bronn                               must shown                                 
Jaime      riverrun granted freys royal decree                       exactly   
Tyrion             hope youre right expedition                    need queen   
Missandei                                       two translators sinking ship   

                                                          7   \
Kevan                                                   None   
Bronn                  come old cunt like still sneak murder   
Jaime                                shouldnt argue politics   
Tyrion                                                 varys   
Missandei  first says know swim second says shout help la...   

                            8                          9   \
Kevan                     None                       None   
Bronn         thats truth isnt  right lets start footwork   
Jaime             im lannister                    propose   
Tyrion      famous dwarf world                      happy   
Missandei  dont even know joke                      jokes   

                                     10                  11  \
Kevan                              None                None   
Bronn                       show stance          listen pod   
Jaime      would abandon ancestral home  ever met blackfish   
Tyrion                  like man reborn          dont drink   
Missandei               changes nothing                None   

                                                    12          13  \
Kevan                                             None        None   
Bronn      lesson number one assume everyone wants hit        None   
Jaime                                hes even stubborn       right   
Tyrion                                                  made rules   
Missandei                                         None        None   

                                             14                  15  \
Kevan                                      None                None   
Bronn                                      None                None   
Jaime                                      word                       
Tyrion     miserable old shits didnt want human  thats know working   
Missandei                                  None                None   

                         16  \
Kevan                  None   
Bronn                  None   
Jaime      yes lady brienne   
Tyrion          heres queen   
Missandei              None   

                                                          17  \
Kevan                                                   None   
Bronn                                                   None   
Jaime                      

### Episode Nine

In [172]:
df_s6.script_text[8]

[u'\n',
 u'\nTYRION: Despite appearances, I think you\u2019ll find the city\u2019s on the rise.',
 u'\n',
 u'\n',
 u'\n',
 u'\nTYRION: Perhaps we should take shelter.',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAENERYS: The city is on the rise?',
 u'\n',
 u'\nTYRION: Meereen is strong. Commerce has returned to the markets. The people are behind you.',
 u'\n',
 u'\n',
 u'\n',
 u'\nTYRION: Well, not all the people, of course. No ruler that ever lived had the support of all the people. But the rebirth of Meereen is the cause of this violence. The Masters cannot let Meereen succeed. Because if Meereen succeeds, a city without slavery, a city without Masters\u2026',
 u'\n',
 u'\n',
 u'\n',
 u'\nTYRION: ...it proves that no one needs a Master.',
 u'\n',
 u'\nDAENERYS: Good. Shall we begin?',
 u'\n',
 u'\nTYRION: Do we have a plan?',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAENERYS: You don\u2019t approve?',
 u'\n',
 u'\nTYRION: You once told me you knew what your father was. Did you know his plans 

In [173]:
script_text6_09 = df_s6.script_text[8]
print type(script_text6_09)

script_text6_09

<type 'list'>


[u'\n',
 u'\nTYRION: Despite appearances, I think you\u2019ll find the city\u2019s on the rise.',
 u'\n',
 u'\n',
 u'\n',
 u'\nTYRION: Perhaps we should take shelter.',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAENERYS: The city is on the rise?',
 u'\n',
 u'\nTYRION: Meereen is strong. Commerce has returned to the markets. The people are behind you.',
 u'\n',
 u'\n',
 u'\n',
 u'\nTYRION: Well, not all the people, of course. No ruler that ever lived had the support of all the people. But the rebirth of Meereen is the cause of this violence. The Masters cannot let Meereen succeed. Because if Meereen succeeds, a city without slavery, a city without Masters\u2026',
 u'\n',
 u'\n',
 u'\n',
 u'\nTYRION: ...it proves that no one needs a Master.',
 u'\n',
 u'\nDAENERYS: Good. Shall we begin?',
 u'\n',
 u'\nTYRION: Do we have a plan?',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAENERYS: You don\u2019t approve?',
 u'\n',
 u'\nTYRION: You once told me you knew what your father was. Did you know his plans 

In [174]:
script_split9 = [i.split('\n') for i in script_text6_09]
script_split9

[[u'', u''],
 [u'',
  u'TYRION: Despite appearances, I think you\u2019ll find the city\u2019s on the rise.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'TYRION: Perhaps we should take shelter.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'DAENERYS: The city is on the rise?'],
 [u'', u''],
 [u'',
  u'TYRION: Meereen is strong. Commerce has returned to the markets. The people are behind you.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'',
  u'TYRION: Well, not all the people, of course. No ruler that ever lived had the support of all the people. But the rebirth of Meereen is the cause of this violence. The Masters cannot let Meereen succeed. Because if Meereen succeeds, a city without slavery, a city without Masters\u2026'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'TYRION: ...it proves that no one needs a Master.'],
 [u'', u''],
 [u'', u'DAENERYS: Good. Shall we begin?'],
 [u'', u''],
 [u'', u'TYRION: Do we have a plan?'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u

In [175]:
string_script_text9 = ' '

for i in script_split9:
    for e in i:
        string_script_text9 = string_script_text9 + ' ' + e

In [176]:
string_script_text9

u'     TYRION: Despite appearances, I think you\u2019ll find the city\u2019s on the rise.        TYRION: Perhaps we should take shelter.        DAENERYS: The city is on the rise?    TYRION: Meereen is strong. Commerce has returned to the markets. The people are behind you.        TYRION: Well, not all the people, of course. No ruler that ever lived had the support of all the people. But the rebirth of Meereen is the cause of this violence. The Masters cannot let Meereen succeed. Because if Meereen succeeds, a city without slavery, a city without Masters\u2026        TYRION: ...it proves that no one needs a Master.    DAENERYS: Good. Shall we begin?    TYRION: Do we have a plan?            DAENERYS: You don\u2019t approve?    TYRION: You once told me you knew what your father was. Did you know his plans for King\u2019s Landing when the Lannister armies were at his gates?        TYRION: Probably not. Well, he told my brother and Jaime told me.   He would have burned every one of his citi

In [177]:
words9 = word_tokenize(string_script_text9)
words9

[u'TYRION',
 u':',
 u'Despite',
 u'appearances',
 u',',
 u'I',
 u'think',
 u'you\u2019ll',
 u'find',
 u'the',
 u'city\u2019s',
 u'on',
 u'the',
 u'rise',
 u'.',
 u'TYRION',
 u':',
 u'Perhaps',
 u'we',
 u'should',
 u'take',
 u'shelter',
 u'.',
 u'DAENERYS',
 u':',
 u'The',
 u'city',
 u'is',
 u'on',
 u'the',
 u'rise',
 u'?',
 u'TYRION',
 u':',
 u'Meereen',
 u'is',
 u'strong',
 u'.',
 u'Commerce',
 u'has',
 u'returned',
 u'to',
 u'the',
 u'markets',
 u'.',
 u'The',
 u'people',
 u'are',
 u'behind',
 u'you',
 u'.',
 u'TYRION',
 u':',
 u'Well',
 u',',
 u'not',
 u'all',
 u'the',
 u'people',
 u',',
 u'of',
 u'course',
 u'.',
 u'No',
 u'ruler',
 u'that',
 u'ever',
 u'lived',
 u'had',
 u'the',
 u'support',
 u'of',
 u'all',
 u'the',
 u'people',
 u'.',
 u'But',
 u'the',
 u'rebirth',
 u'of',
 u'Meereen',
 u'is',
 u'the',
 u'cause',
 u'of',
 u'this',
 u'violence',
 u'.',
 u'The',
 u'Masters',
 u'can',
 u'not',
 u'let',
 u'Meereen',
 u'succeed',
 u'.',
 u'Because',
 u'if',
 u'Meereen',
 u'succeeds',


In [178]:
sentences9 = sent_tokenize(string_script_text9)
sentences9

[u'     TYRION: Despite appearances, I think you\u2019ll find the city\u2019s on the rise.',
 u'TYRION: Perhaps we should take shelter.',
 u'DAENERYS: The city is on the rise?',
 u'TYRION: Meereen is strong.',
 u'Commerce has returned to the markets.',
 u'The people are behind you.',
 u'TYRION: Well, not all the people, of course.',
 u'No ruler that ever lived had the support of all the people.',
 u'But the rebirth of Meereen is the cause of this violence.',
 u'The Masters cannot let Meereen succeed.',
 u'Because if Meereen succeeds, a city without slavery, a city without Masters\u2026        TYRION: ...it proves that no one needs a Master.',
 u'DAENERYS: Good.',
 u'Shall we begin?',
 u'TYRION: Do we have a plan?',
 u'DAENERYS: You don\u2019t approve?',
 u'TYRION: You once told me you knew what your father was.',
 u'Did you know his plans for King\u2019s Landing when the Lannister armies were at his gates?',
 u'TYRION: Probably not.',
 u'Well, he told my brother and Jaime told me.',
 u

In [179]:
dialogue9 = []

for sentence in sentences9:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names6_09):
            dialogue9.append(sentence)

In [180]:
dialogue9

[u'TYRION: Perhaps we should take shelter.',
 u'DAENERYS: The city is on the rise?',
 u'TYRION: Meereen is strong.',
 u'TYRION: Well, not all the people, of course.',
 u'DAENERYS: Good.',
 u'TYRION: Do we have a plan?',
 u'DAENERYS: You don\u2019t approve?',
 u'TYRION: You once told me you knew what your father was.',
 u'TYRION: Probably not.',
 u'DAENERYS: This is entirely different.',
 u'TYRION: You\u2019re talking about destroying cities.',
 u'TYRION: We are here to discuss terms of surrender, not to trade insults.',
 u'YEZZAN: The terms are simple.',
 u'DAENERYS: We obviously didn\u2019t communicate clearly.',
 u'RAZDAL: I imagine it\u2019s difficult adjust to the new reality.',
 u'DAENERYS: My reign has just begun.',
 u'TYRION: Thank you for the armada.',
 u'MISSANDEI: Our queen insists that one of you must die as punishment for your crimes.',
 u'TYRION: It always seems a bit abstract, doesn\u2019t it, other people dying?',
 u'RAZDAL: Him.',
 u'BELICHO: Yes, him.',
 u'RAZDAL: He\u

In [181]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s609.pkl', 'wb') as f:
    pickle.dump(dialogue9, f)

In [182]:
from collections import defaultdict

speakers9 = defaultdict(list)
for sentence in dialogue9:
    speakers9[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers9

defaultdict(list,
            {u'ALL': [u' We do!', u' We do!'],
             u'BELICHO': [u' Yes, him.'],
             u'DAENERYS': [u' The city is on the rise?',
              u' Good.',
              u' You don\u2019t approve?',
              u' This is entirely different.',
              u' We obviously didn\u2019t communicate clearly.',
              u' My reign has just begun.',
              u' You\u2019ve brought us 100 ships from the Iron Fleet with men to sail them.',
              u' And what\u2019s wrong with you?',
              u' Has the Iron Islands ever had a queen before?',
              u' Lord Tyrion tells me your father was a terrible king.',
              u' We do.',
              u' Will their ships be enough?',
              u' So why shouldn\u2019t I wait for him?',
              u' And I imagine your offer is free of any marriage demands?',
              u' And you don\u2019t want the Seven Kingdoms?',
              u' And that\u2019s all?',
              u' R

In [183]:
speakers9['DAVOS']

[u' That\u2019s not his way.',
 u' It\u2019s crucial that we let them charge at us.',
 u' We should all get some sleep.',
 u' It wasn\u2019t the Boltons defeated Stannis.',
 u' What?',
 u' No, it\u2019s a manner of speaking.',
 u' Maybe that was our mistake, believing in kings.',
 u' No, he\u2019s not.',
 u' No, thanks.',
 u' I walk.',
 u' Prepare to charge!',
 u' Go!',
 u' We\u2019ll just kill our own men.',
 u' Follow!',
 u' With me, lads!']

In [184]:
episode_nine = pd.DataFrame.from_dict(speakers9, orient="index")
print episode_nine.shape

(19, 28)


In [185]:
#from numpy import nan
#episode_nine.fillna(value=str(0), inplace=True)

In [186]:
episode_nine.info()

<class 'pandas.core.frame.DataFrame'>
Index: 19 entries, YARA to RAMSAY
Data columns (total 28 columns):
0     19 non-null object
1     15 non-null object
2     13 non-null object
3     10 non-null object
4     10 non-null object
5     10 non-null object
6     10 non-null object
7     9 non-null object
8     8 non-null object
9     8 non-null object
10    7 non-null object
11    7 non-null object
12    7 non-null object
13    6 non-null object
14    6 non-null object
15    4 non-null object
16    4 non-null object
17    3 non-null object
18    3 non-null object
19    3 non-null object
20    1 non-null object
21    1 non-null object
22    1 non-null object
23    1 non-null object
24    1 non-null object
25    1 non-null object
26    1 non-null object
27    1 non-null object
dtypes: object(28)
memory usage: 4.3+ KB


In [187]:
episode_nine.head()

0   \
YARA       And he paid for them.   
DAVOS        That’s not his way.   
KARSTARK        Cavalry, charge!   
SANSA                 Yes, I do.   
MAN #2             Get him back!   

                                                    1   \
YARA                            No more than Westeros.   
DAVOS      It’s crucial that we let them charge at us.   
KARSTARK                                          None   
SANSA                     How do we know you have him?   
MAN #2                                            None   

                                                         2   \
YARA                         You and I have that in common.   
DAVOS                         We should all get some sleep.   
KARSTARK                                               None   
SANSA      So you’ve met the enemy, drawn up your battle...   
MAN #2                                                 None   

                                                         3   \
YARA       I never demand, but I’m up for anything, really.   
DAVOS               It wasn’t the Boltons defeated Stannis.   
KARSTARK                                               None   
SANSA      You’ve known him for the space of a single co...   
MAN #2                                                 None   

                                                         4   \
YARA       We’d like you to help us murder an uncle or t...   
DAVOS                                                 What?   
KARSTARK                                               None   
SANSA          You think he’s going to fall into your trap.   
MAN #2                                                 None   

                                       5   \
YARA              That’s our way of life.   
DAVOS      No, it’s a manner of speaking.   
KARSTARK                             None   
SANSA               He plays with people.   
MAN #2                               None   

                                                        6   \
YARA                                              No more.   
DAVOS      Maybe that was our mistake, believing in kings.   
KARSTARK                                              None   
SANSA                                  You don’t know him.   
MAN #2                                                None   

                                  7                       8               9   \
YARA                            None                    None            None   
DAVOS                  No, he’s not.             No, thanks.         I walk.   
KARSTARK                        None                    None            None   
SANSA      We’ll never get him back.   Listen to me, please.   I don’t know!   
MAN #2                          None                    None            None   

                                  10  \
YARA                            None   
DAVOS             Prepare to charge!   
KARSTARK                        None   
SANSA      You think that’s obvious?   
MAN #2                          None   

                                                         11  \
YARA                                                   None   
DAVOS                                                   Go!   
KARSTARK                                               None   
SANSA      If you had asked for my advice earlier, I wou...   
MAN #2                                                 None   

                                     12  \
YARA                               None   
DAVOS      We’ll just kill our own men.   
KARSTARK                           None   
SANSA                  It’s not enough!   
MAN #2                             None   

                                                        13  \
YARA                                                  None   
DAVOS                                              Follow!   
KARSTARK                                              None   
SANSA      If Ramsay wins, I’m not going back there alive.   
MAN #2       

In [188]:
test9 = episode_nine[0].apply(remove_stops)
test9

YARA                                                  paid
DAVOS                                            thats way
KARSTARK                                    cavalry charge
SANSA                                                  yes
MAN #2                                            get back
TYRION                                perhaps take shelter
MELISANDRE                                      im soldier
ALL                                                       
SMALLJON                                        owns north
TORMUND                      stannis cut us like piss snow
RAZDAL                imagine difficult adjust new reality
YEZZAN                                        terms simple
DAENERYS                                         city rise
BELICHO                                                yes
THEON                                        long time ago
MAN                                       infantry advance
MISSANDEI     queen insists one must die punishment crim

In [189]:
for column in episode_nine.columns:
    for x in range(len(episode_nine[column])):
        episode_nine[column][x] = remove_stops(episode_nine[column][x])

In [190]:
episode_nine.index = episode_nine.index.str.title()

In [191]:
episode_nine.head()

0                      1   \
Yara                paid               westeros   
Davos          thats way  crucial let charge us   
Karstark  cavalry charge                   None   
Sansa                yes                   know   
Man #2          get back                   None   

                                          2   \
Yara                                  common   
Davos                              get sleep   
Karstark                                None   
Sansa     youve met enemy drawn battle plans   
Man #2                                  None   

                                                         3   \
Yara                        never demand im anything really   
Davos                        wasnt boltons defeated stannis   
Karstark                                               None   
Sansa     youve known space single conversation trusted ...   
Man #2                                                 None   

                                                         4                5   \
Yara      wed like help us murder uncle two dont think w...   thats way life   
Davos                                                        manner speaking   
Karstark                                               None             None   
Sansa                             think hes going fall trap     plays people   
Man #2                                                 None             None   

                                     6                    7              8   \
Yara                                                    None           None   
Davos     maybe mistake believing kings                  hes         thanks   
Karstark                           None                 None           None   
Sansa                         dont know  well never get back  listen please   
Man #2                             None                 None           None   

                 9                    10  \
Yara           None                 None   
Davos          walk       prepare charge   
Karstark       None                 None   
Sansa     dont know  think thats obvious   
Man #2         None                 None   

                                                         11             12  \
Yara                                                   None           None   
Davos                                                    go  well kill men   
Karstark                                               None           None   
Sansa     asked advice earlier would told attack winterf...         enough   
Man #2                                                 None           None   

                                       13           14    15    16  \
Yara                                 None         None  None  None   
Davos                              follow         lads  None  None   
Karstark                             None         None  None  None   
Sansa     ramsay wins im going back alive  one protect   jon         
Man #2                               None         None  None  None   

                       17                     18    19    20    21    22  \
Yara                 None                   None  None  None  None  None   
Davos                None                   None  None  None  None  None   
Karstark             None                   None  None  None  None  None   
Sansa     words disappear  havent fed seven days        None  None  None   
Man #2               None                   None  None  None  None  None   

            23    24    25    26    27  
Yara      None  None  None  None  None  
Davos     None  None  None  None  None  
Karstark  None  None  None  None  None  
Sansa     None  None  None  None  None  
Man #2    None  None  None  None  None

### Episode Ten

In [192]:
df_s6.script_text[9]

[u'\n',
 u'\n',
 u'CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - MARGAERY\u2019S CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: GREAT SEPT OF BAELOR - PRAYER ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - MARGAERY\u2019S CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: GREAT SEPT OF BAELOR',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: GREAT SEPT OF BAELOR - LORAS\u2019 CELL',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: GREAT SEPT OF BAELOR',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - TOMMEN\u2019s CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\nATTENDANT: Your Grace. The trial will be getting underway soon.',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - CERSEI\u2019S CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER',
 u'\n',
 u'\

In [193]:
script_text6_10 = df_s6.script_text[9]
print type(script_text6_10)

script_text6_10

<type 'list'>


[u'\n',
 u'\n',
 u'CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - MARGAERY\u2019S CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: GREAT SEPT OF BAELOR - PRAYER ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - MARGAERY\u2019S CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: GREAT SEPT OF BAELOR',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: GREAT SEPT OF BAELOR - LORAS\u2019 CELL',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: GREAT SEPT OF BAELOR',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - TOMMEN\u2019s CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\nATTENDANT: Your Grace. The trial will be getting underway soon.',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - CERSEI\u2019S CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER',
 u'\n',
 u'\

In [194]:
script_split10 = [i.split('\n') for i in script_text6_10]
script_split10

[[u'', u''],
 [u'', u''],
 [u'CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: RED KEEP - MARGAERY\u2019S CHAMBER'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: GREAT SEPT OF BAELOR - PRAYER ROOM'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: RED KEEP - MARGAERY\u2019S CHAMBER'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: GREAT SEPT OF BAELOR'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: GREAT SEPT OF BAELOR - LORAS\u2019 CELL'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: GREAT SEPT OF BAELOR'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: RED KEEP - TOMMEN\u2019s CHAMBER'],
 [u'', u''],
 [u'', u''],
 [u'', u'']

In [195]:
string_script_text10 = ' '

for i in script_split10:
    for e in i:
        string_script_text10 = string_script_text10 + ' ' + e

In [196]:
string_script_text10

u'      CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER         CUT TO: RED KEEP - MARGAERY\u2019S CHAMBER         CUT TO: GREAT SEPT OF BAELOR - PRAYER ROOM         CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER         CUT TO: RED KEEP - MARGAERY\u2019S CHAMBER         CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER         CUT TO: GREAT SEPT OF BAELOR         CUT TO: GREAT SEPT OF BAELOR - LORAS\u2019 CELL         CUT TO: GREAT SEPT OF BAELOR         CUT TO: RED KEEP - TOMMEN\u2019s CHAMBER        ATTENDANT: Your Grace. The trial will be getting underway soon.     CUT TO: RED KEEP - CERSEI\u2019S CHAMBER         CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER         CUT TO: RED KEEP - CERSEI\u2019S CHAMBER         CUT TO: RED KEEP - MAESTER PYCELLE\u2019S CHAMBER        MISTRESS: You got my money?    PYCELLE: Later. Go away.        GIRL: Grand Maester.         CUT TO: GREAT SEPT OF BAELOR        HIGH SPARROW: Ser Loras Tyrell. Are you prepared to stand trial and profess your guilt or innocence before the Sev

In [197]:
words10 = word_tokenize(string_script_text10)
words10

[u'CUT',
 u'TO',
 u':',
 u'RED',
 u'KEEP',
 u'-',
 u'TOMMEN\u2019S',
 u'CHAMBER',
 u'CUT',
 u'TO',
 u':',
 u'RED',
 u'KEEP',
 u'-',
 u'MARGAERY\u2019S',
 u'CHAMBER',
 u'CUT',
 u'TO',
 u':',
 u'GREAT',
 u'SEPT',
 u'OF',
 u'BAELOR',
 u'-',
 u'PRAYER',
 u'ROOM',
 u'CUT',
 u'TO',
 u':',
 u'RED',
 u'KEEP',
 u'-',
 u'TOMMEN\u2019S',
 u'CHAMBER',
 u'CUT',
 u'TO',
 u':',
 u'RED',
 u'KEEP',
 u'-',
 u'MARGAERY\u2019S',
 u'CHAMBER',
 u'CUT',
 u'TO',
 u':',
 u'RED',
 u'KEEP',
 u'-',
 u'TOMMEN\u2019S',
 u'CHAMBER',
 u'CUT',
 u'TO',
 u':',
 u'GREAT',
 u'SEPT',
 u'OF',
 u'BAELOR',
 u'CUT',
 u'TO',
 u':',
 u'GREAT',
 u'SEPT',
 u'OF',
 u'BAELOR',
 u'-',
 u'LORAS\u2019',
 u'CELL',
 u'CUT',
 u'TO',
 u':',
 u'GREAT',
 u'SEPT',
 u'OF',
 u'BAELOR',
 u'CUT',
 u'TO',
 u':',
 u'RED',
 u'KEEP',
 u'-',
 u'TOMMEN\u2019s',
 u'CHAMBER',
 u'ATTENDANT',
 u':',
 u'Your',
 u'Grace',
 u'.',
 u'The',
 u'trial',
 u'will',
 u'be',
 u'getting',
 u'underway',
 u'soon',
 u'.',
 u'CUT',
 u'TO',
 u':',
 u'RED',
 u'KEEP',
 u'-',

In [198]:
sentences10 = sent_tokenize(string_script_text10)
sentences10

[u'      CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER         CUT TO: RED KEEP - MARGAERY\u2019S CHAMBER         CUT TO: GREAT SEPT OF BAELOR - PRAYER ROOM         CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER         CUT TO: RED KEEP - MARGAERY\u2019S CHAMBER         CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER         CUT TO: GREAT SEPT OF BAELOR         CUT TO: GREAT SEPT OF BAELOR - LORAS\u2019 CELL         CUT TO: GREAT SEPT OF BAELOR         CUT TO: RED KEEP - TOMMEN\u2019s CHAMBER        ATTENDANT: Your Grace.',
 u'The trial will be getting underway soon.',
 u'CUT TO: RED KEEP - CERSEI\u2019S CHAMBER         CUT TO: RED KEEP - TOMMEN\u2019S CHAMBER         CUT TO: RED KEEP - CERSEI\u2019S CHAMBER         CUT TO: RED KEEP - MAESTER PYCELLE\u2019S CHAMBER        MISTRESS: You got my money?',
 u'PYCELLE: Later.',
 u'Go away.',
 u'GIRL: Grand Maester.',
 u'CUT TO: GREAT SEPT OF BAELOR        HIGH SPARROW: Ser Loras Tyrell.',
 u'Are you prepared to stand trial and profess your guilt or innocence 

In [199]:
dialogue10 = []

for sentence in sentences10:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names6_10):
            dialogue10.append(sentence)

In [200]:
dialogue10

[u'PYCELLE: Later.',
 u'GIRL: Grand Maester.',
 u'LORAS: There\u2019ll be no need for a trial.',
 u'HIGH SPARROW: To which crimes will you be confessing?',
 u'LORAS: All of them.',
 u'LORAS: I perjured myself before the gods.',
 u'HIGH SPARROW: The gods\u2019 judgment is fierce, but also fair.',
 u'LORAS: I take full responsibility for my many sins and unburden myself of my desires.',
 u'HIGH SPARROW: You understand fully what this means?',
 u'LORAS: I do.',
 u'HIGH SPARROW: Brother Loras\u2026        HIGH SPARROW: ...I ask you to dedicate your life to the seven gods.',
 u'HIGH SPARROW: Will you fight to defend your faith against heretics and apostates?',
 u'LORAS: I will.',
 u'MACE: No, I can\u2019t let them\u2026        MARGAERY: Faith is the way, Father.',
 u'TOMMEN: I have to go, I\u2019m-- I\u2019m late for the trial.',
 u'HIGH SPARROW: I\u2019ve kept my word.',
 u'MARGAERY: And where is the queen mother?',
 u'LANCEL: Her litter never left the Red Keep.',
 u'HIGH SPARROW: It appea

In [201]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s610.pkl', 'wb') as f:
    pickle.dump(dialogue10, f)

In [202]:
from collections import defaultdict

speakers10 = defaultdict(list)
for sentence in dialogue10:
    speakers10[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers10

defaultdict(list,
            {u'ALL': [u' The King in the North!', u' Long may she reign.'],
             u'BENJEN': [u' This is where I leave you.',
              u' The Wall is not just ice and stone.',
              u' The great war is coming and I still fight for the living.',
              u' I wish you both good fortune.'],
             u'BRAN': [u' Thank you, Uncle Benjen.',
              u'I\u2019m the Three-Eyed Raven now.'],
             u'BRONN': [u' You just sit there, a rich slab of beef, and all the birds come pecking.',
              u' She doesn\u2019t want me.',
              u' They have their eyes on you, cunt.',
              u' Not blonde enough?',
              u' Maybe I\u2019m not in the mood.',
              u' Fuck it.',
              u' No need to call me ser just because I\u2019m an anointed knight.'],
             u'CERSEI': [u' Confess.',
              u' Confess.',
              u' You\u2019ve always been quiet.',
              u' I said my face would be

In [203]:
speakers10['CERSEI']

[u' Confess.',
 u' Confess.',
 u' You\u2019ve always been quiet.',
 u' I said my face would be the last thing you saw before you died.',
 u' What?',
 u' This is Ser Gregor Clegane.',
 u' Your gods have forsaken you.',
 u' Shame.',
 u' Shame.',
 u' Shame.',
 u' He should be with his grandfather, his brother, his sister.']

In [204]:
episode_ten = pd.DataFrame.from_dict(speakers10, orient="index")
print episode_ten.shape

(42, 20)


In [205]:
#from numpy import nan
#episode_ten.fillna(value=str(0), inplace=True)

In [206]:
episode_ten.info()

<class 'pandas.core.frame.DataFrame'>
Index: 42 entries, DAVOS to PETYR
Data columns (total 20 columns):
0     42 non-null object
1     34 non-null object
2     26 non-null object
3     23 non-null object
4     19 non-null object
5     17 non-null object
6     15 non-null object
7     13 non-null object
8     11 non-null object
9     8 non-null object
10    7 non-null object
11    4 non-null object
12    3 non-null object
13    3 non-null object
14    3 non-null object
15    2 non-null object
16    1 non-null object
17    1 non-null object
18    1 non-null object
19    1 non-null object
dtypes: object(20)
memory usage: 6.9+ KB


In [207]:
episode_ten.head()

0   \
DAVOS                                 Tell him.   
SEPTA UNELLA                                No.   
PYCELLE                                  Later.   
NED                                     Lyanna.   
MELISANDRE     Could have been worse, Jon Snow.   

                                          1                             2   \
DAVOS          Tell him what you did to her.                          Why?   
SEPTA UNELLA                           Good.                           No.   
PYCELLE          What’s the meaning of this?                          None   
NED                     No, I’m not a dream.         I’ve missed you, too.   
MELISANDRE             The Princess Shireen.   We burned her at the stake.   

                                            3   \
DAVOS          You burned a little girl alive!   
SEPTA UNELLA                              None   
PYCELLE                                   None   
NED                                       Shh.   
MELISANDRE               The army was trapped.   

                                                             4   \
DAVOS          If he commands you to burn children, your Lor...   
SEPTA UNELLA                                               None   
PYCELLE                                                    None   
NED                                    You’re not going to die.   
MELISANDRE                     I only do what my Lord commands!   

                                                   5   \
DAVOS          I loved that girl like she was my own.   
SEPTA UNELLA                                     None   
PYCELLE                                          None   
NED                               Get her some water!   
MELISANDRE       We are standing here because of him.   

                                   6                      7   \
DAVOS          The only way for what?   Aye, you were wrong.   
SEPTA UNELLA                     None                   None   
PYCELLE                          None                   None   
NED               Is there a maester?                   None   
MELISANDRE         So did her father.          I didn’t lie.   

                                                             8     9     10  \
DAVOS          If you ever come back this way, I will execut...  None  None   
SEPTA UNELLA                                               None  None  None   
PYCELLE                                                    None  None  None   
NED                                                        None  None  None   
MELISANDRE               I’ve been ready to die for many years.  None  None   

                11    12    13    14    15    16    17    18    19  
DAVOS         None  None  None  None  None  None  None  None  None  
SEPTA UNELLA  None  None  None  None  None  None  None  None  None  
PYCELLE       None  None  None  None  None  None  None  None  None  
NED           None  None  None  None  None  None  None  None  None  
MELISANDRE    None  None  None  None  None  None  None  None  None

In [208]:
test10 = episode_ten[0].apply(remove_stops)
test10

DAVOS                                                      tell
SEPTA UNELLA                                                   
PYCELLE                                                   later
NED                                                      lyanna
MELISANDRE                                 could worse jon snow
BRONN                     sit rich slab beef birds come pecking
JAIME                                             youre welcome
TYRION                                                know hard
GIRL                                              grand maester
MAESTER                                                      oh
ELLARIA                             nothing fear us lady olenna
SAM                            lord commander snow castle black
OLENNA                 last time tyrell came dorne assassinated
MEERA                                           youre coming us
DAENERYS                                        youre coming us
BENJEN                                  

In [209]:
for column in episode_ten.columns:
    for x in range(len(episode_ten[column])):
        episode_ten[column][x] = remove_stops(episode_ten[column][x])

In [210]:
episode_ten.index = episode_ten.index.str.title()

In [211]:
episode_ten.head()

0                 1             2   \
Davos                         tell              tell                 
Septa Unella                                    good                 
Pycelle                      later     whats meaning          None   
Ned                         lyanna          im dream    ive missed   
Melisandre    could worse jon snow  princess shireen  burned stake   

                                    3                                 4   \
Davos         burned little girl alive  commands burn children lord evil   
Septa Unella                      None                              None   
Pycelle                           None                              None   
Ned                                shh                   youre going die   
Melisandre                army trapped                     lord commands   

                           5        6          7                           8   \
Davos         loved girl like      way  aye wrong  ever come back way execute   
Septa Unella             None     None       None                        None   
Pycelle                  None     None       None                        None   
Ned                 get water  maester       None                        None   
Melisandre           standing   father  didnt lie    ive ready die many years   

                9     10    11    12    13    14    15    16    17    18    19  
Davos         None  None  None  None  None  None  None  None  None  None  None  
Septa Unella  None  None  None  None  None  None  None  None  None  None  None  
Pycelle       None  None  None  None  None  None  None  None  None  None  None  
Ned           None  None  None  None  None  None  None  None  None  None  None  
Melisandre    None  None  None  None  None  None  None  None  None  None  None

## Season Six

In [212]:
episode_one.index

Index([u'Davos', u'Male Voice #2', u'Jaime', u'Tyrion', u'Wife #1',
       u'Dolorous Edd', u'Red Priest', u'Maester Wolkan', u'Daenerys',
       u'Doran', u'Roose', u'Maester', u'Theon', u'Cersei', u'Varys',
       u'Trystane', u'Margaery', u'Ramsay', u'Nymeria', u'Obara',
       u'Alliser Thorne', u'Jorah', u'High Sparrow', u'Bloodrider #2'],
      dtype='object')

In [213]:
episode_two.index

Index([u'Young Benjen', u'Theon', u'Jaime', u'Roose', u'Tommen', u'Sansa',
       u'Nan', u'Waif', u'Bran', u'Hodor', u'Melisandre', u'Hooded Figure',
       u'Tyrion', u'High Sparrow', u'Balon', u'Arya', u'Missandei',
       u'Alliser Thorne', u'Ramsay'],
      dtype='object')

In [214]:
print episode_one.shape
print episode_two.shape

(24, 6)
(19, 4)


In [215]:
season_six = episode_one.join(episode_two, rsuffix="_two", how='outer')
print season_six.shape

(36, 10)


In [216]:
season_six.index

Index([u'Alliser Thorne', u'Arya', u'Balon', u'Bloodrider #2', u'Bran',
       u'Cersei', u'Daenerys', u'Davos', u'Dolorous Edd', u'Doran',
       u'High Sparrow', u'Hodor', u'Hooded Figure', u'Jaime', u'Jorah',
       u'Maester', u'Maester Wolkan', u'Male Voice #2', u'Margaery',
       u'Melisandre', u'Missandei', u'Nan', u'Nymeria', u'Obara', u'Ramsay',
       u'Red Priest', u'Roose', u'Sansa', u'Theon', u'Tommen', u'Trystane',
       u'Tyrion', u'Varys', u'Waif', u'Wife #1', u'Young Benjen'],
      dtype='object')

In [217]:
episode_three.index

Index([u'Davos', u'Melisandre', u'Smalljon', u'Gilly', u'Jaime',
       u'Three-Eyed Raven', u'Tyrion', u'Missandei', u'Dolorous Edd',
       u'Samwell', u'Arthur', u'Grey Worm', u'Cersei', u'Varys', u'Qyburn',
       u'Jon Snow', u'Ramsay', u'Little Bird', u'Bran', u'High Sparrow',
       u'Arya', u'Maester Pycelle'],
      dtype='object')

In [218]:
episode_three.shape

(22, 4)

In [219]:
season_six = season_six.join(episode_three, rsuffix="_three", how='outer')
print season_six.shape

(46, 14)


In [220]:
season_six.index

Index([u'Alliser Thorne', u'Arthur', u'Arya', u'Balon', u'Bloodrider #2',
       u'Bran', u'Cersei', u'Daenerys', u'Davos', u'Dolorous Edd', u'Doran',
       u'Gilly', u'Grey Worm', u'High Sparrow', u'Hodor', u'Hooded Figure',
       u'Jaime', u'Jon Snow', u'Jorah', u'Little Bird', u'Maester',
       u'Maester Pycelle', u'Maester Wolkan', u'Male Voice #2', u'Margaery',
       u'Melisandre', u'Missandei', u'Nan', u'Nymeria', u'Obara', u'Qyburn',
       u'Ramsay', u'Red Priest', u'Roose', u'Samwell', u'Sansa', u'Smalljon',
       u'Theon', u'Three-Eyed Raven', u'Tommen', u'Trystane', u'Tyrion',
       u'Varys', u'Waif', u'Wife #1', u'Young Benjen'],
      dtype='object')

In [221]:
episode_four.index

Index([u'Kevan', u'Melisandre', u'Jaime', u'Tyrion', u'Littlefinger', u'Robin',
       u'Yara', u'Maester Pycelle', u'Yohn Royce', u'Khal #3', u'Daenerys',
       u'Lady Olenna', u'Theon', u'Tommen', u'Cersei', u'Osha', u'Margaery',
       u'Jon Snow', u'Ramsay', u'Khal #4', u'Lhazareen Woman', u'Khal #1',
       u'Khal #2', u'Sansa', u'Brienne', u'Khal Moro', u'Jorah',
       u'Dothraki #1', u'Daario', u'Tormund', u'High Sparrow', u'Loras',
       u'Man'],
      dtype='object')

In [222]:
episode_four.shape

(33, 13)

In [223]:
season_six = season_six.join(episode_four, rsuffix="_four", how='outer')
print season_six.shape

(65, 27)


In [224]:
season_six.index

Index([u'Alliser Thorne', u'Arthur', u'Arya', u'Balon', u'Bloodrider #2',
       u'Bran', u'Brienne', u'Cersei', u'Daario', u'Daenerys', u'Davos',
       u'Dolorous Edd', u'Doran', u'Dothraki #1', u'Gilly', u'Grey Worm',
       u'High Sparrow', u'Hodor', u'Hooded Figure', u'Jaime', u'Jon Snow',
       u'Jorah', u'Kevan', u'Khal #1', u'Khal #2', u'Khal #3', u'Khal #4',
       u'Khal Moro', u'Lady Olenna', u'Lhazareen Woman', u'Little Bird',
       u'Littlefinger', u'Loras', u'Maester', u'Maester Pycelle',
       u'Maester Wolkan', u'Male Voice #2', u'Man', u'Margaery', u'Melisandre',
       u'Missandei', u'Nan', u'Nymeria', u'Obara', u'Osha', u'Qyburn',
       u'Ramsay', u'Red Priest', u'Robin', u'Roose', u'Samwell', u'Sansa',
       u'Smalljon', u'Theon', u'Three-Eyed Raven', u'Tommen', u'Tormund',
       u'Trystane', u'Tyrion', u'Varys', u'Waif', u'Wife #1', u'Yara',
       u'Yohn Royce', u'Young Benjen'],
      dtype='object')

In [225]:
episode_five.index

Index([u'Davos', u'Kinvara', u'Nan', u'Three-Eyed Raven', u'Tyrion', u'Euron',
       u'Littlefinger', u'Missandei', u'Dolorous Edd', u'Yara', u'Young Hodor',
       u'Aerson', u'Theon', u'Lady Crane', u'Rickard', u'Hodor', u'Meera',
       u'Daenerys', u'Clarenzo', u'Ladyc Rane', u'Grey Worm', u'Waif',
       u'Varys', u'Bobono', u'Bianca', u'Izembaro', u'Jon Snow', u'All',
       u'Leaf', u'Aeron', u'Sansa', u'Brienne', u'Man #2', u'Man #1', u'Jorah',
       u'Jaqen', u'Camello', u'Young Ned', u'Arya', u'Bran', u'Man'],
      dtype='object')

In [226]:
episode_five = episode_five.reset_index()

In [227]:
episode_five_dict = {'Davos':'Davos', 
                     'Kinvara':'Kinvara', 
                     'Nan':'Nan', 
                     'Three-Eyed Raven':'Three-Eyed Raven', 
                     'Tyrion':'Tyrion', 
                     'Euron':'Euron',
                     'Littlefinger':'Littlefinger', 
                     'Missandei':'Missandei', 
                     'Dolorous Edd':'Dolorous Edd', 
                     'Yara':'Yara', 
                     'Young Hodor':'Young Hodor',
                     'Aerson':'Aeron', 
                     'Theon':'Theon', 
                     'Lady Crane':'Lady Crane', 
                     'Rickard':'Rickard', 
                     'Hodor':'Hodor', 
                     'Meera':'Meera',
                     'Daenerys':'Daenerys', 
                     'Clarenzo':'Clarenzo', 
                     'Ladyc Rane':'Lady Crane', 
                     'Grey Worm':'Grey Worm', 
                     'Waif':'Waif',
                     'Varys':'Varys', 
                     'Bobono':'Bobono', 
                     'Bianca':'Bianca', 
                     'Izembaro':'Izembaro', 
                     'Jon Snow':'Jon Snow', 
                     'All':'All',
                     'Leaf':'Leaf', 
                     'Aeron':'Aeron', 
                     'Sansa':'Sansa', 
                     'Brienne':'Brienne', 
                     'Man #2':'Man #2', 
                     'Man #1':'Man #1', 
                     'Jorah':'Jorah',
                     'Jaqen':'Jaqen', 
                     'Camello':'Camello', 
                     'Young Ned':'Young Ned', 
                     'Arya':'Arya', 
                     'Bran':'Bran', 
                     'Man':'Man'}

episode_five['index'] = episode_five['index'].replace(episode_five_dict)

In [228]:
episode_five = episode_five.set_index('index')

In [229]:
episode_five.shape

(41, 30)

In [230]:
season_six = season_six.join(episode_five, rsuffix="_five", how='outer')
print season_six.shape    

(85, 57)


In [231]:
season_six.index

Index([           u'Aeron',            u'Aeron',              u'All',
         u'Alliser Thorne',           u'Arthur',             u'Arya',
                  u'Balon',           u'Bianca',    u'Bloodrider #2',
                 u'Bobono',             u'Bran',          u'Brienne',
                u'Camello',           u'Cersei',         u'Clarenzo',
                 u'Daario',         u'Daenerys',            u'Davos',
           u'Dolorous Edd',            u'Doran',      u'Dothraki #1',
                  u'Euron',            u'Gilly',        u'Grey Worm',
           u'High Sparrow',            u'Hodor',    u'Hooded Figure',
               u'Izembaro',            u'Jaime',            u'Jaqen',
               u'Jon Snow',            u'Jorah',            u'Kevan',
                u'Khal #1',          u'Khal #2',          u'Khal #3',
                u'Khal #4',        u'Khal Moro',          u'Kinvara',
             u'Lady Crane',       u'Lady Crane',      u'Lady Olenna',
                   u

In [232]:
episode_six.index

Index([u'Dickon', u'Gilly', u'Jaime', u'Woman', u'Sam', u'Olenna',
       u'Lady Crane', u'Talla', u'Meera', u'Lothar', u'Daenerys', u'Benjen',
       u'Cersei', u'Clarenzo', u'Tommen', u'Waif', u'Bobono', u'Bianca',
       u'Mace', u'Izembaro', u'Melessa', u'Margaery', u'Walder', u'Rider',
       u'Randyll', u'All', u'Captain', u'Jaqen', u'Daario', u'Camello',
       u'High Sparrow', u'Black Walder', u'Arya', u'Bran'],
      dtype='object')

In [233]:
episode_six.shape

(34, 32)

In [234]:
season_six = season_six.join(episode_six, rsuffix="_six", how='outer')
print season_six.shape    

(99, 89)


In [235]:
season_six.index

Index([           u'Aeron',            u'Aeron',              u'All',
         u'Alliser Thorne',           u'Arthur',             u'Arya',
                  u'Balon',           u'Benjen',           u'Bianca',
           u'Black Walder',    u'Bloodrider #2',           u'Bobono',
                   u'Bran',          u'Brienne',          u'Camello',
                u'Captain',           u'Cersei',         u'Clarenzo',
                 u'Daario',         u'Daenerys',            u'Davos',
                 u'Dickon',     u'Dolorous Edd',            u'Doran',
            u'Dothraki #1',            u'Euron',            u'Gilly',
              u'Grey Worm',     u'High Sparrow',            u'Hodor',
          u'Hooded Figure',         u'Izembaro',            u'Jaime',
                  u'Jaqen',         u'Jon Snow',            u'Jorah',
                  u'Kevan',          u'Khal #1',          u'Khal #2',
                u'Khal #3',          u'Khal #4',        u'Khal Moro',
                u'Ki

In [236]:
episode_seven.index

Index([u'Davos', u'Bronn', u'Jaime', u'Brynden', u'Yara', u'Woman', u'Olenna',
       u'Lothar', u'Ray', u'Theon', u'Cersei', u'Dim Dalba', u'Sandor',
       u'Robett', u'Lyanna', u'Margaery', u'Jon Snow', u'Sansa', u'Man #2',
       u'Lem', u'Wun Wun', u'Tormund', u'High Sparrow', u'Black Walder',
       u'Arya', u'Man'],
      dtype='object')

In [237]:
episode_seven.shape

(26, 31)

In [238]:
season_six = season_six.join(episode_seven, rsuffix="_seven", how='outer')
print season_six.shape

(108, 120)


In [239]:
episode_eight.index

Index([u'Kevan', u'Bronn', u'Jaime', u'Tyrion', u'Missandei', u'Crowd',
       u'Lady Crane', u'Guard', u'Guard Captain', u'Thoros', u'Gatins',
       u'Tommen', u'Grey Worm', u'Young Man', u'Varys', u'Cersei', u'Sandor',
       u'Beric', u'Brynden', u'Qyburn', u'Edmure', u'Podrick', u'Lancel',
       u'Brienne', u'Lem', u'Jaqen', u'Waif', u'Arya', u'Man'],
      dtype='object')

In [240]:
episode_eight.shape

(29, 36)

In [241]:
season_six = season_six.join(episode_eight, rsuffix="_eight", how='outer')
print season_six.shape

(118, 156)


In [242]:
episode_nine.index

Index([u'Yara', u'Davos', u'Karstark', u'Sansa', u'Man #2', u'Tyrion',
       u'Melisandre', u'All', u'Smalljon', u'Tormund', u'Razdal', u'Yezzan',
       u'Daenerys', u'Belicho', u'Theon', u'Man', u'Missandei', u'Jon Snow',
       u'Ramsay'],
      dtype='object')

In [243]:
episode_nine.shape

(19, 28)

In [244]:
season_six = season_six.join(episode_nine, rsuffix="_nine", how='outer')
print season_six.shape

(122, 184)


In [245]:
episode_ten.index

Index([u'Davos', u'Septa Unella', u'Pycelle', u'Ned', u'Melisandre', u'Bronn',
       u'Jaime', u'Tyrion', u'Girl', u'Maester', u'Ellaria', u'Sam', u'Olenna',
       u'Meera', u'Daenerys', u'Benjen', u'Vale Knight', u'Tommen', u'Cersei',
       u'Varys', u'Walder', u'Handmaiden', u'Mace', u'Lyanna', u'Margaery',
       u'Qyburn', u'Jon Snow', u'Nymeria', u'All', u'Lancel', u'Obara',
       u'Sansa', u'Men', u'Manderly', u'Daario', u'Tormund', u'Glover',
       u'High Sparrow', u'Man', u'Bran', u'Loras', u'Petyr'],
      dtype='object')

In [246]:
episode_ten.shape

(42, 20)

In [247]:
season_six = season_six.join(episode_ten, rsuffix="_ten", how='outer')
print season_six.shape

(133, 204)


In [248]:
season_six.index

Index([         u'Aeron',          u'Aeron',            u'All',
       u'Alliser Thorne',         u'Arthur',           u'Arya',
                u'Balon',        u'Belicho',         u'Benjen',
                u'Beric',
       ...
              u'Wife #1',          u'Woman',        u'Wun Wun',
                 u'Yara',         u'Yezzan',     u'Yohn Royce',
         u'Young Benjen',    u'Young Hodor',      u'Young Man',
            u'Young Ned'],
      dtype='object', length=133)

In [249]:
from numpy import nan
season_six.fillna(value=str(0), inplace=True)

In [250]:
season_six.head(135)

0  \
Aeron                                                             0   
Aeron                                                             0   
All                                                               0   
Alliser Thorne             know youre jon snow dead nights watchman   
Arthur                                                            0   
Arya                                                              0   
Balon                                                             0   
Belicho                                                           0   
Benjen                                                            0   
Beric                                                             0   
Bianca                                                            0   
Black Walder                                                      0   
Bloodrider #2                   fucking grandma bloodrider daenerys   
Bobono                                                            0   
Bran                                                              0   
Brienne                                                           0   
Bronn                                                             0   
Brynden                                                           0   
Camello                                                           0   
Captain                                                           0   
Cersei                          think locking myrcella crypt cersei   
Clarenzo                                                          0   
Crowd                                                             0   
Daario                                                            0   
Daenerys          lie bear children anyone else sun rises west s...   
Davos                                           help get inside cut   
Dickon                                                            0   
Dim Dalba                                                         0   
Dolorous Edd                                                  trust   
Doran             always envied oberyn lived truly lived sailed ...   
Dothraki #1                                                       0   
Edmure                                                            0   
Ellaria                                                           0   
Euron                                                             0   
Gatins                                                            0   
Gilly                                                             0   
Girl                                                              0   
Glover                                                            0   
Grey Worm                                                         0   
Guard                                                             0   
Guard Captain                                                     0   
Handmaiden                                                        0   
High Sparrow      isnt ser loras brings husband misses dearly lo...   
Hodor                                                             0   
Hooded Figure                                                     0   
Izembaro                                                          0   
Jaime                                                 mother cersei   
Jaqen                                                             0   
Jon Snow                                                          0   
Jorah                                                    ram daario   
Karstark                                                          0   
Kevan                                                             0   
Khal #1                                                           0   
Khal #2                                                           0   
Khal #3                                                           0   
Khal #4                                                           0   
Khal Moro          

In [251]:
season_six.info()

<class 'pandas.core.frame.DataFrame'>
Index: 133 entries, Aeron to Young Ned
Columns: 204 entries, 0 to 19_ten
dtypes: object(204)
memory usage: 213.0+ KB


In [252]:
season_six.to_pickle('/Users/zoemarkovits/Metis/project_five_got/PKLs/season_six.pkl')

## Character Breakdown

### Arya Stark

In [253]:
Arya = season_six.loc['Arya']
print Arya

0                                             0
1                                             0
2                                             0
3                                             0
4                                             0
5                                             0
0_two                                  one waif
1_two                                 one jaqen
2_two                                         0
3_two                                         0
0                                       one ext
1                                             0
2                                             0
3                                             0
0_four                                        0
1_four                                        0
2_four                                        0
3_four                                        0
4_four                                        0
5_four                                        0
6                                       

In [254]:
Arya_Text = Arya.values.tolist()
Arya_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'one waif',
 u'one jaqen',
 '0',
 '0',
 u'one ext',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'first',
 u'go',
 u'girl desires',
 '',
 u'girl could use one faces hall jaqen',
 u'shes good actress',
 u'seems like decent woman',
 '',
 u'younger actress',
 u'girl decided',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'nothing',
 u'three times',
 '',
 u'youre good',
 u'change',
 u'queen loves son anything',
 u'mercy',
 u'go',
 u'careful one',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'youre westerosi',
 u'want book passage home',
 u'care',
 u'want cabin',
 u'see sunrise',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',


In [255]:
Arya_Words = []

for word in Arya_Text:
    if len(word)>=1:
        if word != '0':
            Arya_Words.append(word)
        
Arya_Words 

[u'one waif',
 u'one jaqen',
 u'one ext',
 u'first',
 u'go',
 u'girl desires',
 u'girl could use one faces hall jaqen',
 u'shes good actress',
 u'seems like decent woman',
 u'younger actress',
 u'girl decided',
 u'nothing',
 u'three times',
 u'youre good',
 u'change',
 u'queen loves son anything',
 u'mercy',
 u'go',
 u'careful one',
 u'youre westerosi',
 u'want book passage home',
 u'care',
 u'want cabin',
 u'see sunrise',
 u'good putting holes',
 u'happened actress',
 u'mmm',
 u'cant',
 u'dont think could remember lines',
 u'wouldnt safe',
 u'doesnt name',
 u'whats',
 u'dont want',
 u'lady crane',
 u'lady crane',
 u'girl arya stark winterfell im going home']

In [256]:
Arya_Words_String = ' '.join(Arya_Words)
Arya_Words_String

u'one waif one jaqen one ext first go girl desires girl could use one faces hall jaqen shes good actress seems like decent woman younger actress girl decided nothing three times youre good change queen loves son anything mercy go careful one youre westerosi want book passage home care want cabin see sunrise good putting holes happened actress mmm cant dont think could remember lines wouldnt safe doesnt name whats dont want lady crane lady crane girl arya stark winterfell im going home'

In [257]:
Arya_String_Length = len(Arya_Words_String)
Arya_String_Length

487

In [258]:
Arya_Sentiment = TextBlob(Arya_Words_String).sentiment
Arya_Sentiment

Sentiment(polarity=0.3018518518518518, subjectivity=0.5444444444444445)

### Brienne of Tarth

In [259]:
Brienne = season_six.loc['Brienne']
print Brienne

0                                                           0
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
0_two                                                       0
1_two                                                       0
2_two                                                       0
3_two                                                       0
0                                                           0
1                                                           0
2                                                           0
3                                                           0
0_four      saw happened saw stannis forces defeated field...
1_four                    stannis executed littlefinger robin
2_four  

In [260]:
Brienne_Text = Brienne.values.tolist()
Brienne_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'saw happened saw stannis forces defeated field davos',
 u'stannis executed littlefinger robin',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'lady sansa asked question',
 u'send blackfish raven',
 u'dont like leaving alone',
 '',
 u'lie asked learned riverrun',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'keen military mind pod',
 u'name brienne tarth',
 u'would assume',
 u'dont think know many girls 

In [261]:
Brienne_Words = []

for word in Brienne_Text:
    if len(word)>=1:
        if word != '0':
            Brienne_Words.append(word)
        
Brienne_Words 

[u'saw happened saw stannis forces defeated field davos',
 u'stannis executed littlefinger robin',
 u'lady sansa asked question',
 u'send blackfish raven',
 u'dont like leaving alone',
 u'lie asked learned riverrun',
 u'keen military mind pod',
 u'name brienne tarth',
 u'would assume',
 u'dont think know many girls like',
 u'ive come blackfish',
 u'lady sansa desires take ancestral seat back boltons assume rightful position lady winterfell',
 u'tully army',
 u'tullys rebels theyre fighting home',
 u'reward betraying robb stark slaughtering family',
 u'youre knight ser jaime',
 u'thing',
 u'allow enter riverrun flag truce',
 u'youll allow lead tully forces safely north',
 u'need word',
 u'gave purpose',
 u'one last thing ser jaime',
 u'fail persuade blackfish surrender attack castle honor compels fight sansas kin',
 u'fight',
 u'signed letter niece sansa stark',
 u'said name brynden',
 u'always spoke highly',
 u'riverrun cannot stand lannisters freys',
 u'hes friend',
 u'ser jaime kept 

In [262]:
Brienne_Words_String = ' '.join(Brienne_Words)
Brienne_Words_String

u'saw happened saw stannis forces defeated field davos stannis executed littlefinger robin lady sansa asked question send blackfish raven dont like leaving alone lie asked learned riverrun keen military mind pod name brienne tarth would assume dont think know many girls like ive come blackfish lady sansa desires take ancestral seat back boltons assume rightful position lady winterfell tully army tullys rebels theyre fighting home reward betraying robb stark slaughtering family youre knight ser jaime thing allow enter riverrun flag truce youll allow lead tully forces safely north need word gave purpose one last thing ser jaime fail persuade blackfish surrender attack castle honor compels fight sansas kin fight signed letter niece sansa stark said name brynden always spoke highly riverrun cannot stand lannisters freys hes friend ser jaime kept word niece catelyn stark tell failed come us family north'

In [263]:
Brienne_String_Length = len(Brienne_Words_String)
Brienne_String_Length

909

In [264]:
Brienne_Sentiment = TextBlob(Brienne_Words_String).sentiment
Brienne_Sentiment

Sentiment(polarity=-0.049090909090909095, subjectivity=0.3733333333333333)

### Cersei Lannister

In [265]:
Cersei = season_six.loc['Cersei']
print Cersei

0                         think locking myrcella crypt cersei
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
0_two                                                       0
1_two                                                       0
2_two                                                       0
3_two                                                       0
0                                                   yet jaime
1                                                           0
2                                                           0
3                                                           0
0_four                                                       
1_four      since ive missed past several small coucil mee...
2_four  

In [266]:
Cersei_Text = Cersei.values.tolist()
Cersei_Text

[u'think locking myrcella crypt cersei',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'yet jaime',
 '0',
 '0',
 '0',
 '',
 u'since ive missed past several small coucil meetings wanted speak things',
 u'unfortunately',
 u'look',
 u'right',
 u'whether like completely unimportant',
 u'youve spoken',
 u'spoke respect father understood necessity working ones rivals',
 u'high sparrow seized power knowing full well wed bicker amongst instead seizing back',
 u'hate fanatics much',
 u'stand aside let people took destroyed',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'better youre elsewhere head army sept dungeons',
 '',
 u'cant',
 u'treat without mercy',
 u'trial combat',
 u'idea strong',
 u'weve always together',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0

In [267]:
Cersei_Words = []

for word in Cersei_Text:
    if len(word)>=1:
        if word != '0':
            Cersei_Words.append(word)
        
Cersei_Words 

[u'think locking myrcella crypt cersei',
 u'yet jaime',
 u'since ive missed past several small coucil meetings wanted speak things',
 u'unfortunately',
 u'look',
 u'right',
 u'whether like completely unimportant',
 u'youve spoken',
 u'spoke respect father understood necessity working ones rivals',
 u'high sparrow seized power knowing full well wed bicker amongst instead seizing back',
 u'hate fanatics much',
 u'stand aside let people took destroyed',
 u'better youre elsewhere head army sept dungeons',
 u'cant',
 u'treat without mercy',
 u'trial combat',
 u'idea strong',
 u'weve always together',
 u'heard leaving kings landing',
 u'grandson still prisoner',
 u'youre right',
 u'delivered army fanatics onto doorstep',
 u'love granddaughter',
 u'never',
 u'permitted',
 u'permitted inside red keep',
 u'king aware presence',
 u'holiness high septon welcome see red keep',
 u'request cousin lancel',
 u'promised could stay red keep trial',
 u'choose violence',
 u'please tell high holiness hes a

In [268]:
Cersei_Words_String = ' '.join(Cersei_Words)
Cersei_Words_String

u'think locking myrcella crypt cersei yet jaime since ive missed past several small coucil meetings wanted speak things unfortunately look right whether like completely unimportant youve spoken spoke respect father understood necessity working ones rivals high sparrow seized power knowing full well wed bicker amongst instead seizing back hate fanatics much stand aside let people took destroyed better youre elsewhere head army sept dungeons cant treat without mercy trial combat idea strong weve always together heard leaving kings landing grandson still prisoner youre right delivered army fanatics onto doorstep love granddaughter never permitted permitted inside red keep king aware presence holiness high septon welcome see red keep request cousin lancel promised could stay red keep trial choose violence please tell high holiness hes always welcome visit theres royal announcement wasnt informed stand son confess confess youve always quiet said face would last thing saw died ser gregor cle

In [269]:
Cersei_String_Length = len(Cersei_Words_String)
Cersei_String_Length

1061

In [270]:
Cersei_Sentiment = TextBlob(Cersei_Words_String).sentiment
Cersei_Sentiment

Sentiment(polarity=0.10739047619047618, subjectivity=0.44899047619047616)

### Daenerys Targaryen

In [271]:
Daenerys = season_six.loc['Daenerys']
print Daenerys

0           lie bear children anyone else sun rises west s...
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
0_two                                                       0
1_two                                                       0
2_two                                                       0
3_two                                                       0
0                                                           0
1                                                           0
2                                                           0
3                                                           0
0_four                                  mmhmm lhazareen woman
1_four                                 would like see one day
2_four  

In [272]:
Dany_Text = Daenerys.values.tolist()
Dany_Text

[u'lie bear children anyone else sun rises west sets east',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'mmhmm lhazareen woman',
 u'would like see one day',
 u'dont want know think',
 '',
 u'know',
 u'drogo promised take khalasar west world ends',
 u'great matters great khals discuss',
 u'youre going serve',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'cure',
 u'long take',
 u'im sorry',
 u'walk away queen jorah andal',
 u'dismissed',
 u'well command find cure wherever world',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'many days ride meereen',
 u'many ships need bring khalasar westeros',
 u'many',
 u'nobody yet',
 u'take mine',
 u'made',
 u'wait',
 u'kill enemies iron suits tear stone houses',
 u'give seven kingdoms gift khal drogo promised mother mountains',
 '',
 u'always',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 

In [273]:
Dany_Words = []

for word in Dany_Text:
    if len(word)>=1:
        if word != '0':
            Dany_Words.append(word)
        
Dany_Words 

[u'lie bear children anyone else sun rises west sets east',
 u'mmhmm lhazareen woman',
 u'would like see one day',
 u'dont want know think',
 u'know',
 u'drogo promised take khalasar west world ends',
 u'great matters great khals discuss',
 u'youre going serve',
 u'cure',
 u'long take',
 u'im sorry',
 u'walk away queen jorah andal',
 u'dismissed',
 u'well command find cure wherever world',
 u'many days ride meereen',
 u'many ships need bring khalasar westeros',
 u'many',
 u'nobody yet',
 u'take mine',
 u'made',
 u'wait',
 u'kill enemies iron suits tear stone houses',
 u'give seven kingdoms gift khal drogo promised mother mountains',
 u'always',
 u'city rise',
 u'good',
 u'dont approve',
 u'entirely different',
 u'obviously didnt communicate clearly',
 u'reign begun',
 u'youve brought us ships iron fleet men sail',
 u'whats wrong',
 u'iron islands ever queen',
 u'lord tyrion tells father terrible king',
 u'ships enough',
 u'shouldnt wait',
 u'imagine offer free marriage demands',
 u'don

In [274]:
Dany_Words_String = ' '.join(Dany_Words)
Dany_Words_String

u'lie bear children anyone else sun rises west sets east mmhmm lhazareen woman would like see one day dont want know think know drogo promised take khalasar west world ends great matters great khals discuss youre going serve cure long take im sorry walk away queen jorah andal dismissed well command find cure wherever world many days ride meereen many ships need bring khalasar westeros many nobody yet take mine made wait kill enemies iron suits tear stone houses give seven kingdoms gift khal drogo promised mother mountains always city rise good dont approve entirely different obviously didnt communicate clearly reign begun youve brought us ships iron fleet men sail whats wrong iron islands ever queen lord tyrion tells father terrible king ships enough shouldnt wait imagine offer free marriage demands dont want seven kingdoms thats reasonable shes demanding shes asking support claim queen seven kingdoms respect integrity seven kingdoms youre coming us youre going westeros promised dont k

In [275]:
Dany_String_Length = len(Dany_Words_String)
Dany_String_Length

1272

In [276]:
Dany_Sentiment = TextBlob(Dany_Words_String).sentiment
Dany_Sentiment

Sentiment(polarity=0.15000000000000002, subjectivity=0.6253968253968254)

### Davos

In [277]:
Davos = season_six.loc['Davos']
print Davos

0                                         help get inside cut
1                                 need help get melisandre os
2                  youre ones owe lives jon snow dolorous edd
3           im much hunter ill need food im gonna make sou...
4                                    havent seen ive seen cut
5                                                           0
0_two                                                       0
1_two                                                       0
2_two                                                       0
3_two                                                       0
0           dead youre thats completely fucking mad seems ...
1                      dont know maybe well never know matter
2                                                           0
3                                                           0
0_four                                                      0
1_four                                                      0
2_four  

In [278]:
Davos_Text = Davos.values.tolist()
Davos_Text

[u'help get inside cut',
 u'need help get melisandre os',
 u'youre ones owe lives jon snow dolorous edd',
 u'im much hunter ill need food im gonna make south without starving alliser thorne',
 u'havent seen ive seen cut',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'dead youre thats completely fucking mad seems imagine seems jon snow',
 u'dont know maybe well never know matter',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'aside starks boltons powerful houses north umbers karstarks manderlys',
 u'umbers karstarks already declared boltons well',
 u'beg pardon lady know stark beheaded father',
 u'precious little lady',
 u'may well loyal many rose boltons betrayed family',
 u'dont doubt',
 u'didnt know tullys still army',
 u'thats good',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0

In [279]:
Davos_Words = []

for word in Davos_Text:
    if len(word)>=1:
        if word != '0':
            Davos_Words.append(word)
        
Davos_Words 

[u'help get inside cut',
 u'need help get melisandre os',
 u'youre ones owe lives jon snow dolorous edd',
 u'im much hunter ill need food im gonna make south without starving alliser thorne',
 u'havent seen ive seen cut',
 u'dead youre thats completely fucking mad seems imagine seems jon snow',
 u'dont know maybe well never know matter',
 u'aside starks boltons powerful houses north umbers karstarks manderlys',
 u'umbers karstarks already declared boltons well',
 u'beg pardon lady know stark beheaded father',
 u'precious little lady',
 u'may well loyal many rose boltons betrayed family',
 u'dont doubt',
 u'didnt know tullys still army',
 u'thats good',
 u'please lady understand feel',
 u'davos lady house seaworth',
 u'never thought youd find position',
 u'uncle lord commander mormont made man steward',
 u'long boltons hold winterfell north divided',
 u'theyre half ferocious lady boltons doomed',
 u'stannis camped way winterfell',
 u'experienced commander westeros',
 u'wildlings',
 u'we

In [280]:
Davos_Words_String = ' '.join(Davos_Words)
Davos_Words_String

u'help get inside cut need help get melisandre os youre ones owe lives jon snow dolorous edd im much hunter ill need food im gonna make south without starving alliser thorne havent seen ive seen cut dead youre thats completely fucking mad seems imagine seems jon snow dont know maybe well never know matter aside starks boltons powerful houses north umbers karstarks manderlys umbers karstarks already declared boltons well beg pardon lady know stark beheaded father precious little lady may well loyal many rose boltons betrayed family dont doubt didnt know tullys still army thats good please lady understand feel davos lady house seaworth never thought youd find position uncle lord commander mormont made man steward long boltons hold winterfell north divided theyre half ferocious lady boltons doomed stannis camped way winterfell experienced commander westeros wildlings wed hoped fucks sake friends worth fighting thisll hold thats way crucial let charge us get sleep wasnt boltons defeated st

In [281]:
Davos_String_Length = len(Davos_Words_String)
Davos_String_Length

1234

In [282]:
Davos_Sentiment = TextBlob(Davos_Words_String).sentiment
Davos_Sentiment

Sentiment(polarity=0.0673611111111111, subjectivity=0.6229166666666667)

### Gilly

In [283]:
Gilly = season_six.loc['Gilly']
print Gilly

0                                                           0
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
0_two                                                       0
1_two                                                       0
2_two                                                       0
3_two                                                       0
0           wont long well south soon im excited see oldto...
1                                        going oldtown taking
2                                                           0
3                                                           0
0_four                                                      0
1_four                                                      0
2_four  

In [284]:
Gilly_Text = Gilly.values.tolist()
Gilly_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'wont long well south soon im excited see oldtown captain says beautiful city westeros going vomit',
 u'going oldtown taking',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'green',
 u'youre nervous',
 u'thats better nervous mute',
 u'little sam baby',
 u'tell family',
 u'tell far north',
 u'didnt tell im really',
 u'think',
 u'happy know lady tarly',
 u'yes course',
 u'hard walk',
 u'wield sword',
 u'saw eyes way castle black',
 u'nights watch came keep',
 u'north wall',
 u'im angry',
 u'youre thinks sam',
 u'sam',
 '',
 u'dont things',
 '',
 u'sisters dress',
 u'sam',
 u'sam',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',


In [285]:
Gilly_Words = []

for word in Gilly_Text:
    if len(word)>=1:
        if word != '0':
            Gilly_Words.append(word)
        
Gilly_Words 

[u'wont long well south soon im excited see oldtown captain says beautiful city westeros going vomit',
 u'going oldtown taking',
 u'green',
 u'youre nervous',
 u'thats better nervous mute',
 u'little sam baby',
 u'tell family',
 u'tell far north',
 u'didnt tell im really',
 u'think',
 u'happy know lady tarly',
 u'yes course',
 u'hard walk',
 u'wield sword',
 u'saw eyes way castle black',
 u'nights watch came keep',
 u'north wall',
 u'im angry',
 u'youre thinks sam',
 u'sam',
 u'dont things',
 u'sisters dress',
 u'sam',
 u'sam']

In [286]:
Gilly_Words_String = ' '.join(Gilly_Words)
Gilly_Words_String

u'wont long well south soon im excited see oldtown captain says beautiful city westeros going vomit going oldtown taking green youre nervous thats better nervous mute little sam baby tell family tell far north didnt tell im really think happy know lady tarly yes course hard walk wield sword saw eyes way castle black nights watch came keep north wall im angry youre thinks sam sam dont things sisters dress sam sam'

In [287]:
Gilly_String_Length = len(Gilly_Words_String)
Gilly_String_Length

413

In [288]:
Gilly_Sentiment = TextBlob(Gilly_Words_String).sentiment
Gilly_Sentiment

Sentiment(polarity=0.11909722222222224, subjectivity=0.6354166666666666)

### Jaime Lannister

In [289]:
Jaime = season_six.loc['Jaime']
print Jaime

0                                               mother cersei
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
0_two                                   fail sometimes tommen
1_two                  go see mother ask forgive high sparrow
2_two       broke sacred oath stabbed king back killed cou...
3_two       oh gods wont mind theyve spilled blood rest us...
0           women murdered myrcella overthrown house marte...
1                                                           0
2                                                           0
3                                                           0
0_four                                     cersei mother king
1_four                                      youll take action
2_four  

In [290]:
Jaime_Text = Jaime.values.tolist()
Jaime_Text

[u'mother cersei',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'fail sometimes tommen',
 u'go see mother ask forgive high sparrow',
 u'broke sacred oath stabbed king back killed cousin gods judged brother guilty helped escape justice atonement deserve',
 u'oh gods wont mind theyve spilled blood rest us combined high sparrow',
 u'women murdered myrcella overthrown house martell taken control dorne weve got lot discuss us together cersei',
 '0',
 '0',
 '0',
 u'cersei mother king',
 u'youll take action',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'lord',
 u'sorry interrupt',
 u'speak king tommen house baratheon first name',
 u'already insulted one great house',
 u'ive member kingsguard since born',
 u'youre sitting chair',
 u'walking naked streets',
 u'im sent deal blackfish',
 u'im going riverlands

In [291]:
Jaime_Words = []

for word in Jaime_Text:
    if len(word)>=1:
        if word != '0':
            Jaime_Words.append(word)
        
Jaime_Words 

[u'mother cersei',
 u'fail sometimes tommen',
 u'go see mother ask forgive high sparrow',
 u'broke sacred oath stabbed king back killed cousin gods judged brother guilty helped escape justice atonement deserve',
 u'oh gods wont mind theyve spilled blood rest us combined high sparrow',
 u'women murdered myrcella overthrown house martell taken control dorne weve got lot discuss us together cersei',
 u'cersei mother king',
 u'youll take action',
 u'lord',
 u'sorry interrupt',
 u'speak king tommen house baratheon first name',
 u'already insulted one great house',
 u'ive member kingsguard since born',
 u'youre sitting chair',
 u'walking naked streets',
 u'im sent deal blackfish',
 u'im going riverlands',
 u'im going give bronn largest bag gold anyones ever seen gather best killers knows',
 u'son',
 u'youll stand trial soon',
 u'someone certainly',
 u'youre anointed knight',
 u'better instincts officer lannister army',
 u'expect command lannister forces long',
 u'youll get three',
 u'lothar'

In [292]:
Jaime_Words_String = ' '.join(Jaime_Words)
Jaime_Words_String

u'mother cersei fail sometimes tommen go see mother ask forgive high sparrow broke sacred oath stabbed king back killed cousin gods judged brother guilty helped escape justice atonement deserve oh gods wont mind theyve spilled blood rest us combined high sparrow women murdered myrcella overthrown house martell taken control dorne weve got lot discuss us together cersei cersei mother king youll take action lord sorry interrupt speak king tommen house baratheon first name already insulted one great house ive member kingsguard since born youre sitting chair walking naked streets im sent deal blackfish im going riverlands im going give bronn largest bag gold anyones ever seen gather best killers knows son youll stand trial soon someone certainly youre anointed knight better instincts officer lannister army expect command lannister forces long youll get three lothar cause didnt set proper perimeter lord edmure bathed fed fool makes threats hes prepared carry siege command get word blackfish

In [293]:
Jaime_String_Length = len(Jaime_Words_String)
Jaime_String_Length

1999

In [294]:
Jaime_Sentiment = TextBlob(Jaime_Words_String).sentiment
Jaime_Sentiment

Sentiment(polarity=0.15543062200956936, subjectivity=0.5173517126148706)

### Jon Snow

In [295]:
Jon = season_six.loc['Jon Snow']
print Jon

0                                                           0
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
0_two                                                       0
1_two                                                       0
2_two                                                       0
3_two                                                       0
0               stabbed ollyhe put knife heart shouldnt davos
1                        think hold burning body dolorous edd
2                wear burn whatever want castle black credits
3                                                           0
0_four                                     south dolorous edd
1_four                                  get warm dolorous edd
2_four  

In [296]:
Jon_Text = Jon.values.tolist()
Jon_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'stabbed ollyhe put knife heart shouldnt davos',
 u'think hold burning body dolorous edd',
 u'wear burn whatever want castle black credits',
 '0',
 u'south dolorous edd',
 u'get warm dolorous edd',
 u'everything could know dolorous edd',
 u'peas onions',
 u'theres nothing forgive sansa',
 u'go',
 u'cant stay happened sansa',
 u'didnt come serve sansa',
 u'sansa sansa',
 u'im lord commander anymore',
 '',
 u'lord winterfell warden north',
 u'dont know',
 u'cant defend north walkers south boltons',
 u'three houses north glover mormont cerwyn mazin hornwood',
 u'know',
 u'year like wolf bit',
 u'thank sansa',
 u'dont knock im gone',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',


In [297]:
Jon_Words = []

for word in Jon_Text:
    if len(word)>=1:
        if word != '0':
            Jon_Words.append(word)
        
Jon_Words 

[u'stabbed ollyhe put knife heart shouldnt davos',
 u'think hold burning body dolorous edd',
 u'wear burn whatever want castle black credits',
 u'south dolorous edd',
 u'get warm dolorous edd',
 u'everything could know dolorous edd',
 u'peas onions',
 u'theres nothing forgive sansa',
 u'go',
 u'cant stay happened sansa',
 u'didnt come serve sansa',
 u'sansa sansa',
 u'im lord commander anymore',
 u'lord winterfell warden north',
 u'dont know',
 u'cant defend north walkers south boltons',
 u'three houses north glover mormont cerwyn mazin hornwood',
 u'know',
 u'year like wolf bit',
 u'thank sansa',
 u'dont knock im gone',
 u'thats whatll happen lose',
 u'served uncle castle black lady lyanna',
 u'stannis baratheon garrisoned castle black marched winterfell killed',
 u'ramsay bolton cannot allowed keep winterfell lady',
 u'uncle fought fist first men',
 u'thank lady',
 u'lord glover could hear us',
 u'boltons traitors',
 u'house mormont',
 u'sent raven houses manderly robett',
 u'bulk fo

In [298]:
Jon_Words_String = ' '.join(Jon_Words)
Jon_Words_String

u'stabbed ollyhe put knife heart shouldnt davos think hold burning body dolorous edd wear burn whatever want castle black credits south dolorous edd get warm dolorous edd everything could know dolorous edd peas onions theres nothing forgive sansa go cant stay happened sansa didnt come serve sansa sansa sansa im lord commander anymore lord winterfell warden north dont know cant defend north walkers south boltons three houses north glover mormont cerwyn mazin hornwood know year like wolf bit thank sansa dont knock im gone thats whatll happen lose served uncle castle black lady lyanna stannis baratheon garrisoned castle black marched winterfell killed ramsay bolton cannot allowed keep winterfell lady uncle fought fist first men thank lady lord glover could hear us boltons traitors house mormont sent raven houses manderly robett bulk force made wildlings lord glover staying long march winterfell still ser davos reason im standing talking served stannis years theres time dont youre right ay

In [299]:
Jon_String_Length = len(Jon_Words_String)
Jon_String_Length

1603

In [300]:
Jon_Sentiment = TextBlob(Jon_Words_String).sentiment
Jon_Sentiment

Sentiment(polarity=0.18095238095238095, subjectivity=0.4542162698412699)

### Jorah Mormont

In [301]:
Jorah = season_six.loc['Jorah']
print Jorah

0                                                  ram daario
1               dont know anything else melt rams horn daario
2                                                 know daario
3                                               course daario
4                                           army horde daario
5                                                  bloodrider
0_two                                                       0
1_two                                                       0
2_two                                                       0
3_two                                                       0
0                                                           0
1                                                           0
2                                                           0
3                                                           0
0_four                                         im fine daario
1_four             forbidden carry weapons sacred city daario
2_four  

In [302]:
Jorah_Text = Jorah.values.tolist()
Jorah_Text

[u'ram daario',
 u'dont know anything else melt rams horn daario',
 u'know daario',
 u'course daario',
 u'army horde daario',
 u'bloodrider',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'im fine daario',
 u'forbidden carry weapons sacred city daario',
 u'spot us unarmed well say traders heading western market see weapons daario',
 u'know happens daario',
 u'wine come stall tomorrow ill give cask arbors finest dothraki',
 u'find body stab wound whole city looking us daario',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'must send away',
 u'dont know',
 u'dont know either',
 u'dont',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0'

In [303]:
Jorah_Words = []

for word in Jorah_Text:
    if len(word)>=1:
        if word != '0':
            Jorah_Words.append(word)
        
Jorah_Words 

[u'ram daario',
 u'dont know anything else melt rams horn daario',
 u'know daario',
 u'course daario',
 u'army horde daario',
 u'bloodrider',
 u'im fine daario',
 u'forbidden carry weapons sacred city daario',
 u'spot us unarmed well say traders heading western market see weapons daario',
 u'know happens daario',
 u'wine come stall tomorrow ill give cask arbors finest dothraki',
 u'find body stab wound whole city looking us daario',
 u'must send away',
 u'dont know',
 u'dont know either',
 u'dont']

In [304]:
Jorah_Words_String = ' '.join(Jorah_Words)
Jorah_Words_String

u'ram daario dont know anything else melt rams horn daario know daario course daario army horde daario bloodrider im fine daario forbidden carry weapons sacred city daario spot us unarmed well say traders heading western market see weapons daario know happens daario wine come stall tomorrow ill give cask arbors finest dothraki find body stab wound whole city looking us daario must send away dont know dont know either dont'

In [305]:
Jorah_String_Length = len(Jorah_Words_String)
Jorah_String_Length

423

In [306]:
Jorah_Sentiment = TextBlob(Jorah_Words_String).sentiment
Jorah_Sentiment

Sentiment(polarity=0.029166666666666674, subjectivity=0.475)

### Petyr Baelish/Littlefinger

In [307]:
Littlefinger = season_six.loc['Littlefinger']
Petyr = season_six.loc['Petyr']

In [308]:
Littlefinger_Text = Littlefinger.values.tolist()
Petyr_Text = Petyr.values.tolist()

In [309]:
Littlefinger_Words = []

for word in Littlefinger_Text:
    if len(word)>=1:
        if word != '0':
            Littlefinger_Words.append(word)

for word in Petyr_Text:
    if len(word)>=1:
        if word != '0':
            Littlefinger_Words.append(word)            
            
Littlefinger_Words 

[u'lord come see littlefinger',
 u'indeed yohn royce',
 u'tell lord royce many people knew travel plans sansa stark',
 u'lord royce served vale well hes enjoyed distinguished military career could trust absolute loyalty would make capable commander wars come yohn royce',
 u'rode north knights vale come aid',
 u'cant begin contemplate sansa',
 u'beat',
 u'sansa sansa',
 u'cut',
 u'didnt know',
 u'made mistake horrible mistake',
 u'im sorry',
 u'want beg life',
 u'die',
 u'would anything undo whats done',
 u'brothers army',
 u'halfbrother',
 u'child',
 u'thought knew wanted',
 u'werent',
 u'news battle spread quickly seven kingdoms',
 u'past gone good']

In [310]:
Littlefinger_Words_String = ' '.join(Littlefinger_Words)
Littlefinger_Words_String

u'lord come see littlefinger indeed yohn royce tell lord royce many people knew travel plans sansa stark lord royce served vale well hes enjoyed distinguished military career could trust absolute loyalty would make capable commander wars come yohn royce rode north knights vale come aid cant begin contemplate sansa beat sansa sansa cut didnt know made mistake horrible mistake im sorry want beg life die would anything undo whats done brothers army halfbrother child thought knew wanted werent news battle spread quickly seven kingdoms past gone good'

In [311]:
Littlefinger_String_Length = len(Littlefinger_Words_String)
Littlefinger_String_Length

549

In [312]:
Littlefinger_Sentiment = TextBlob(Littlefinger_Words_String).sentiment
Littlefinger_Sentiment

Sentiment(polarity=0.03484848484848485, subjectivity=0.5954545454545456)

### Margaery Tyrell

In [313]:
Margaery = season_six.loc['Margaery']
print Margaery

0                                    none us high sparrow
1                                                       0
2                                                       0
3                                                       0
4                                                       0
5                                                       0
0_two                                                   0
1_two                                                   0
2_two                                                   0
3_two                                                   0
0                                                       0
1                                                       0
2                                                       0
3                                                       0
0_four          id go brother husband family high sparrow
1_four                                             listen
2_four                                             strong
3_four        

In [314]:
Margaery_Text = Margaery.values.tolist()
Margaery_Text

[u'none us high sparrow',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'id go brother husband family high sparrow',
 u'listen',
 u'strong',
 u'shh',
 u'want help',
 u'right',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'grace',
 u'well together soon everything better',
 u'spoken high sparrow',
 u'yes',
 u'think im mad',
 u'ah yes visited hovels fed soup made sure seen',
 u'right',
 u'love brother',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'book mother holiness',
 u'year pretended love poor afflicted',
 u'course',
 '',
 u'justthe desires drove longer',
 u'forgive',
 u'grandmother',
 u'septa unella true friend counselor',
 u'grandmother please',
 u'marched high sparrow fait

In [315]:
Margaery_Words = []

for word in Margaery_Text:
    if len(word)>=1:
        if word != '0':
            Margaery_Words.append(word)
        
Margaery_Words 

[u'none us high sparrow',
 u'id go brother husband family high sparrow',
 u'listen',
 u'strong',
 u'shh',
 u'want help',
 u'right',
 u'grace',
 u'well together soon everything better',
 u'spoken high sparrow',
 u'yes',
 u'think im mad',
 u'ah yes visited hovels fed soup made sure seen',
 u'right',
 u'love brother',
 u'book mother holiness',
 u'year pretended love poor afflicted',
 u'course',
 u'justthe desires drove longer',
 u'forgive',
 u'grandmother',
 u'septa unella true friend counselor',
 u'grandmother please',
 u'marched high sparrow faith',
 u'gods could punished father didnt',
 u'lorass hope confess crimes repent',
 u'live life penitent',
 u'begin',
 u'free man',
 u'queen',
 u'leave grandmother',
 u'must',
 u'go home',
 u'mother watches us',
 u'seven blessings grandmother',
 u'shall pray',
 u'queen mother',
 u'cersei',
 u'loras',
 u'let us']

In [316]:
Margaery_Words_String = ' '.join(Margaery_Words)
Margaery_Words_String

u'none us high sparrow id go brother husband family high sparrow listen strong shh want help right grace well together soon everything better spoken high sparrow yes think im mad ah yes visited hovels fed soup made sure seen right love brother book mother holiness year pretended love poor afflicted course justthe desires drove longer forgive grandmother septa unella true friend counselor grandmother please marched high sparrow faith gods could punished father didnt lorass hope confess crimes repent live life penitent begin free man queen leave grandmother must go home mother watches us seven blessings grandmother shall pray queen mother cersei loras let us'

In [317]:
Margaery_String_Length = len(Margaery_Words_String)
Margaery_String_Length

662

In [318]:
Margaery_Sentiment = TextBlob(Margaery_Words_String).sentiment
Margaery_Sentiment

Sentiment(polarity=0.21913284632034633, subjectivity=0.6314781746031745)

### Melisandre

In [319]:
Melisandre = season_six.loc['Melisandre']
print Melisandre

0                                                           0
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
0_two                                            asking davos
1_two                                   want help leave davos
2_two                                                       0
3_two                                                       0
0           lord let come back reason stannis prince promi...
1                                                           0
2                                                           0
3                                                           0
0_four                                jon snow commands davos
1_four                              hes prince promised davos
2_four  

In [320]:
Melisandre_Text = Melisandre.values.tolist()
Melisandre_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'asking davos',
 u'want help leave davos',
 '0',
 '0',
 u'lord let come back reason stannis prince promised someone davos melisandre',
 '0',
 '0',
 '0',
 u'jon snow commands davos',
 u'hes prince promised davos',
 u'battle stannis defeated davos',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',


In [321]:
Melisandre_Words = []

for word in Melisandre_Text:
    if len(word)>=1:
        if word != '0':
            Melisandre_Words.append(word)
        
Melisandre_Words 

[u'asking davos',
 u'want help leave davos',
 u'lord let come back reason stannis prince promised someone davos melisandre',
 u'jon snow commands davos',
 u'hes prince promised davos',
 u'battle stannis defeated davos',
 u'im soldier',
 u'dont lose',
 u'ill try',
 u'servant jon snow',
 u'serve lord light',
 u'interpret signs well',
 u'dont know',
 u'one weve got',
 u'could worse jon snow',
 u'princess shireen',
 u'burned stake',
 u'army trapped',
 u'lord commands',
 u'standing',
 u'father',
 u'didnt lie',
 u'ive ready die many years']

In [322]:
Melisandre_Words_String = ' '.join(Melisandre_Words)
Melisandre_Words_String

u'asking davos want help leave davos lord let come back reason stannis prince promised someone davos melisandre jon snow commands davos hes prince promised davos battle stannis defeated davos im soldier dont lose ill try servant jon snow serve lord light interpret signs well dont know one weve got could worse jon snow princess shireen burned stake army trapped lord commands standing father didnt lie ive ready die many years'

In [323]:
Melisandre_String_Length = len(Melisandre_Words_String)
Melisandre_String_Length

425

In [324]:
Melisandre_Sentiment = TextBlob(Melisandre_Words_String).sentiment
Melisandre_Sentiment

Sentiment(polarity=7.93016446160826e-18, subjectivity=0.4714285714285714)

### Missandei

In [325]:
Missandei = season_six.loc['Missandei']
print Missandei

0                                                           0
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
0_two                                       many times tyrion
1_two                                            never tyrion
2_two                                                       0
3_two                                                       0
0           cannot masters speak one language spoke many y...
1                                                           0
2                                                           0
3                                                           0
0_four                                                      0
1_four                                                      0
2_four  

In [326]:
type(Missandei)

pandas.core.series.Series

In [327]:
Missandei_Text = Missandei.values.tolist()
Missandei_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'many times tyrion',
 u'never tyrion',
 '0',
 '0',
 u'cannot masters speak one language spoke many years know better mother tongue want hear us must speak back may last thing ever hear tyrion',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'people know brought freedom',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'seem happy',
 u'happy queen returns',
 u'tried wine',
 u'know jokes',
 u'joke like s

In [328]:
Missandei_Words = []

for word in Missandei_Text:
    if len(word)>=1:
        if word != '0':
            Missandei_Words.append(word)
        
Missandei_Words 

[u'many times tyrion',
 u'never tyrion',
 u'cannot masters speak one language spoke many years know better mother tongue want hear us must speak back may last thing ever hear tyrion',
 u'people know brought freedom',
 u'seem happy',
 u'happy queen returns',
 u'tried wine',
 u'know jokes',
 u'joke like story torgo nudho',
 u'two translators sinking ship',
 u'first says know swim second says shout help languages tyrion ah',
 u'dont even know joke',
 u'jokes',
 u'changes nothing',
 u'queen insists one must die punishment crimes']

In [329]:
Missandei_Words_String = ' '.join(Missandei_Words)
Missandei_Words_String

u'many times tyrion never tyrion cannot masters speak one language spoke many years know better mother tongue want hear us must speak back may last thing ever hear tyrion people know brought freedom seem happy happy queen returns tried wine know jokes joke like story torgo nudho two translators sinking ship first says know swim second says shout help languages tyrion ah dont even know joke jokes changes nothing queen insists one must die punishment crimes'

In [330]:
Missandei_String_Length = len(Missandei_Words_String)
Missandei_String_Length

457

In [331]:
Missandei_Sentiment = TextBlob(Missandei_Words_String).sentiment
Missandei_Sentiment

Sentiment(polarity=0.3722222222222222, subjectivity=0.43333333333333335)

### Olenna Tyrell

In [332]:
Olenna1 = season_six.loc['Lady Olenna']
Olenna2 = season_six.loc['Olenna']

In [333]:
Olenna_Text1 = Olenna1.values.tolist()
Olenna_Text2 = Olenna2.values.tolist()

In [334]:
Olenna_Words = []

for word in Olenna_Text1:
    if len(word)>=1:
        if word != '0':
            Olenna_Words.append(word)

for word in Olenna_Text2:
    if len(word)>=1:
        if word != '0':
            Olenna_Words.append(word)            
            
Olenna_Words 

[u'would thought perfectly clear first time',
 u'dear stripped dignity authority publicly shamed confined red keep',
 u'oh',
 u'many die matter',
 u'hes beaten us',
 u'oh madness',
 u'tell stop',
 u'done',
 u'marched',
 u'brother',
 u'heir highgarden future house tyrell',
 u'mindless fanatic',
 u'leave highgarden today',
 u'never leave',
 u'ill see soon dear',
 u'hardly concern',
 u'loras rots cell',
 u'good',
 u'wonder youre worst person ive ever met',
 u'im leaving wretched city fast shoeless zealot throws one cells',
 u'whatll',
 u'last time tyrell came dorne assassinated',
 u'murder prince expect trust',
 u'name',
 u'obara',
 u'anything',
 u'cersei stole future',
 u'hearts desire']

In [335]:
Olenna_Words_String = ' '.join(Olenna_Words)
Olenna_Words_String

u'would thought perfectly clear first time dear stripped dignity authority publicly shamed confined red keep oh many die matter hes beaten us oh madness tell stop done marched brother heir highgarden future house tyrell mindless fanatic leave highgarden today never leave ill see soon dear hardly concern loras rots cell good wonder youre worst person ive ever met im leaving wretched city fast shoeless zealot throws one cells whatll last time tyrell came dorne assassinated murder prince expect trust name obara anything cersei stole future hearts desire'

In [336]:
Olenna_String_Length = len(Olenna_Words_String)
Olenna_String_Length

554

In [337]:
Olenna_Sentiment = TextBlob(Olenna_Words_String).sentiment
Olenna_Sentiment

Sentiment(polarity=-0.0361111111111111, subjectivity=0.4694444444444444)

### Ramsay Bolton

In [338]:
Ramsay = season_six.loc['Ramsay']
print Ramsay

0                               pain paid thousand times
1                                          buried burned
2                              good meat feed hounds cut
3                                                  roose
4                                                  roose
5                                                      0
0_two                               obviously help roose
1_two                    course follow mother lady walda
2_two                             lord bolton lady walda
3_two                                                  0
0                           appears bit impasse smalljon
1                            welcome home lord stark int
2                                                      0
3                                                      0
0_four                                               yes
1_four                                             worry
2_four                                                  
3_four                         

In [339]:
Ramsay_Text = Ramsay.values.tolist()
Ramsay_Text

[u'pain paid thousand times',
 u'buried burned',
 u'good meat feed hounds cut',
 u'roose',
 u'roose',
 '0',
 u'obviously help roose',
 u'course follow mother lady walda',
 u'lord bolton lady walda',
 '0',
 u'appears bit impasse smalljon',
 u'welcome home lord stark int',
 '0',
 '0',
 u'yes',
 u'worry',
 '',
 u'served starks',
 u'starks gone long time kept protecting rickon',
 u'may rickons sell anymore',
 u'sure know',
 u'youre good talker',
 u'like',
 u'youre much better talker theon greyjoy',
 u'work hard get talking',
 u'told everything',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '

In [340]:
Ramsay_Words = []

for word in Ramsay_Text:
    if len(word)>=1:
        if word != '0':
            Ramsay_Words.append(word)
        
Ramsay_Words 

[u'pain paid thousand times',
 u'buried burned',
 u'good meat feed hounds cut',
 u'roose',
 u'roose',
 u'obviously help roose',
 u'course follow mother lady walda',
 u'lord bolton lady walda',
 u'appears bit impasse smalljon',
 u'welcome home lord stark int',
 u'yes',
 u'worry',
 u'served starks',
 u'starks gone long time kept protecting rickon',
 u'may rickons sell anymore',
 u'sure know',
 u'youre good talker',
 u'like',
 u'youre much better talker theon greyjoy',
 u'work hard get talking',
 u'told everything',
 u'beloved wife',
 u'thank returning lady bolton safely',
 u'keep hearing stories bastard',
 u'hes good',
 u'want save sansa',
 u'like games little man',
 u'run remember',
 u'loose',
 u'time go',
 u'winterfell',
 u'ive reconsidered',
 u'hounds never harm',
 u'theyre loyal beasts',
 u'sit']

In [341]:
Ramsay_Words_String = ' '.join(Ramsay_Words)
Ramsay_Words_String

u'pain paid thousand times buried burned good meat feed hounds cut roose roose obviously help roose course follow mother lady walda lord bolton lady walda appears bit impasse smalljon welcome home lord stark int yes worry served starks starks gone long time kept protecting rickon may rickons sell anymore sure know youre good talker like youre much better talker theon greyjoy work hard get talking told everything beloved wife thank returning lady bolton safely keep hearing stories bastard hes good want save sansa like games little man run remember loose time go winterfell ive reconsidered hounds never harm theyre loyal beasts sit'

In [342]:
Ramsay_String_Length = len(Ramsay_Words_String)
Ramsay_String_Length

634

In [343]:
Ramsay_Sentiment = TextBlob(Ramsay_Words_String).sentiment
Ramsay_Sentiment

Sentiment(polarity=0.308482905982906, subjectivity=0.6155413105413107)

### Samwell Tarly

In [344]:
Sam1 = season_six.loc['Sam']
Sam2 = season_six.loc['Samwell']

In [345]:
Sam_Text1 = Sam1.values.tolist()
Sam_Text2 = Sam2.values.tolist()

In [346]:
Sam_Words = []

for word in Sam_Text1:
    if len(word)>=1:
        if word != '0':
            Sam_Words.append(word)

for word in Sam_Text2:
    if len(word)>=1:
        if word != '0':
            Sam_Words.append(word)            
            
Sam_Words 

[u'oh yes',
 u'didnt think id ever come back father made renounce title inheritance well threaten kill didnt',
 u'certainly didnt expect introducing family',
 u'yes thats important',
 u'told met north',
 u'well wasnt large piece parchment',
 u'thing ismy father doesnt like wildlings',
 u'oh hello mother',
 u'oh',
 u'talla',
 u'oh um mother gilly',
 u'oh son samwell',
 u'father',
 u'beautiful',
 u'oh course',
 u'oh thats fair distance',
 u'oh yes',
 u'rabbits',
 u'oh yes',
 u'travelled south orders lord commander',
 u'yes',
 u'gilly',
 u'first light',
 u'say goodbye',
 u'goodbye gilly',
 u'leaving',
 u'get things',
 u'belong together',
 u'oh theyll understand',
 u'wont mind',
 u'familys sword',
 u'bloody well try',
 u'lord commander snow castle black',
 u'im im new maester',
 u'died',
 u'maester aemon became quite ill shortly election',
 u'yes well suppose life irregular',
 u'yes yes im fine gilly',
 u'dont think gilly',
 u'citadel doesnt admit women wont place little sam gilly',
 u'hom

In [347]:
Sam_Words_String = ' '.join(Sam_Words)
Sam_Words_String

u'oh yes didnt think id ever come back father made renounce title inheritance well threaten kill didnt certainly didnt expect introducing family yes thats important told met north well wasnt large piece parchment thing ismy father doesnt like wildlings oh hello mother oh talla oh um mother gilly oh son samwell father beautiful oh course oh thats fair distance oh yes rabbits oh yes travelled south orders lord commander yes gilly first light say goodbye goodbye gilly leaving get things belong together oh theyll understand wont mind familys sword bloody well try lord commander snow castle black im im new maester died maester aemon became quite ill shortly election yes well suppose life irregular yes yes im fine gilly dont think gilly citadel doesnt admit women wont place little sam gilly home horn hill fathers well father mothers kind woman sisters lovely theyll take care gilly'

In [348]:
Sam_String_Length = len(Sam_Words_String)
Sam_String_Length

885

In [349]:
Sam_Sentiment = TextBlob(Sam_Words_String).sentiment
Sam_Sentiment

Sentiment(polarity=0.1780844155844156, subjectivity=0.6277183600713013)

### Sansa Stark

In [350]:
Sansa = season_six.loc['Sansa']
print Sansa

0                                                           0
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
0_two                                                      go
1_two                                                       0
2_two                                                       0
3_two                                                       0
0                                                           0
1                                                           0
2                                                           0
3                                                           0
0_four                                           mmm jon snow
1_four      spent lot time thinking ass wish could change ...
2_four  

In [351]:
Sansa_Text = Sansa.values.tolist()
Sansa_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'go',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'mmm jon snow',
 u'spent lot time thinking ass wish could change everything jon snow',
 u'well take back jon snow',
 u'thats right',
 u'go',
 u'watch soldiers take turns raping sister',
 u'fathers dead',
 u'yes',
 u'heard say talking stanniss attack',
 u'monster taken home brother',
 '0',
 '0',
 '0',
 u'far moles town',
 u'unharmed',
 u'come aid',
 u'would like hear wedding night',
 u'yes enjoyed',
 u'maybe know ramsay along',
 u'thought knew everyones secrets',
 u'things ladies arent supposed talk things imagine brothel keepers talk time',
 u'said would protect',
 u'dont believe anymore',
 u'want die',
 u'freed monsters murdered family gave monsters murdered family',
 u'army',
 u'umbers gave rickon enemies',
 u'well know north ser davos',
 u'father always said northerners different',
 u'north remembers',
 '',
 u'jon every bit much ned starks son ramsay roose boltons',
 u'uncle blackfish reformed re

In [352]:
Sansa_Words = []

for word in Sansa_Text:
    if len(word)>=1:
        if word != '0':
            Sansa_Words.append(word)
        
Sansa_Words 

[u'go',
 u'mmm jon snow',
 u'spent lot time thinking ass wish could change everything jon snow',
 u'well take back jon snow',
 u'thats right',
 u'go',
 u'watch soldiers take turns raping sister',
 u'fathers dead',
 u'yes',
 u'heard say talking stanniss attack',
 u'monster taken home brother',
 u'far moles town',
 u'unharmed',
 u'come aid',
 u'would like hear wedding night',
 u'yes enjoyed',
 u'maybe know ramsay along',
 u'thought knew everyones secrets',
 u'things ladies arent supposed talk things imagine brothel keepers talk time',
 u'said would protect',
 u'dont believe anymore',
 u'want die',
 u'freed monsters murdered family gave monsters murdered family',
 u'army',
 u'umbers gave rickon enemies',
 u'well know north ser davos',
 u'father always said northerners different',
 u'north remembers',
 u'jon every bit much ned starks son ramsay roose boltons',
 u'uncle blackfish reformed retaken riverrun',
 u'ramsay received raven escaped winterfell',
 u'heard',
 u'cant risk ramsay interce

In [353]:
Sansa_Words_String = ' '.join(Sansa_Words)
Sansa_Words_String

u'go mmm jon snow spent lot time thinking ass wish could change everything jon snow well take back jon snow thats right go watch soldiers take turns raping sister fathers dead yes heard say talking stanniss attack monster taken home brother far moles town unharmed come aid would like hear wedding night yes enjoyed maybe know ramsay along thought knew everyones secrets things ladies arent supposed talk things imagine brothel keepers talk time said would protect dont believe anymore want die freed monsters murdered family gave monsters murdered family army umbers gave rickon enemies well know north ser davos father always said northerners different north remembers jon every bit much ned starks son ramsay roose boltons uncle blackfish reformed retaken riverrun ramsay received raven escaped winterfell heard cant risk ramsay intercepting ride riverrun jon made good made made like one father used wear youre welcome remember born lady survive lady would remind house glover pledged house stark

In [354]:
Sansa_String_Length = len(Sansa_Words_String)
Sansa_String_Length

1706

In [355]:
Sansa_Sentiment = TextBlob(Sansa_Words_String).sentiment
Sansa_Sentiment

Sentiment(polarity=0.07939560439560439, subjectivity=0.49807692307692303)

### Theon Greyjoy

In [356]:
Theon = season_six.loc['Theon']
print Theon

0                                  dead bolton officer
1                                                    0
2                                                    0
3                                                    0
4                                                    0
5                                                    0
0_two        would taken way wall would died get theon
1_two                                         home ext
2_two                                                0
3_two                                                0
0                                                    0
1                                                    0
2                                                    0
3                                                    0
0_four                                         escaped
1_four                                         escaped
2_four                                        im sorry
3_four                                            know
4_four    

In [357]:
Theon_Text = Theon.values.tolist()
Theon_Text

[u'dead bolton officer',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'would taken way wall would died get theon',
 u'home ext',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'escaped',
 u'escaped',
 u'im sorry',
 u'know',
 u'broke',
 u'dont know',
 u'else could go',
 '',
 u'didnt know',
 u'dont want king',
 u'shouldve listened',
 u'rule iron islands',
 '0',
 u'theon greyjoylast living son balon greyjoy',
 u'rightful ruler',
 u'reaver',
 u'warrior',
 u'ironborn',
 u'find better leader',
 u'would hard',
 u'gone',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'dont want one',
 u'think uncle eurons hunting us',
 u'hell find us',
 u'dont want',
 u'bad years',
 u'got justice burnt body would hang gates winterfell',
 '0',
 '0',
 '0',
 '0

In [358]:
Theon_Words = []

for word in Theon_Text:
    if len(word)>=1:
        if word != '0':
            Theon_Words.append(word)
        
Theon_Words 

[u'dead bolton officer',
 u'would taken way wall would died get theon',
 u'home ext',
 u'escaped',
 u'escaped',
 u'im sorry',
 u'know',
 u'broke',
 u'dont know',
 u'else could go',
 u'didnt know',
 u'dont want king',
 u'shouldve listened',
 u'rule iron islands',
 u'theon greyjoylast living son balon greyjoy',
 u'rightful ruler',
 u'reaver',
 u'warrior',
 u'ironborn',
 u'find better leader',
 u'would hard',
 u'gone',
 u'dont want one',
 u'think uncle eurons hunting us',
 u'hell find us',
 u'dont want',
 u'bad years',
 u'got justice burnt body would hang gates winterfell',
 u'long time ago',
 u'didnt murder stark boys',
 u'claim',
 u'im fit rule',
 u'uncle euron returned home long absence',
 u'euron building',
 u'iron fleet isnt hes bringing',
 u'murdered father would murdered us',
 u'ancestors defeated took iron islands']

In [359]:
Theon_Words_String = ' '.join(Theon_Words)
Theon_Words_String

u'dead bolton officer would taken way wall would died get theon home ext escaped escaped im sorry know broke dont know else could go didnt know dont want king shouldve listened rule iron islands theon greyjoylast living son balon greyjoy rightful ruler reaver warrior ironborn find better leader would hard gone dont want one think uncle eurons hunting us hell find us dont want bad years got justice burnt body would hang gates winterfell long time ago didnt murder stark boys claim im fit rule uncle euron returned home long absence euron building iron fleet isnt hes bringing murdered father would murdered us ancestors defeated took iron islands'

In [360]:
Theon_String_Length = len(Theon_Words_String)
Theon_String_Length

647

In [361]:
Theon_Sentiment = TextBlob(Theon_Words_String).sentiment
Theon_Sentiment

Sentiment(polarity=-0.11041666666666665, subjectivity=0.49083333333333334)

### Tyrion Lannister

In [362]:
Tyrion = season_six.loc['Tyrion']
print Tyrion

0           never going fix whats wrong city top foot pyra...
1                  hard know queen popular meereen used varys
2           possibly daenerys targaryen took away valuable...
3                                              problem tyrion
4                                                           0
5                                                           0
0_two                        dragons well captivity missandei
1_two                          thats drink know things tyrion
2_two                                         time supper cut
3_two                                                       0
0                   right conversations lets play game tyrion
1                                          possibly missandei
2                                         conversation tyrion
3                                                           0
0_four                                              grey worm
1_four                             long enough know missandei
2_four  

In [363]:
Tyrion_Text = Tyrion.values.tolist()
Tyrion_Text

[u'never going fix whats wrong city top foot pyramid tyrion',
 u'hard know queen popular meereen used varys',
 u'possibly daenerys targaryen took away valuable property told human beings werent even property begin see theyre unhappy course could also freed men listeners speaking valyrian',
 u'problem tyrion',
 '0',
 '0',
 u'dragons well captivity missandei',
 u'thats drink know things tyrion',
 u'time supper cut',
 '0',
 u'right conversations lets play game tyrion',
 u'possibly missandei',
 u'conversation tyrion',
 '0',
 u'grey worm',
 u'long enough know missandei',
 u'instead abolishing slavery overnight give seven years end practice tyrion',
 u'queen chose advisor returns travels man',
 u'soon word man',
 u'offered terms man speaking valyrian',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'enough',
 u'enough meereen peace',
 u'yes know brought security',
 u'said anything',
 u'thats extent valyrian',
 u'thank travelling way',
 u'truth need help',
 u'yes',
 u'indeed',
 u'ideally wed avo

In [364]:
Tyrion_Words = []

for word in Tyrion_Text:
    if len(word)>=1:
        if word != '0':
            Tyrion_Words.append(word)
        
Tyrion_Words 

[u'never going fix whats wrong city top foot pyramid tyrion',
 u'hard know queen popular meereen used varys',
 u'possibly daenerys targaryen took away valuable property told human beings werent even property begin see theyre unhappy course could also freed men listeners speaking valyrian',
 u'problem tyrion',
 u'dragons well captivity missandei',
 u'thats drink know things tyrion',
 u'time supper cut',
 u'right conversations lets play game tyrion',
 u'possibly missandei',
 u'conversation tyrion',
 u'grey worm',
 u'long enough know missandei',
 u'instead abolishing slavery overnight give seven years end practice tyrion',
 u'queen chose advisor returns travels man',
 u'soon word man',
 u'offered terms man speaking valyrian',
 u'enough',
 u'enough meereen peace',
 u'yes know brought security',
 u'said anything',
 u'thats extent valyrian',
 u'thank travelling way',
 u'truth need help',
 u'yes',
 u'indeed',
 u'ideally wed avoid purifying many nonbelievers',
 u'id settle obeyed',
 u'sounds e

In [365]:
Tyrion_Words_String = ' '.join(Tyrion_Words)
Tyrion_Words_String

u'never going fix whats wrong city top foot pyramid tyrion hard know queen popular meereen used varys possibly daenerys targaryen took away valuable property told human beings werent even property begin see theyre unhappy course could also freed men listeners speaking valyrian problem tyrion dragons well captivity missandei thats drink know things tyrion time supper cut right conversations lets play game tyrion possibly missandei conversation tyrion grey worm long enough know missandei instead abolishing slavery overnight give seven years end practice tyrion queen chose advisor returns travels man soon word man offered terms man speaking valyrian enough enough meereen peace yes know brought security said anything thats extent valyrian thank travelling way truth need help yes indeed ideally wed avoid purifying many nonbelievers id settle obeyed sounds excellent varys wed grateful support could provide queen friend healthy skepticism religion loyal supporters queen id call successful gam

In [366]:
Tyrion_String_Length = len(Tyrion_Words_String)
Tyrion_String_Length

1979

In [367]:
Tyrion_Sentiment = TextBlob(Tyrion_Words_String).sentiment
Tyrion_Sentiment

Sentiment(polarity=0.15876393110435663, subjectivity=0.54209726443769)

### Varys

In [368]:
Varys = season_six.loc['Varys']
print Varys

0           walk though paving stones personal property us...
1           little birds already taken wing soon theyll re...
2                                                           0
3                                                           0
4                                                           0
5                                                           0
0_two                                                       0
1_two                                                       0
2_two                                                       0
3_two                                                       0
0           thats right know youve done youve done lot you...
1           good masters astapor wise masters yunkai help ...
2                                                           0
3                                                           0
0_four                                                      0
1_four                                                      0
2_four  

In [369]:
Varys_Text = Varys.values.tolist()
Varys_Text

[u'walk though paving stones personal property used steal people like boy tyrion',
 u'little birds already taken wing soon theyll return singing songs men gold masks tyrion',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'thats right know youve done youve done lot youve sacrificed body cause people youve helped sons harpy murder unsullied second sons vala',
 u'good masters astapor wise masters yunkai help friends volantis tyrion',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'many masters butchered free men',
 u'safe say fragile peace taken hold',
 u'best get profession',
 u'considering city brink civil war id say good start',
 u'sounds like quite hero',
 u'suppose hard fanatic admit mistake',
 u'honest servant lord trust know priestess counseled stannis',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '

In [370]:
Varys_Words = []

for word in Varys_Text:
    if len(word)>=1:
        if word != '0':
            Varys_Words.append(word)
        
Varys_Words 

[u'walk though paving stones personal property used steal people like boy tyrion',
 u'little birds already taken wing soon theyll return singing songs men gold masks tyrion',
 u'thats right know youve done youve done lot youve sacrificed body cause people youve helped sons harpy murder unsullied second sons vala',
 u'good masters astapor wise masters yunkai help friends volantis tyrion',
 u'many masters butchered free men',
 u'safe say fragile peace taken hold',
 u'best get profession',
 u'considering city brink civil war id say good start',
 u'sounds like quite hero',
 u'suppose hard fanatic admit mistake',
 u'honest servant lord trust know priestess counseled stannis',
 u'would',
 u'made pact fanatics',
 u'shaved beard straight razor youd say razor worked',
 u'know',
 u'dont return youll know wrong',
 u'need friends westeros',
 u'shell come back',
 u'ill walk rest way',
 u'fire blood']

In [371]:
Varys_Words_String = ' '.join(Varys_Words)
Varys_Words_String

u'walk though paving stones personal property used steal people like boy tyrion little birds already taken wing soon theyll return singing songs men gold masks tyrion thats right know youve done youve done lot youve sacrificed body cause people youve helped sons harpy murder unsullied second sons vala good masters astapor wise masters yunkai help friends volantis tyrion many masters butchered free men safe say fragile peace taken hold best get profession considering city brink civil war id say good start sounds like quite hero suppose hard fanatic admit mistake honest servant lord trust know priestess counseled stannis would made pact fanatics shaved beard straight razor youd say razor worked know dont return youll know wrong need friends westeros shell come back ill walk rest way fire blood'

In [372]:
Varys_String_Length = len(Varys_Words_String)
Varys_String_Length

800

In [373]:
Varys_Sentiment = TextBlob(Varys_Words_String).sentiment
Varys_Sentiment

Sentiment(polarity=0.20034461152882202, subjectivity=0.5567042606516291)

### Yara Greyjoy

In [374]:
Yara = season_six.loc['Yara']
print Yara

0                                                           0
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
0_two                                                       0
1_two                                                       0
2_two                                                       0
3_two                                                       0
0                                                           0
1                                                           0
2                                                           0
3                                                           0
0_four                                              cant hear
1_four                                                   look
2_four  

In [375]:
Yara_Text = Yara.values.tolist()
Yara_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'cant hear',
 u'look',
 u'brother',
 u'stop saying',
 u'know',
 u'send us one pieces',
 u'come',
 u'heard father dead thought youd claim crown',
 u'happen show pyke right kingsmoot',
 u'think ironborn wants king',
 u'want',
 '0',
 '0',
 u'yara greyjoy daughter balon greyjoy king iron islands',
 u'many things weve never done',
 u'sea people',
 u'god sea god',
 u'queen build fleet man',
 u'finished',
 u'return uncle',
 u'im glad youre',
 u'build largest fleet world ever seen',
 u'youre going seduce dragon queen',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'us still like',
 u'dont go far love',
 u'ill find bit',
 u'nothing iron islands as

In [376]:
Yara_Words = []

for word in Yara_Text:
    if len(word)>=1:
        if word != '0':
            Yara_Words.append(word)
        
Yara_Words 

[u'cant hear',
 u'look',
 u'brother',
 u'stop saying',
 u'know',
 u'send us one pieces',
 u'come',
 u'heard father dead thought youd claim crown',
 u'happen show pyke right kingsmoot',
 u'think ironborn wants king',
 u'want',
 u'yara greyjoy daughter balon greyjoy king iron islands',
 u'many things weve never done',
 u'sea people',
 u'god sea god',
 u'queen build fleet man',
 u'finished',
 u'return uncle',
 u'im glad youre',
 u'build largest fleet world ever seen',
 u'youre going seduce dragon queen',
 u'us still like',
 u'dont go far love',
 u'ill find bit',
 u'nothing iron islands ass like',
 u'im sorry',
 u'course',
 u'great big world fast ships',
 u'dont care want',
 u'drink',
 u'youre ironborn theon',
 u'im tired watching cower like beat dog',
 u'listen',
 u'escaped hear',
 u'fuck justice',
 u'listen',
 u'since last night ashore long im gonna go fuck tits one',
 u'paid',
 u'westeros',
 u'common',
 u'never demand im anything really',
 u'wed like help us murder uncle two dont think 

In [378]:
Yara_Words_String = ' '.join(Yara_Words)
Yara_Words_String

u'cant hear look brother stop saying know send us one pieces come heard father dead thought youd claim crown happen show pyke right kingsmoot think ironborn wants king want yara greyjoy daughter balon greyjoy king iron islands many things weve never done sea people god sea god queen build fleet man finished return uncle im glad youre build largest fleet world ever seen youre going seduce dragon queen us still like dont go far love ill find bit nothing iron islands ass like im sorry course great big world fast ships dont care want drink youre ironborn theon im tired watching cower like beat dog listen escaped hear fuck justice listen since last night ashore long im gonna go fuck tits one paid westeros common never demand im anything really wed like help us murder uncle two dont think womans fit rule thats way life'

In [379]:
Yara_String_Length = len(Yara_Words_String)
Yara_String_Length

822

In [380]:
Yara_Sentiment = TextBlob(Yara_Words_String).sentiment
Yara_Sentiment

Sentiment(polarity=0.04678571428571429, subjectivity=0.5526190476190476)